In [5]:
from azasplan import *  #this is the python file than carries the planning algorithm

C:\ProgramData\anaconda3\Lib\site-packages\paramiko\transport.py:219: CryptographyDeprecationWarning: Blowfish has been deprecated
  "class": algorithms.Blowfish,


In [6]:
from enum import Enum
from queue import PriorityQueue
import numpy as np
import math
from skimage.morphology import medial_axis
from skimage.util import invert

In [7]:
!activate fcnd

In [8]:
#UDA DRONE SIMULATOR LIBRARIES
from udacidrone import Drone
from udacidrone.connection import MavlinkConnection
from udacidrone.messaging import MsgID
from udacidrone.frame_utils import global_to_local

In [9]:
#THIS LIBRARY I WILL USE IT TO read and write states messages from drone
import msgpack

In [10]:
from enum import Enum, auto

class States(Enum):
    
    
    """
    this class inherates from enum its proparties, we are intrested to mark each state by a unique id in enum auto() 
    makes this function, so State.Manual for example will be defined by id 1 automatically in all occurances
    """
    Manual= auto()  
    Arming=auto()
    Takeoff=auto()
    InAir= auto()
    landing=auto()
    disarming=auto()
    planning=auto()

In [11]:
import numpy as np
import re
import argparse
import time
import msgpack
from enum import Enum, auto
from udacidrone import Drone
from udacidrone.connection import MavlinkConnection
from udacidrone.messaging import MsgID


In [30]:
import numpy as np
import re
import argparse
import time

class MotionPlanning(Drone):
    
    
    """
    in this class we will set up the environment for Azza to travel safely, 
    this will not happen if we left azza flying without stoping her if any sudden change in state happpens
    That is why you will find in this class, 
    first we call the drone constructor by super().__init__(connection) to intialise various attributes 
    such as 
        goal_position, 
        target_position, 
        waypoints, 
        in_mission, 
        check_state
        set the initial flight_state to States.MANUAL.
        
    it also register callback functions to handle messages like position velocity or states
    
    
    
    then we will define the call back functions, transition, and azaplan functions
    
    
    
    """
    def __init__(self, connection) :
        
        super().__init__(connection)
        self.goal = [0.0, 0.0, 0.0]
        self.goal = np.array([0.0, 0.0, 0.0])
        self.target_pos = np.array([0.0, 0.0, 0.0])
        self.waypoints = []
        self.in_mission = True
        self.check_state = {}
        
        self.flight_state= States.Manual      #initial state
        
        
        #register the call backs to the drone messages
        self.register_callback(MsgID.LOCAL_POSITION, self.azza_position_callback) #azza_posistion_callback returns local position of azza
        self.register_callback(MsgID.LOCAL_VELOCITY, self.azza_velocity_callback) 
        self.register_callback(MsgID.STATE, self.state_callback)
        
        
        
        #NOW WE ARE DONE WITH THE CONSTRUCTOR
        
        
    def azza_position_callback(self): #let's define azza's local position function
        if self.flight_state==States.Takeoff:
            
            """
            in the take off condition we want to go to the next way point 
            as soon as drone reaches the desired altitude, this can't be 
            optimum if we wait for the curr altitude to be sharpely equal 
            desired altitude that is why when it reaches above 95% drone 
            can go for other way poitn
            
            
            the -1 is becasue in local NED frame upwards is negative
            """
            if -1.0 * self.local_position[2]> 0.95*self.target_pos[2]:
                self.inair_transition()
                
                
        elif self.flight_state == States.InAir:
            
            """
            this part we check if we still have way points 
            and 
            the target postion x axis minus local position x axis less than 1 almost equal
            and
            the target postion y axis minus local position y axis less than 1 almost equal
            
            then do a transition
            """
            if np.linalg.norm(self.target_pos[0:2]-self.local_position[0:2]) <1.0:
                if len(self.waypoints)>0:
                    self.inair_transition()
                else:
                    if np.linalg.norm(self.local_velocity[0:2])< 1.0:
                        self.landing_transition()
                        
                        
    def azza_velocity_callback(self):
        
        if self.flight_state == States.landing:
            
            if self.global_position[2] - self.global_home[2] <0.1:
                
                if abs(self.local_position[2]) < 0.01:
                    self.disarming_transition()
                
    def state_callback(self):
        
        """
        in this call back we will do the transitions between all states
        if the drone is flying or in mission
        """
        if self.in_mission:
            if self.flight_state == States.Manual:
                
                self.arming_transition()
                
            elif self.flight_state == States.Arming:
                
                if self.armed:
                    self.plan_path()
                    
            elif self.flight_state ==States.planning:
                self.takeoff_transition()
                
            elif self.flight_state ==States.disarming:
                if not self.armed and not self.guided:
                    self.manual_transition()
                    
                    
    def arming_transition(self):
        self.flight_state= States.Arming
        print(" AZZA BT- ARM")
        self.arm()
        self.take_control() # a Drone methode that controls the software with hardware
        print(" AZZA BT- ARM")
        
    def takeoff_transition(self):
        self.flight_state= States.Takeoff
        print(" AZZA BT- takeoff")
        self.takeoff(self.target_pos[2]) #go to target height
        
    def inair_transition(self):
        self.flight_state= States.InAir
        print(" AZZA BT- teer")
        self.target_pos =self.waypoints.pop(0) #this returns then removes first element from way points
        print("3azza ray7a " , self.target_pos)
        
        #cmd_pos is a Drone methode that sends command to go to this position
        self.cmd_position(self.target_pos[0], self.target_pos[1], self.target_pos[2], self.target_pos[3])
        
    def landing_transition(self):
        
        self.flight_state= States.landing
        print(" AZZA BT- Land")  
        self.land()
    def disarming_transition():
        
        self.flight_state= States.disarming
        print(" AZZA BT- disarm")  
        self.disarm()    
        self.release_control()
        
    def manual_transition(self):
        self.flight_state= States.Manual
        print(" AZZA  BTSLM 3LEK")  
        self.stop()    
        self.in_mission= False
        
        
    def zend_way_points(self):
        print("ZENDING WAY POINTS -----")
        data = msgpack.dumps(self.waypoints) #msgpack.dumps serialize or ease the way of delievering complex structure to connections
        self.connection._master.write(data[100:])
        #now we can send way points to the simulator
    
    def plan_path(self):
        
        
        
        """
        The real path plan will happen here
        as we will retrieve the functions we created in azzaplan.py to use here
        
        """
        self.flight_state=States.planning
        print("3aza btdwr 3la tri2-----")
        target_alt=azza.goal[2]
        safe_dist= 2
        
        self.target_pos[2]= target_alt
        
        #as u may remeber the colliders.csv first row carried the start lat and long
        #we can later retrieve the from azzas gps reading
        file=open("colliders.csv", 'r')
        homepos = file.readline()
        #use regular expression to extract lat and long values
        #here we match the message that starts with(^) lat0 followed by either + or - and a range of numbers followed by point *\.? then range of numbers
        homeposition=re.match("^lat0 ([-+]?[0-9]*\.?[0-9]+), lon0 ([-+]?[0-9]*\.?[0-9]+)$", homepos)
        
        home_lat= float(homeposition.group(1))
        home_long= float(homeposition.group(2))
        
        file.close()
        #home_lat=30.173416
        #home_long= 31.431209
        
        self.set_home_position(home_long, home_lat, 0)#drone inhareted methode for home position
        
        
        """
        as u may remember global_to_local(current_position, home_position) function
        that we created in azzaplan.py that measures the distance traveled using utm
        """
        local_start_position= global_to_local(self.global_position, self.global_home)   
        
        local_goal_pos = ((self.goal[0], self.goal[1], 0), self.global_home)
        
        #data=np.loadtxt("colliders.csv",delimiter=',', skiprows=2)
        data=np.loadtxt("colliders.csv",delimiter=',', skiprows=2)
        
        #recal create grid function
        
        #min_north and min_east are the offsets 
        
        gridz, min_north, min_east = grid(data, target_alt, safe_dist)
        
        
        #create graph
        
        """
        we need to generate the graph once and save it as presistant value
        so we will save it in numpy file so that we do this operation once
        """
        creategraph= True
        if creategraph:
            graph=create_graph(gridz)
            np.save("graph", graph)
            
        else:
            graph =np.load("graph.npy")
            
        grid_start = (int(np.rint(local_start_position[0])) - min_north, int(np.rint(local_start_position[1])) - min_east)
        grid_goal = (int(np.rint(local_goal_pos[0][0])) - min_north, int(np.rint(local_goal_pos[0][1])) - min_east)
        graph_start, graph_goal = skel_start_goal(grid_start, grid_goal, graph)
        
        
        path, _ = a_star(invert(graph).astype(int),H_s, tuple(graph_start), tuple(graph_goal))
        
        print("Extracting way points-----")
        
        path = Waypointz(path)
        
        
        waypoints=[]
        lengthpoints= len(path)
        heading=0
        
        for i, p in enumerate(path):
            
            if i>0:
                p2=path[i-1]
                heading = np.arctan2((p2[1]-p[1]), (p2[0]-p[0]))
            waypoint = [int(np.rint(p[0])) + min_north, int(np.rint(p[1])) + min_east, int(np.rint(target_alt)), heading]
            waypoints.append(waypoint)
            
        print("PHEW, Done extracting way points")
        
        self.waypoints = waypoints
        
        self.zend_way_points()
        
        
    def start(self):
        
        
        """
        Copied from doc. to start the connection
        
        """
        self.start_log("Logs", "NavLog.txt")

        print("starting connection")
        #self.connection.start()
        super().start()
        # Only required if they do threaded
        # while self.in_mission:
        #    pass

        self.stop_log()

        
        
            
    
            
    
        
            
            
        
            
            


In [12]:
import sys
sys.argv = ['your_script.py', '--port', '5760', '--host', '127.0.0.1', '--goal_lat', '37.796385', '--goal_lon', '-122.400219', '--goal_alt', '8']

In [21]:
pip install --upgrade udacidrone

Note: you may need to restart the kernel to use updated packages.
Defaulting to user installation because normal site-packages is not writeable


ERROR: Could not find a version that satisfies the requirement udacidrone (from versions: none)
ERROR: No matching distribution found for udacidrone

[notice] A new release of pip is available: 23.3 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


In [14]:
if __name__ == "__main__":
    parser = argparse.ArgumentParser()
    parser.add_argument('--port', type=int, default=5760, help='Port number')
    parser.add_argument('--host', type=str, default='127.0.0.1', help="host address, i.e. '127.0.0.1'")
    parser.add_argument('--goal_lat', type=float, default=37.796385, help='Goal latitude')
    parser.add_argument('--goal_lon', type=float, default=-122.400219, help='Goal longitude')
    parser.add_argument('--goal_alt', type=float, default=8, help='Goal altitude')
    args = parser.parse_args()

    conn = MavlinkConnection('tcp:127.0.0.1:5760')
    azza = MotionPlanning(conn)

    azza.goal[0] = args.goal_lon
    azza.goal[1] = args.goal_lat
    azza.goal[2] = args.goal_alt
    azza.waypoints=path[:100]
   
    time.sleep(0.005)


    azza.start()

[WinError 10061] No connection could be made because the target machine actively refused it sleeping
[WinError 10061] No connection could be made because the target machine actively refused it sleeping
Retrying connection in 1 second ...
[WinError 10061] No connection could be made because the target machine actively refused it sleeping
[WinError 10061] No connection could be made because the target machine actively refused it sleeping
Retrying connection in 1 second ...
Logs\TLog.txt
Logs\NavLog.txt
starting connection
 AZZA BT- ARM
 AZZA BT- ARM
3aza btdwr 3la tri2-----
ZENDING WAY POINTS -----
 AZZA BT- takeoff
 AZZA BT- teer
3azza ray7a  [-1, 0, 100, 0]
 AZZA BT- teer
3azza ray7a  [3, 4, 100, -2.356194490192345]
 AZZA BT- teer
3azza ray7a  [5, 2, 100, 2.356194490192345]
 AZZA BT- teer
3azza ray7a  [5, 0, 100, 1.5707963267948966]
 AZZA BT- teer
3azza ray7a  [6, -1, 100, 2.356194490192345]
 AZZA BT- teer
3azza ray7a  [6, -3, 100, 1.5707963267948966]
 AZZA BT- teer
3azza ray7a  [7, -4


KeyboardInterrupt



# azza.waypoints


I use the comming steps as the simulator fails to work for large amount of waypoints after planning as it losses connection, so i save the waypoints then pass them to the class as an attribute in the planning phase to save the time wasted in planning

In [19]:
path=azza.waypoints

In [33]:
print(path)

[[-1, 0, 100, 0], [3, 4, 100, -2.356194490192345], [5, 2, 100, 2.356194490192345], [5, 0, 100, 1.5707963267948966], [6, -1, 100, 2.356194490192345], [6, -3, 100, 1.5707963267948966], [7, -4, 100, 2.356194490192345], [7, -6, 100, 1.5707963267948966], [8, -7, 100, 2.356194490192345], [8, -9, 100, 1.5707963267948966], [10, -11, 100, 2.356194490192345], [9, -12, 100, 0.7853981633974483], [9, -64, 100, 1.5707963267948966], [8, -65, 100, 0.7853981633974483], [8, -67, 100, 1.5707963267948966], [7, -68, 100, 0.7853981633974483], [7, -69, 100, 1.5707963267948966], [6, -70, 100, 0.7853981633974483], [6, -71, 100, 1.5707963267948966], [5, -72, 100, 0.7853981633974483], [5, -73, 100, 1.5707963267948966], [4, -74, 100, 0.7853981633974483], [4, -95, 100, 1.5707963267948966], [5, -96, 100, 2.356194490192345], [5, -99, 100, 1.5707963267948966], [6, -100, 100, 2.356194490192345], [6, -102, 100, 1.5707963267948966], [7, -103, 100, 2.356194490192345], [7, -104, 100, 1.5707963267948966], [8, -105, 100, 2.

In [14]:
len(path)

1289

In [13]:
import numpy as np
import re
import argparse
import time

class MotionPlanning(Drone):
    
    
    """
    in this class we will set up the environment for Azza to travel safely, 
    this will not happen if we left azza flying without stoping her if any sudden change in state happpens
    That is why you will find in this class, 
    first we call the drone constructor by super().__init__(connection) to intialise various attributes 
    such as 
        goal_position, 
        target_position, 
        waypoints, 
        in_mission, 
        check_state
        set the initial flight_state to States.MANUAL.
        
    it also register callback functions to handle messages like position velocity or states
    
    
    
    then we will define the call back functions, transition, and azaplan functions
    
    
    
    """
    def __init__(self, connection) :
        
        super().__init__(connection)
        self.goal = [0.0, 0.0, 0.0, 0.0]
        self.goal = np.array([0.0, 0.0, 0.0, 0.0])
        self.target_pos = np.array([0.0, 0.0, 0.0, 0.0])
        self.waypoints = []
        self.in_mission = True
        self.check_state = {}
        
        self.flight_state= States.Manual      #initial state
        
        
        #register the call backs to the drone messages
        self.register_callback(MsgID.LOCAL_POSITION, self.azza_position_callback) #azza_posistion_callback returns local position of azza
        self.register_callback(MsgID.LOCAL_VELOCITY, self.azza_velocity_callback) 
        self.register_callback(MsgID.STATE, self.state_callback)
        
        
        
        #NOW WE ARE DONE WITH THE CONSTRUCTOR
        
        
    def azza_position_callback(self): #let's define azza's local position function
        if self.flight_state==States.Takeoff:
            
            """
            in the take off condition we want to go to the next way point 
            as soon as drone reaches the desired altitude, this can't be 
            optimum if we wait for the curr altitude to be sharpely equal 
            desired altitude that is why when it reaches above 95% drone 
            can go for other way poitn
            
            
            the -1 is becasue in local NED frame upwards is negative
            """
            if -1.0 * self.local_position[2]> 0.95*self.target_pos[2]:
                self.inair_transition()
                
                
        elif self.flight_state == States.InAir:
            
            """
            this part we check if we still have way points 
            and 
            the target postion x axis minus local position x axis less than 1 almost equal
            and
            the target postion y axis minus local position y axis less than 1 almost equal
            
            then do a transition
            """
            if np.linalg.norm(self.target_pos[0:2]-self.local_position[0:2]) <1.0:
                if len(self.waypoints)>0:
                    self.inair_transition()
                else:
                    if np.linalg.norm(self.local_velocity[0:2])< 1.0:
                        self.landing_transition()
                        
                        
    def azza_velocity_callback(self):
        
        if self.flight_state == States.landing:
            
            if self.global_position[2] - self.global_home[2] <0.1:
                
                if abs(self.local_position[2]) < 0.01:
                    self.disarming_transition()
                
    def state_callback(self):
        
        """
        in this call back we will do the transitions between all states
        if the drone is flying or in mission
        """
        if self.in_mission:
            if self.flight_state == States.Manual:
                
                self.arming_transition()
                
            elif self.flight_state == States.Arming:
                
                if self.armed:
                    self.plan_path()
                    
            elif self.flight_state ==States.planning:
                self.takeoff_transition()
                
            
                
            elif self.flight_state ==States.disarming:
                if not self.armed and not self.guided:
                    self.manual_transition()
                    
                    
    def arming_transition(self):
        self.flight_state= States.Arming
        print(" AZZA BT- ARM")
        self.arm()
        self.take_control() # a Drone methode that controls the software with hardware
        print(" AZZA BT- ARM")
        
    def takeoff_transition(self):
        self.flight_state= States.Takeoff
        print(" AZZA BT- takeoff")
        self.takeoff(self.target_pos[2]) #go to target height
        
    def inair_transition(self):
        self.flight_state= States.InAir
        print(" AZZA BT- teer")
        self.target_pos =self.waypoints.pop(0) #this returns then removes first element from way points
        print("3azza ray7a " , self.target_pos)
        
        #cmd_pos is a Drone methode that sends command to go to this position
        self.cmd_position(self.target_pos[0], self.target_pos[1], self.target_pos[2], self.target_pos[3])
        
    def landing_transition(self):
        
        self.flight_state= States.landing
        print(" AZZA BT- Land")  
        self.land()
    def disarming_transition():
        
        self.flight_state= States.disarming
        print(" AZZA BT- disarm")  
        self.disarm()    
        self.release_control()
        
    def manual_transition(self):
        self.flight_state= States.Manual
        print(" AZZA  BTSLM 3LEK")  
        self.stop()    
        self.in_mission= False
        
        
    def zend_way_points(self):
        print("ZENDING WAY POINTS -----")
        data = msgpack.dumps(self.waypoints) #msgpack.dumps serialize or ease the way of delievering complex structure to connections
        self.connection._master.write(data)
        #now we can send way points to the simulator
    
    def plan_path(self):
        
        self.flight_state=States.planning
        print("3aza btdwr 3la tri2-----")
        target_alt=azza.goal[2]
        
        
        self.target_pos[2]= target_alt
        
        #as u may remeber the colliders.csv first row carried the start lat and long
        #we can later retrieve the from azzas gps reading
        file=open("final_map", 'r')
        homepos = file.readline()
        #use regular expression to extract lat and long values
        #here we match the message that starts with(^) lat0 followed by either + or - and a range of numbers followed by point *\.? then range of numbers
        homeposition=re.match("^lat0 ([-+]?[0-9]*\.?[0-9]+), lon0 ([-+]?[0-9]*\.?[0-9]+)$", homepos)
        
        home_lat= float(37.792480)
        home_long= float(-122.397450)
        
        file.close()
        
        self.set_home_position(home_long, home_lat, 0)
        
        
        
        self.waypoints = azza.waypoints
        
        self.zend_way_points()
        
        
    def start(self):
        
        
        """
        Copied from doc. to start the connection
        
        """
        self.start_log("Logs", "NavLog.txt")

        print("starting connection")
        self.connection.start()
        #super().start()
        # Only required if they do threaded
        while self.in_mission:
            pass

        self.stop_log()

        
        
            
    
            
    
        
            
            
        
            
            


In [18]:
path=[[-1, 0, 100, 0], [3, 4, 100, -2.356194490192345], [5, 2, 100, 2.356194490192345], [5, 0, 100, 1.5707963267948966], [6, -1, 100, 2.356194490192345], [6, -3, 100, 1.5707963267948966], [7, -4, 100, 2.356194490192345], [7, -6, 100, 1.5707963267948966], [8, -7, 100, 2.356194490192345], [8, -9, 100, 1.5707963267948966], [10, -11, 100, 2.356194490192345], [9, -12, 100, 0.7853981633974483], [9, -64, 100, 1.5707963267948966], [8, -65, 100, 0.7853981633974483], [8, -67, 100, 1.5707963267948966], [7, -68, 100, 0.7853981633974483], [7, -69, 100, 1.5707963267948966], [6, -70, 100, 0.7853981633974483], [6, -71, 100, 1.5707963267948966], [5, -72, 100, 0.7853981633974483], [5, -73, 100, 1.5707963267948966], [4, -74, 100, 0.7853981633974483], [4, -95, 100, 1.5707963267948966], [5, -96, 100, 2.356194490192345], [5, -99, 100, 1.5707963267948966], [6, -100, 100, 2.356194490192345], [6, -102, 100, 1.5707963267948966], [7, -103, 100, 2.356194490192345], [7, -104, 100, 1.5707963267948966], [8, -105, 100, 2.356194490192345], [8, -106, 100, 1.5707963267948966], [10, -108, 100, 2.356194490192345], [10, -110, 100, 1.5707963267948966], [11, -111, 100, 2.356194490192345], [11, -114, 100, 1.5707963267948966], [12, -115, 100, 2.356194490192345], [12, -116, 100, 1.5707963267948966], [13, -117, 100, 2.356194490192345], [15, -117, 100, 3.141592653589793], [16, -118, 100, 2.356194490192345], [18, -118, 100, 3.141592653589793], [19, -119, 100, 2.356194490192345], [22, -119, 100, 3.141592653589793], [23, -120, 100, 2.356194490192345], [45, -120, 100, 3.141592653589793], [46, -121, 100, 2.356194490192345], [49, -121, 100, 3.141592653589793], [50, -122, 100, 2.356194490192345], [52, -122, 100, 3.141592653589793], [53, -123, 100, 2.356194490192345], [55, -123, 100, 3.141592653589793], [56, -124, 100, 2.356194490192345], [57, -124, 100, 3.141592653589793], [58, -125, 100, 2.356194490192345], [59, -125, 100, 3.141592653589793], [60, -126, 100, 2.356194490192345], [61, -126, 100, 3.141592653589793], [62, -127, 100, 2.356194490192345], [64, -127, 100, 3.141592653589793], [65, -128, 100, 2.356194490192345], [67, -128, 100, 3.141592653589793], [68, -129, 100, 2.356194490192345], [70, -129, 100, 3.141592653589793], [71, -130, 100, 2.356194490192345], [72, -130, 100, 3.141592653589793], [73, -131, 100, 2.356194490192345], [74, -131, 100, 3.141592653589793], [75, -132, 100, 2.356194490192345], [77, -132, 100, 3.141592653589793], [78, -133, 100, 2.356194490192345], [79, -133, 100, 3.141592653589793], [80, -134, 100, 2.356194490192345], [82, -134, 100, 3.141592653589793], [83, -135, 100, 2.356194490192345], [84, -135, 100, 3.141592653589793], [85, -136, 100, 2.356194490192345], [87, -136, 100, 3.141592653589793], [88, -137, 100, 2.356194490192345], [89, -137, 100, 3.141592653589793], [90, -138, 100, 2.356194490192345], [92, -138, 100, 3.141592653589793], [93, -139, 100, 2.356194490192345], [94, -139, 100, 3.141592653589793], [95, -140, 100, 2.356194490192345], [96, -140, 100, 3.141592653589793], [97, -141, 100, 2.356194490192345], [99, -141, 100, 3.141592653589793], [100, -142, 100, 2.356194490192345], [101, -142, 100, 3.141592653589793], [102, -143, 100, 2.356194490192345], [104, -143, 100, 3.141592653589793], [105, -144, 100, 2.356194490192345], [106, -144, 100, 3.141592653589793], [107, -145, 100, 2.356194490192345], [109, -145, 100, 3.141592653589793], [110, -146, 100, 2.356194490192345], [111, -146, 100, 3.141592653589793], [112, -147, 100, 2.356194490192345], [114, -147, 100, 3.141592653589793], [115, -148, 100, 2.356194490192345], [116, -148, 100, 3.141592653589793], [117, -149, 100, 2.356194490192345], [119, -149, 100, 3.141592653589793], [123, -153, 100, 2.356194490192345], [124, -153, 100, 3.141592653589793], [125, -154, 100, 2.356194490192345], [126, -153, 100, -2.356194490192345], [128, -153, 100, 3.141592653589793], [132, -157, 100, 2.356194490192345], [133, -156, 100, -2.356194490192345], [134, -157, 100, 2.356194490192345], [135, -156, 100, -2.356194490192345], [136, -157, 100, 2.356194490192345], [138, -157, 100, 3.141592653589793], [143, -162, 100, 2.356194490192345], [145, -162, 100, 3.141592653589793], [146, -161, 100, -2.356194490192345], [149, -164, 100, 2.356194490192345], [150, -164, 100, 3.141592653589793], [151, -165, 100, 2.356194490192345], [152, -164, 100, -2.356194490192345], [153, -165, 100, 2.356194490192345], [154, -165, 100, 3.141592653589793], [155, -166, 100, 2.356194490192345], [156, -165, 100, -2.356194490192345], [158, -167, 100, 2.356194490192345], [159, -166, 100, -2.356194490192345], [159, -165, 100, -1.5707963267948966], [160, -164, 100, -2.356194490192345], [160, -163, 100, -1.5707963267948966], [162, -161, 100, -2.356194490192345], [162, -160, 100, -1.5707963267948966], [166, -156, 100, -2.356194490192345], [166, -155, 100, -1.5707963267948966], [169, -152, 100, -2.356194490192345], [169, -151, 100, -1.5707963267948966], [171, -149, 100, -2.356194490192345], [171, -148, 100, -1.5707963267948966], [173, -146, 100, -2.356194490192345], [173, -145, 100, -1.5707963267948966], [175, -143, 100, -2.356194490192345], [175, -142, 100, -1.5707963267948966], [178, -139, 100, -2.356194490192345], [178, -138, 100, -1.5707963267948966], [180, -136, 100, -2.356194490192345], [180, -135, 100, -1.5707963267948966], [183, -132, 100, -2.356194490192345], [183, -131, 100, -1.5707963267948966], [186, -128, 100, -2.356194490192345], [188, -128, 100, 3.141592653589793], [189, -127, 100, -2.356194490192345], [191, -127, 100, 3.141592653589793], [192, -126, 100, -2.356194490192345], [194, -126, 100, 3.141592653589793], [195, -125, 100, -2.356194490192345], [197, -125, 100, 3.141592653589793], [198, -124, 100, -2.356194490192345], [201, -124, 100, 3.141592653589793], [202, -123, 100, -2.356194490192345], [204, -123, 100, 3.141592653589793], [205, -122, 100, -2.356194490192345], [207, -122, 100, 3.141592653589793], [208, -121, 100, -2.356194490192345], [210, -121, 100, 3.141592653589793], [211, -120, 100, -2.356194490192345], [213, -120, 100, 3.141592653589793], [214, -119, 100, -2.356194490192345], [216, -119, 100, 3.141592653589793], [217, -118, 100, -2.356194490192345], [220, -118, 100, 3.141592653589793], [221, -117, 100, -2.356194490192345], [223, -117, 100, 3.141592653589793], [224, -116, 100, -2.356194490192345], [227, -116, 100, 3.141592653589793], [228, -115, 100, -2.356194490192345], [231, -115, 100, 3.141592653589793], [232, -114, 100, -2.356194490192345], [235, -114, 100, 3.141592653589793], [236, -113, 100, -2.356194490192345], [237, -113, 100, 3.141592653589793], [243, -107, 100, -2.356194490192345], [244, -107, 100, 3.141592653589793], [248, -103, 100, -2.356194490192345], [249, -103, 100, 3.141592653589793], [253, -99, 100, -2.356194490192345], [254, -99, 100, 3.141592653589793], [256, -97, 100, -2.356194490192345], [257, -97, 100, 3.141592653589793], [259, -95, 100, -2.356194490192345], [260, -95, 100, 3.141592653589793], [262, -93, 100, -2.356194490192345], [263, -93, 100, 3.141592653589793], [265, -91, 100, -2.356194490192345], [266, -91, 100, 3.141592653589793], [267, -90, 100, -2.356194490192345], [268, -90, 100, 3.141592653589793], [270, -88, 100, -2.356194490192345], [271, -88, 100, 3.141592653589793], [272, -87, 100, -2.356194490192345], [273, -88, 100, 2.356194490192345], [275, -88, 100, 3.141592653589793], [276, -87, 100, -2.356194490192345], [277, -88, 100, 2.356194490192345], [278, -88, 100, 3.141592653589793], [279, -89, 100, 2.356194490192345], [280, -88, 100, -2.356194490192345], [283, -91, 100, 2.356194490192345], [284, -91, 100, 3.141592653589793], [285, -92, 100, 2.356194490192345], [287, -90, 100, -2.356194490192345], [285, -88, 100, -0.7853981633974483], [284, -88, 100, 0.0], [281, -85, 100, -0.7853981633974483], [280, -86, 100, 0.7853981633974483], [279, -85, 100, -0.7853981633974483], [278, -86, 100, 0.7853981633974483], [275, -83, 100, -0.7853981633974483], [279, -79, 100, -2.356194490192345], [279, -78, 100, -1.5707963267948966], [283, -74, 100, -2.356194490192345], [283, -73, 100, -1.5707963267948966], [285, -71, 100, -2.356194490192345], [285, -70, 100, -1.5707963267948966], [287, -68, 100, -2.356194490192345], [287, -67, 100, -1.5707963267948966], [289, -65, 100, -2.356194490192345], [289, -64, 100, -1.5707963267948966], [290, -63, 100, -2.356194490192345], [290, -62, 100, -1.5707963267948966], [291, -61, 100, -2.356194490192345], [291, -60, 100, -1.5707963267948966], [292, -59, 100, -2.356194490192345], [292, -58, 100, -1.5707963267948966], [293, -57, 100, -2.356194490192345], [293, -56, 100, -1.5707963267948966], [294, -55, 100, -2.356194490192345], [294, -54, 100, -1.5707963267948966], [295, -53, 100, -2.356194490192345], [295, -52, 100, -1.5707963267948966], [296, -51, 100, -2.356194490192345], [296, -50, 100, -1.5707963267948966], [297, -49, 100, -2.356194490192345], [297, -48, 100, -1.5707963267948966], [298, -47, 100, -2.356194490192345], [298, -46, 100, -1.5707963267948966], [300, -44, 100, -2.356194490192345], [300, -43, 100, -1.5707963267948966], [301, -42, 100, -2.356194490192345], [301, -41, 100, -1.5707963267948966], [302, -40, 100, -2.356194490192345], [302, -39, 100, -1.5707963267948966], [303, -38, 100, -2.356194490192345], [303, -37, 100, -1.5707963267948966], [305, -35, 100, -2.356194490192345], [306, -36, 100, 2.356194490192345], [307, -36, 100, 3.141592653589793], [308, -37, 100, 2.356194490192345], [310, -37, 100, 3.141592653589793], [311, -38, 100, 2.356194490192345], [312, -38, 100, 3.141592653589793], [314, -40, 100, 2.356194490192345], [315, -40, 100, 3.141592653589793], [316, -41, 100, 2.356194490192345], [317, -41, 100, 3.141592653589793], [318, -42, 100, 2.356194490192345], [319, -42, 100, 3.141592653589793], [320, -43, 100, 2.356194490192345], [321, -43, 100, 3.141592653589793], [322, -44, 100, 2.356194490192345], [323, -44, 100, 3.141592653589793], [324, -45, 100, 2.356194490192345], [325, -45, 100, 3.141592653589793], [326, -46, 100, 2.356194490192345], [327, -46, 100, 3.141592653589793], [328, -47, 100, 2.356194490192345], [329, -47, 100, 3.141592653589793], [330, -48, 100, 2.356194490192345], [331, -48, 100, 3.141592653589793], [332, -49, 100, 2.356194490192345], [334, -49, 100, 3.141592653589793], [335, -50, 100, 2.356194490192345], [359, -50, 100, 3.141592653589793], [360, -51, 100, 2.356194490192345], [361, -51, 100, 3.141592653589793], [364, -54, 100, 2.356194490192345], [366, -54, 100, 3.141592653589793], [367, -55, 100, 2.356194490192345], [416, -55, 100, 3.141592653589793], [417, -54, 100, -2.356194490192345], [418, -55, 100, 2.356194490192345], [424, -55, 100, 3.141592653589793], [425, -56, 100, 2.356194490192345], [427, -56, 100, 3.141592653589793], [428, -57, 100, 2.356194490192345], [430, -57, 100, 3.141592653589793], [431, -58, 100, 2.356194490192345], [433, -58, 100, 3.141592653589793], [434, -59, 100, 2.356194490192345], [436, -59, 100, 3.141592653589793], [437, -60, 100, 2.356194490192345], [439, -60, 100, 3.141592653589793], [442, -63, 100, 2.356194490192345], [443, -62, 100, -2.356194490192345], [444, -62, 100, 3.141592653589793], [449, -67, 100, 2.356194490192345], [450, -66, 100, -2.356194490192345], [452, -68, 100, 2.356194490192345], [453, -68, 100, 3.141592653589793], [454, -67, 100, -2.356194490192345], [455, -68, 100, 2.356194490192345], [456, -67, 100, -2.356194490192345], [457, -67, 100, 3.141592653589793], [459, -69, 100, 2.356194490192345], [460, -69, 100, 3.141592653589793], [461, -70, 100, 2.356194490192345], [462, -69, 100, -2.356194490192345], [463, -70, 100, 2.356194490192345], [464, -70, 100, 3.141592653589793], [465, -71, 100, 2.356194490192345], [466, -70, 100, -2.356194490192345], [468, -72, 100, 2.356194490192345], [469, -71, 100, -2.356194490192345], [471, -73, 100, 2.356194490192345], [472, -73, 100, 3.141592653589793], [475, -76, 100, 2.356194490192345], [476, -76, 100, 3.141592653589793], [478, -78, 100, 2.356194490192345], [479, -78, 100, 3.141592653589793], [480, -79, 100, 2.356194490192345], [487, -72, 100, -2.356194490192345], [488, -72, 100, 3.141592653589793], [489, -71, 100, -2.356194490192345], [490, -71, 100, 3.141592653589793], [492, -69, 100, -2.356194490192345], [493, -69, 100, 3.141592653589793], [494, -68, 100, -2.356194490192345], [495, -68, 100, 3.141592653589793], [496, -67, 100, -2.356194490192345], [497, -67, 100, 3.141592653589793], [499, -65, 100, -2.356194490192345], [500, -65, 100, 3.141592653589793], [501, -64, 100, -2.356194490192345], [502, -64, 100, 3.141592653589793], [503, -63, 100, -2.356194490192345], [504, -63, 100, 3.141592653589793], [506, -61, 100, -2.356194490192345], [507, -61, 100, 3.141592653589793], [508, -60, 100, -2.356194490192345], [509, -60, 100, 3.141592653589793], [510, -59, 100, -2.356194490192345], [511, -59, 100, 3.141592653589793], [513, -57, 100, -2.356194490192345], [514, -57, 100, 3.141592653589793], [515, -56, 100, -2.356194490192345], [516, -56, 100, 3.141592653589793], [517, -55, 100, -2.356194490192345], [518, -55, 100, 3.141592653589793], [520, -53, 100, -2.356194490192345], [521, -53, 100, 3.141592653589793], [522, -52, 100, -2.356194490192345], [523, -52, 100, 3.141592653589793], [524, -51, 100, -2.356194490192345], [525, -51, 100, 3.141592653589793], [527, -49, 100, -2.356194490192345], [528, -49, 100, 3.141592653589793], [529, -48, 100, -2.356194490192345], [530, -48, 100, 3.141592653589793], [532, -46, 100, -2.356194490192345], [533, -46, 100, 3.141592653589793], [534, -45, 100, -2.356194490192345], [535, -45, 100, 3.141592653589793], [536, -44, 100, -2.356194490192345], [537, -44, 100, 3.141592653589793], [539, -42, 100, -2.356194490192345], [540, -42, 100, 3.141592653589793], [541, -41, 100, -2.356194490192345], [542, -41, 100, 3.141592653589793], [543, -40, 100, -2.356194490192345], [544, -40, 100, 3.141592653589793], [546, -38, 100, -2.356194490192345], [547, -38, 100, 3.141592653589793], [548, -37, 100, -2.356194490192345], [549, -37, 100, 3.141592653589793], [550, -36, 100, -2.356194490192345], [551, -36, 100, 3.141592653589793], [553, -34, 100, -2.356194490192345], [554, -34, 100, 3.141592653589793], [555, -33, 100, -2.356194490192345], [556, -33, 100, 3.141592653589793], [557, -32, 100, -2.356194490192345], [558, -32, 100, 3.141592653589793], [559, -31, 100, -2.356194490192345], [559, -30, 100, -1.5707963267948966], [560, -29, 100, -2.356194490192345], [561, -29, 100, 3.141592653589793], [563, -27, 100, -2.356194490192345], [564, -28, 100, 2.356194490192345], [565, -28, 100, 3.141592653589793], [568, -25, 100, -2.356194490192345], [570, -25, 100, 3.141592653589793], [573, -22, 100, -2.356194490192345], [574, -23, 100, 2.356194490192345], [578, -19, 100, -2.356194490192345], [579, -20, 100, 2.356194490192345], [580, -19, 100, -2.356194490192345], [582, -19, 100, 3.141592653589793], [583, -18, 100, -2.356194490192345], [585, -18, 100, 3.141592653589793], [586, -17, 100, -2.356194490192345], [588, -17, 100, 3.141592653589793], [589, -16, 100, -2.356194490192345], [591, -16, 100, 3.141592653589793], [592, -15, 100, -2.356194490192345], [594, -15, 100, 3.141592653589793], [595, -14, 100, -2.356194490192345], [597, -14, 100, 3.141592653589793], [598, -13, 100, -2.356194490192345], [600, -13, 100, 3.141592653589793], [601, -12, 100, -2.356194490192345], [603, -12, 100, 3.141592653589793], [604, -13, 100, 2.356194490192345], [604, -55, 100, 1.5707963267948966], [603, -56, 100, 0.7853981633974483], [604, -57, 100, 2.356194490192345], [604, -444, 100, 1.5707963267948966], [603, -445, 100, 0.7853981633974483], [449, -445, 100, 0.0], [448, -444, 100, -0.7853981633974483], [447, -445, 100, 0.7853981633974483], [374, -445, 100, 0.0], [373, -444, 100, -0.7853981633974483], [372, -445, 100, 0.7853981633974483], [359, -445, 100, 0.0], [358, -444, 100, -0.7853981633974483], [357, -445, 100, 0.7853981633974483], [217, -445, 100, 0.0], [216, -444, 100, -0.7853981633974483], [215, -445, 100, 0.7853981633974483], [207, -445, 100, 0.0], [206, -444, 100, -0.7853981633974483], [205, -445, 100, 0.7853981633974483], [104, -445, 100, 0.0], [98, -439, 100, -0.7853981633974483], [98, -438, 100, -1.5707963267948966], [92, -432, 100, -0.7853981633974483], [92, -431, 100, -1.5707963267948966], [90, -429, 100, -0.7853981633974483], [90, -428, 100, -1.5707963267948966], [88, -426, 100, -0.7853981633974483], [88, -425, 100, -1.5707963267948966], [87, -424, 100, -0.7853981633974483], [87, -423, 100, -1.5707963267948966], [86, -422, 100, -0.7853981633974483], [86, -420, 100, -1.5707963267948966], [85, -419, 100, -0.7853981633974483], [85, -417, 100, -1.5707963267948966], [84, -416, 100, -0.7853981633974483], [84, -414, 100, -1.5707963267948966], [83, -413, 100, -0.7853981633974483], [83, -411, 100, -1.5707963267948966], [82, -410, 100, -0.7853981633974483], [82, -408, 100, -1.5707963267948966], [81, -407, 100, -0.7853981633974483], [81, -406, 100, -1.5707963267948966], [80, -405, 100, -0.7853981633974483], [80, -404, 100, -1.5707963267948966], [78, -402, 100, -0.7853981633974483], [78, -401, 100, -1.5707963267948966], [76, -399, 100, -0.7853981633974483], [76, -398, 100, -1.5707963267948966], [70, -392, 100, -0.7853981633974483], [70, -391, 100, -1.5707963267948966], [67, -388, 100, -0.7853981633974483], [65, -388, 100, 0.0], [64, -389, 100, 0.7853981633974483], [63, -389, 100, 0.0], [62, -390, 100, 0.7853981633974483], [61, -390, 100, 0.0], [60, -391, 100, 0.7853981633974483], [58, -391, 100, 0.0], [57, -392, 100, 0.7853981633974483], [55, -392, 100, 0.0], [54, -393, 100, 0.7853981633974483], [52, -393, 100, 0.0], [51, -394, 100, 0.7853981633974483], [50, -394, 100, 0.0], [49, -395, 100, 0.7853981633974483], [48, -395, 100, 0.0], [47, -396, 100, 0.7853981633974483], [46, -396, 100, 0.0], [45, -397, 100, 0.7853981633974483], [43, -397, 100, 0.0], [42, -398, 100, 0.7853981633974483], [40, -398, 100, 0.0], [39, -399, 100, 0.7853981633974483], [36, -399, 100, 0.0], [35, -400, 100, 0.7853981633974483], [23, -400, 100, 0.0], [22, -401, 100, 0.7853981633974483], [19, -401, 100, 0.0], [18, -402, 100, 0.7853981633974483], [16, -402, 100, 0.0], [15, -403, 100, 0.7853981633974483], [13, -403, 100, 0.0], [12, -404, 100, 0.7853981633974483], [11, -404, 100, 0.0], [10, -405, 100, 0.7853981633974483], [9, -405, 100, 0.0], [8, -406, 100, 0.7853981633974483], [7, -406, 100, 0.0], [6, -407, 100, 0.7853981633974483], [5, -407, 100, 0.0], [3, -409, 100, 0.7853981633974483], [2, -409, 100, 0.0], [-1, -412, 100, 0.7853981633974483], [-2, -412, 100, 0.0], [-5, -415, 100, 0.7853981633974483], [-6, -415, 100, 0.0], [-9, -418, 100, 0.7853981633974483], [-10, -418, 100, 0.0], [-14, -422, 100, 0.7853981633974483], [-15, -422, 100, 0.0], [-19, -426, 100, 0.7853981633974483], [-21, -426, 100, 0.0], [-25, -430, 100, 0.7853981633974483], [-26, -429, 100, -0.7853981633974483], [-29, -432, 100, 0.7853981633974483], [-31, -432, 100, 0.0], [-36, -437, 100, 0.7853981633974483], [-37, -436, 100, -0.7853981633974483], [-38, -437, 100, 0.7853981633974483], [-40, -437, 100, 0.0], [-45, -442, 100, 0.7853981633974483], [-46, -442, 100, 0.0], [-49, -445, 100, 0.7853981633974483], [-50, -444, 100, -0.7853981633974483], [-51, -445, 100, 0.7853981633974483], [-52, -444, 100, -0.7853981633974483], [-53, -445, 100, 0.7853981633974483], [-74, -445, 100, 0.0], [-75, -444, 100, -0.7853981633974483], [-76, -445, 100, 0.7853981633974483], [-88, -445, 100, 0.0], [-89, -444, 100, -0.7853981633974483], [-89, -442, 100, -1.5707963267948966], [-90, -441, 100, -0.7853981633974483], [-90, -437, 100, -1.5707963267948966], [-91, -436, 100, -0.7853981633974483], [-91, -433, 100, -1.5707963267948966], [-92, -432, 100, -0.7853981633974483], [-92, -429, 100, -1.5707963267948966], [-93, -428, 100, -0.7853981633974483], [-93, -424, 100, -1.5707963267948966], [-94, -423, 100, -0.7853981633974483], [-94, -420, 100, -1.5707963267948966], [-95, -419, 100, -0.7853981633974483], [-95, -415, 100, -1.5707963267948966], [-96, -414, 100, -0.7853981633974483], [-96, -411, 100, -1.5707963267948966], [-97, -410, 100, -0.7853981633974483], [-97, -406, 100, -1.5707963267948966], [-98, -405, 100, -0.7853981633974483], [-98, -400, 100, -1.5707963267948966], [-99, -399, 100, -0.7853981633974483], [-99, -394, 100, -1.5707963267948966], [-100, -393, 100, -0.7853981633974483], [-100, -384, 100, -1.5707963267948966], [-101, -383, 100, -0.7853981633974483], [-101, -357, 100, -1.5707963267948966], [-103, -355, 100, -0.7853981633974483], [-226, -355, 100, 0.0], [-227, -354, 100, -0.7853981633974483], [-230, -354, 100, 0.0], [-231, -353, 100, -0.7853981633974483], [-233, -353, 100, 0.0], [-234, -352, 100, -0.7853981633974483], [-235, -352, 100, 0.0], [-236, -351, 100, -0.7853981633974483], [-237, -351, 100, 0.0], [-239, -349, 100, -0.7853981633974483], [-241, -349, 100, 0.0], [-242, -348, 100, -0.7853981633974483], [-244, -348, 100, 0.0], [-245, -347, 100, -0.7853981633974483], [-247, -347, 100, 0.0], [-248, -346, 100, -0.7853981633974483], [-249, -346, 100, 0.0], [-250, -345, 100, -0.7853981633974483], [-251, -345, 100, 0.0], [-252, -344, 100, -0.7853981633974483], [-253, -344, 100, 0.0], [-254, -343, 100, -0.7853981633974483], [-255, -343, 100, 0.0], [-257, -341, 100, -0.7853981633974483], [-258, -341, 100, 0.0], [-260, -339, 100, -0.7853981633974483], [-264, -339, 100, 0.0], [-265, -338, 100, -0.7853981633974483], [-270, -338, 100, 0.0], [-271, -337, 100, -0.7853981633974483], [-276, -337, 100, 0.0], [-277, -336, 100, -0.7853981633974483], [-282, -336, 100, 0.0], [-283, -335, 100, -0.7853981633974483], [-288, -335, 100, 0.0], [-289, -334, 100, -0.7853981633974483], [-294, -334, 100, 0.0], [-295, -333, 100, -0.7853981633974483], [-300, -333, 100, 0.0], [-301, -332, 100, -0.7853981633974483], [-304, -332, 100, 0.0], [-307, -335, 100, 0.7853981633974483], [-310, -332, 100, -0.7853981633974483], [-310, -331, 100, -1.5707963267948966], [-316, -325, 100, -0.7853981633974483], [-315, -324, 100, -2.356194490192345], [-316, -323, 100, -0.7853981633974483], [-316, -304, 100, -1.5707963267948966], [-315, -303, 100, -2.356194490192345], [-314, -303, 100, 3.141592653589793], [-280, -269, 100, -2.356194490192345], [-279, -269, 100, 3.141592653589793], [-273, -263, 100, -2.356194490192345], [-272, -263, 100, 3.141592653589793], [-270, -261, 100, -2.356194490192345], [-269, -261, 100, 3.141592653589793], [-266, -258, 100, -2.356194490192345], [-265, -258, 100, 3.141592653589793], [-263, -256, 100, -2.356194490192345], [-262, -256, 100, 3.141592653589793], [-260, -254, 100, -2.356194490192345], [-259, -254, 100, 3.141592653589793], [-257, -252, 100, -2.356194490192345], [-256, -252, 100, 3.141592653589793], [-253, -249, 100, -2.356194490192345], [-251, -249, 100, 3.141592653589793], [-250, -248, 100, -2.356194490192345], [-248, -248, 100, 3.141592653589793], [-247, -247, 100, -2.356194490192345], [-245, -247, 100, 3.141592653589793], [-244, -246, 100, -2.356194490192345], [-244, -245, 100, -1.5707963267948966], [-243, -244, 100, -2.356194490192345], [-243, -243, 100, -1.5707963267948966], [-242, -242, 100, -2.356194490192345], [-242, -241, 100, -1.5707963267948966], [-230, -229, 100, -2.356194490192345], [-229, -229, 100, 3.141592653589793], [-228, -228, 100, -2.356194490192345], [-227, -228, 100, 3.141592653589793], [-226, -227, 100, -2.356194490192345], [-225, -227, 100, 3.141592653589793], [-224, -226, 100, -2.356194490192345], [-223, -226, 100, 3.141592653589793], [-222, -225, 100, -2.356194490192345], [-221, -225, 100, 3.141592653589793], [-220, -224, 100, -2.356194490192345], [-219, -224, 100, 3.141592653589793], [-218, -223, 100, -2.356194490192345], [-216, -223, 100, 3.141592653589793], [-215, -222, 100, -2.356194490192345], [-213, -222, 100, 3.141592653589793], [-212, -221, 100, -2.356194490192345], [-210, -221, 100, 3.141592653589793], [-209, -220, 100, -2.356194490192345], [-208, -220, 100, 3.141592653589793], [-207, -219, 100, -2.356194490192345], [-206, -219, 100, 3.141592653589793], [-205, -218, 100, -2.356194490192345], [-204, -218, 100, 3.141592653589793], [-202, -216, 100, -2.356194490192345], [-201, -216, 100, 3.141592653589793], [-200, -215, 100, -2.356194490192345], [-199, -215, 100, 3.141592653589793], [-197, -213, 100, -2.356194490192345], [-196, -213, 100, 3.141592653589793], [-192, -209, 100, -2.356194490192345], [-220, -181, 100, -0.7853981633974483], [-220, -180, 100, -1.5707963267948966], [-225, -175, 100, -0.7853981633974483], [-225, -174, 100, -1.5707963267948966], [-226, -173, 100, -0.7853981633974483], [-226, -168, 100, -1.5707963267948966], [-227, -167, 100, -0.7853981633974483], [-227, -166, 100, -1.5707963267948966], [-228, -165, 100, -0.7853981633974483], [-233, -165, 100, 0.0], [-236, -162, 100, -0.7853981633974483], [-236, -158, 100, -1.5707963267948966], [-239, -155, 100, -0.7853981633974483], [-243, -155, 100, 0.0], [-244, -154, 100, -0.7853981633974483], [-245, -154, 100, 0.0], [-246, -153, 100, -0.7853981633974483], [-246, -148, 100, -1.5707963267948966], [-249, -145, 100, -0.7853981633974483], [-254, -145, 100, 0.0], [-255, -144, 100, -0.7853981633974483], [-255, -143, 100, -1.5707963267948966], [-256, -142, 100, -0.7853981633974483], [-256, -137, 100, -1.5707963267948966], [-258, -135, 100, -0.7853981633974483], [-263, -135, 100, 0.0], [-264, -134, 100, -0.7853981633974483], [-266, -134, 100, 0.0], [-270, -130, 100, -0.7853981633974483], [-275, -130, 100, 0.0], [-276, -129, 100, -0.7853981633974483], [-278, -129, 100, 0.0], [-279, -128, 100, -0.7853981633974483], [-280, -128, 100, 0.0], [-281, -127, 100, -0.7853981633974483], [-282, -127, 100, 0.0], [-283, -126, 100, -0.7853981633974483], [-284, -126, 100, 0.0], [-285, -125, 100, -0.7853981633974483], [-286, -125, 100, 0.0], [-287, -124, 100, -0.7853981633974483], [-290, -124, 100, 0.0], [-291, -123, 100, -0.7853981633974483], [-293, -123, 100, 0.0], [-294, -122, 100, -0.7853981633974483], [-296, -122, 100, 0.0], [-297, -121, 100, -0.7853981633974483], [-299, -121, 100, 0.0], [-300, -120, 100, -0.7853981633974483], [-315, -120, 100, 0.0], [-316, -119, 100, -0.7853981633974483], [-316, -47, 100, -1.5707963267948966], [-314, -45, 100, -2.356194490192345], [-296, -45, 100, 3.141592653589793], [-295, -46, 100, 2.356194490192345], [-293, -44, 100, -2.356194490192345], [-290, -44, 100, 3.141592653589793], [-289, -43, 100, -2.356194490192345], [-286, -43, 100, 3.141592653589793], [-285, -42, 100, -2.356194490192345], [-282, -42, 100, 3.141592653589793], [-281, -41, 100, -2.356194490192345], [-279, -41, 100, 3.141592653589793], [-277, -39, 100, -2.356194490192345], [-276, -39, 100, 3.141592653589793], [-275, -38, 100, -2.356194490192345], [-274, -38, 100, 3.141592653589793], [-273, -37, 100, -2.356194490192345], [-271, -37, 100, 3.141592653589793], [-270, -36, 100, -2.356194490192345], [-267, -36, 100, 3.141592653589793], [-266, -35, 100, -2.356194490192345], [-256, -35, 100, 3.141592653589793], [-255, -34, 100, -2.356194490192345], [-252, -34, 100, 3.141592653589793], [-251, -33, 100, -2.356194490192345], [-249, -33, 100, 3.141592653589793], [-248, -32, 100, -2.356194490192345], [-247, -32, 100, 3.141592653589793], [-246, -31, 100, -2.356194490192345], [-245, -31, 100, 3.141592653589793], [-243, -29, 100, -2.356194490192345], [-241, -29, 100, 3.141592653589793], [-240, -28, 100, -2.356194490192345], [-237, -28, 100, 3.141592653589793], [-236, -27, 100, -2.356194490192345], [-233, -27, 100, 3.141592653589793], [-219, -13, 100, -2.356194490192345], [-219, -12, 100, -1.5707963267948966], [-217, -10, 100, -2.356194490192345], [-217, -9, 100, -1.5707963267948966], [-218, -8, 100, -0.7853981633974483], [-218, -5, 100, -1.5707963267948966], [-219, -4, 100, -0.7853981633974483], [-219, -1, 100, -1.5707963267948966], [-220, 0, 100, -0.7853981633974483], [-220, 2, 100, -1.5707963267948966], [-222, 4, 100, -0.7853981633974483], [-222, 5, 100, -1.5707963267948966], [-223, 6, 100, -0.7853981633974483], [-223, 7, 100, -1.5707963267948966], [-224, 8, 100, -0.7853981633974483], [-224, 10, 100, -1.5707963267948966], [-225, 11, 100, -0.7853981633974483], [-225, 14, 100, -1.5707963267948966], [-226, 15, 100, -0.7853981633974483], [-226, 16, 100, -1.5707963267948966], [-227, 17, 100, -0.7853981633974483], [-227, 18, 100, -1.5707963267948966], [-228, 19, 100, -0.7853981633974483], [-228, 20, 100, -1.5707963267948966], [-229, 21, 100, -0.7853981633974483], [-229, 22, 100, -1.5707963267948966], [-230, 23, 100, -0.7853981633974483], [-230, 25, 100, -1.5707963267948966], [-231, 26, 100, -0.7853981633974483], [-231, 30, 100, -1.5707963267948966], [-281, 80, 100, -0.7853981633974483], [-272, 89, 100, -2.356194490192345], [-272, 90, 100, -1.5707963267948966], [-267, 95, 100, -2.356194490192345], [-267, 97, 100, -1.5707963267948966], [-266, 98, 100, -2.356194490192345], [-266, 102, 100, -1.5707963267948966], [-263, 105, 100, -2.356194490192345], [-258, 105, 100, 3.141592653589793], [-256, 107, 100, -2.356194490192345], [-256, 113, 100, -1.5707963267948966], [-254, 115, 100, -2.356194490192345], [-249, 115, 100, 3.141592653589793], [-246, 118, 100, -2.356194490192345], [-246, 123, 100, -1.5707963267948966], [-245, 124, 100, -2.356194490192345], [-245, 125, 100, -1.5707963267948966], [-241, 129, 100, -2.356194490192345], [-241, 130, 100, -1.5707963267948966], [-236, 135, 100, -2.356194490192345], [-236, 163, 100, -1.5707963267948966], [-237, 164, 100, -0.7853981633974483], [-236, 165, 100, -2.356194490192345], [-236, 183, 100, -1.5707963267948966], [-237, 184, 100, -0.7853981633974483], [-236, 185, 100, -2.356194490192345], [-236, 190, 100, -1.5707963267948966], [-239, 193, 100, -0.7853981633974483], [-239, 194, 100, -1.5707963267948966], [-244, 199, 100, -0.7853981633974483], [-244, 200, 100, -1.5707963267948966], [-245, 201, 100, -0.7853981633974483], [-245, 202, 100, -1.5707963267948966], [-247, 204, 100, -0.7853981633974483], [-247, 205, 100, -1.5707963267948966], [-249, 207, 100, -0.7853981633974483], [-249, 208, 100, -1.5707963267948966], [-251, 210, 100, -0.7853981633974483], [-251, 212, 100, -1.5707963267948966], [-252, 213, 100, -0.7853981633974483], [-252, 215, 100, -1.5707963267948966], [-254, 217, 100, -0.7853981633974483], [-254, 218, 100, -1.5707963267948966], [-255, 219, 100, -0.7853981633974483], [-255, 220, 100, -1.5707963267948966], [-263, 228, 100, -0.7853981633974483], [-263, 229, 100, -1.5707963267948966], [-270, 236, 100, -0.7853981633974483], [-270, 237, 100, -1.5707963267948966], [-277, 244, 100, -0.7853981633974483], [-278, 244, 100, 0.0], [-279, 245, 100, -0.7853981633974483], [-280, 245, 100, 0.0], [-282, 247, 100, -0.7853981633974483], [-283, 247, 100, 0.0], [-284, 248, 100, -0.7853981633974483], [-285, 248, 100, 0.0], [-286, 249, 100, -0.7853981633974483], [-287, 249, 100, 0.0], [-288, 250, 100, -0.7853981633974483], [-289, 250, 100, 0.0], [-292, 253, 100, -0.7853981633974483], [-294, 253, 100, 0.0], [-295, 254, 100, -0.7853981633974483], [-296, 254, 100, 0.0], [-298, 256, 100, -0.7853981633974483], [-299, 256, 100, 0.0], [-300, 257, 100, -0.7853981633974483], [-301, 257, 100, 0.0], [-303, 259, 100, -0.7853981633974483], [-304, 259, 100, 0.0], [-306, 261, 100, -0.7853981633974483], [-307, 261, 100, 0.0], [-309, 263, 100, -0.7853981633974483], [-310, 263, 100, 0.0], [-312, 265, 100, -0.7853981633974483], [-313, 265, 100, 0.0], [-314, 266, 100, -0.7853981633974483], [-315, 266, 100, 0.0], [-316, 267, 100, -0.7853981633974483], [-316, 474, 100, -1.5707963267948966], [-315, 475, 100, -2.356194490192345], [-271, 475, 100, 3.141592653589793], [-270, 474, 100, 2.356194490192345], [-269, 475, 100, -2.356194490192345], [-256, 475, 100, 3.141592653589793], [-255, 474, 100, 2.356194490192345], [-254, 475, 100, -2.356194490192345], [-236, 475, 100, 3.141592653589793], [-235, 474, 100, 2.356194490192345], [-234, 475, 100, -2.356194490192345], [-216, 475, 100, 3.141592653589793], [-215, 474, 100, 2.356194490192345], [-214, 475, 100, -2.356194490192345], [-48, 475, 100, 3.141592653589793], [-47, 474, 100, 2.356194490192345], [-46, 475, 100, -2.356194490192345], [-28, 475, 100, 3.141592653589793], [-27, 474, 100, 2.356194490192345], [-26, 475, 100, -2.356194490192345], [-16, 475, 100, 3.141592653589793], [-15, 474, 100, 2.356194490192345], [-14, 475, 100, -2.356194490192345], [14, 475, 100, 3.141592653589793], [15, 474, 100, 2.356194490192345], [16, 475, 100, -2.356194490192345], [34, 475, 100, 3.141592653589793], [35, 474, 100, 2.356194490192345], [36, 475, 100, -2.356194490192345], [54, 475, 100, 3.141592653589793], [55, 474, 100, 2.356194490192345], [56, 475, 100, -2.356194490192345], [182, 475, 100, 3.141592653589793], [183, 474, 100, 2.356194490192345], [184, 475, 100, -2.356194490192345], [202, 475, 100, 3.141592653589793], [203, 474, 100, 2.356194490192345], [204, 475, 100, -2.356194490192345], [222, 475, 100, 3.141592653589793], [223, 474, 100, 2.356194490192345], [224, 475, 100, -2.356194490192345], [242, 475, 100, 3.141592653589793], [243, 474, 100, 2.356194490192345], [244, 475, 100, -2.356194490192345], [450, 475, 100, 3.141592653589793], [451, 474, 100, 2.356194490192345], [452, 475, 100, -2.356194490192345], [603, 475, 100, 3.141592653589793], [604, 474, 100, 2.356194490192345], [604, 401, 100, 1.5707963267948966], [603, 400, 100, 0.7853981633974483], [604, 399, 100, 2.356194490192345], [604, 22, 100, 1.5707963267948966], [603, 21, 100, 0.7853981633974483], [604, 20, 100, 2.356194490192345], [604, 15, 100, 1.5707963267948966], [602, 13, 100, 0.7853981633974483], [600, 15, 100, -0.7853981633974483], [601, 16, 100, -2.356194490192345], [599, 18, 100, -0.7853981633974483], [598, 17, 100, 0.7853981633974483], [596, 19, 100, -0.7853981633974483], [597, 20, 100, -2.356194490192345], [595, 22, 100, -0.7853981633974483], [594, 21, 100, 0.7853981633974483], [592, 23, 100, -0.7853981633974483], [593, 24, 100, -2.356194490192345], [591, 26, 100, -0.7853981633974483], [590, 25, 100, 0.7853981633974483], [588, 27, 100, -0.7853981633974483], [589, 28, 100, -2.356194490192345], [587, 30, 100, -0.7853981633974483], [586, 29, 100, 0.7853981633974483], [584, 31, 100, -0.7853981633974483], [585, 32, 100, -2.356194490192345], [583, 34, 100, -0.7853981633974483], [582, 33, 100, 0.7853981633974483], [580, 35, 100, -0.7853981633974483], [581, 36, 100, -2.356194490192345], [577, 40, 100, -0.7853981633974483], [578, 41, 100, -2.356194490192345], [576, 43, 100, -0.7853981633974483], [574, 43, 100, 0.0], [573, 42, 100, 0.7853981633974483], [572, 42, 100, 0.0], [571, 43, 100, -0.7853981633974483], [570, 43, 100, 0.0], [569, 44, 100, -0.7853981633974483], [568, 44, 100, 0.0], [567, 43, 100, 0.7853981633974483], [565, 43, 100, 0.0], [564, 44, 100, -0.7853981633974483], [563, 44, 100, 0.0], [562, 45, 100, -0.7853981633974483], [561, 44, 100, 0.7853981633974483], [560, 45, 100, -0.7853981633974483], [559, 45, 100, 0.0], [558, 46, 100, -0.7853981633974483], [557, 45, 100, 0.7853981633974483], [556, 45, 100, 0.0], [554, 47, 100, -0.7853981633974483], [553, 47, 100, 0.0], [552, 46, 100, 0.7853981633974483], [554, 44, 100, 2.356194490192345], [552, 42, 100, 0.7853981633974483], [551, 42, 100, 0.0], [550, 43, 100, -0.7853981633974483], [549, 43, 100, 0.0], [548, 44, 100, -0.7853981633974483], [550, 46, 100, -2.356194490192345], [548, 48, 100, -0.7853981633974483], [545, 48, 100, 0.0], [544, 49, 100, -0.7853981633974483], [542, 49, 100, 0.0], [541, 48, 100, 0.7853981633974483], [539, 50, 100, -0.7853981633974483], [538, 50, 100, 0.0], [537, 49, 100, 0.7853981633974483], [536, 50, 100, -0.7853981633974483], [535, 50, 100, 0.0], [534, 51, 100, -0.7853981633974483], [533, 50, 100, 0.7853981633974483], [532, 50, 100, 0.0], [531, 51, 100, -0.7853981633974483], [530, 50, 100, 0.7853981633974483], [529, 51, 100, -0.7853981633974483], [528, 51, 100, 0.0], [527, 52, 100, -0.7853981633974483], [525, 50, 100, 0.7853981633974483], [522, 53, 100, -0.7853981633974483], [520, 53, 100, 0.0], [519, 54, 100, -0.7853981633974483], [516, 54, 100, 0.0], [515, 55, 100, -0.7853981633974483], [512, 52, 100, 0.7853981633974483], [511, 52, 100, 0.0], [510, 53, 100, -0.7853981633974483], [509, 53, 100, 0.0], [505, 57, 100, -0.7853981633974483], [504, 56, 100, 0.7853981633974483], [503, 57, 100, -0.7853981633974483], [502, 56, 100, 0.7853981633974483], [501, 56, 100, 0.0], [498, 59, 100, -0.7853981633974483], [495, 59, 100, 0.0], [494, 58, 100, 0.7853981633974483], [493, 58, 100, 0.0], [490, 61, 100, -0.7853981633974483], [487, 61, 100, 0.0], [486, 62, 100, -0.7853981633974483], [483, 62, 100, 0.0], [482, 63, 100, -0.7853981633974483], [479, 63, 100, 0.0], [478, 64, 100, -0.7853981633974483], [475, 64, 100, 0.0], [474, 65, 100, -0.7853981633974483], [471, 65, 100, 0.0], [470, 66, 100, -0.7853981633974483], [467, 66, 100, 0.0], [466, 67, 100, -0.7853981633974483], [463, 67, 100, 0.0], [462, 68, 100, -0.7853981633974483], [459, 68, 100, 0.0], [458, 69, 100, -0.7853981633974483], [455, 69, 100, 0.0], [454, 70, 100, -0.7853981633974483], [452, 70, 100, 0.0], [451, 71, 100, -0.7853981633974483], [448, 71, 100, 0.0], [447, 72, 100, -0.7853981633974483], [444, 72, 100, 0.0], [443, 73, 100, -0.7853981633974483], [440, 73, 100, 0.0], [439, 74, 100, -0.7853981633974483], [436, 74, 100, 0.0], [435, 75, 100, -0.7853981633974483], [434, 75, 100, 0.0], [433, 76, 100, -0.7853981633974483], [432, 75, 100, 0.7853981633974483], [384, 75, 100, 0.0], [383, 76, 100, -0.7853981633974483], [380, 76, 100, 0.0], [379, 77, 100, -0.7853981633974483], [377, 77, 100, 0.0], [376, 78, 100, -0.7853981633974483], [375, 78, 100, 0.0], [374, 79, 100, -0.7853981633974483], [373, 79, 100, 0.0], [372, 80, 100, -0.7853981633974483], [331, 80, 100, 0.0], [330, 79, 100, 0.7853981633974483], [329, 80, 100, -0.7853981633974483], [328, 80, 100, 0.0], [327, 81, 100, -0.7853981633974483], [323, 81, 100, 0.0], [322, 82, 100, -0.7853981633974483], [318, 82, 100, 0.0], [317, 83, 100, -0.7853981633974483], [313, 83, 100, 0.0], [312, 84, 100, -0.7853981633974483], [308, 84, 100, 0.0], [307, 85, 100, -0.7853981633974483], [303, 85, 100, 0.0], [302, 86, 100, -0.7853981633974483], [298, 86, 100, 0.0], [297, 87, 100, -0.7853981633974483], [295, 87, 100, 0.0], [294, 88, 100, -0.7853981633974483], [294, 89, 100, -1.5707963267948966], [292, 91, 100, -0.7853981633974483], [292, 92, 100, -1.5707963267948966], [291, 93, 100, -0.7853981633974483], [291, 94, 100, -1.5707963267948966], [290, 95, 100, -0.7853981633974483], [290, 96, 100, -1.5707963267948966], [289, 97, 100, -0.7853981633974483], [289, 98, 100, -1.5707963267948966], [287, 100, 100, -0.7853981633974483], [287, 101, 100, -1.5707963267948966], [286, 102, 100, -0.7853981633974483], [286, 103, 100, -1.5707963267948966], [285, 104, 100, -0.7853981633974483], [285, 105, 100, -1.5707963267948966], [283, 107, 100, -0.7853981633974483], [283, 108, 100, -1.5707963267948966], [282, 109, 100, -0.7853981633974483], [282, 110, 100, -1.5707963267948966], [280, 112, 100, -0.7853981633974483], [280, 113, 100, -1.5707963267948966], [278, 115, 100, -0.7853981633974483], [278, 116, 100, -1.5707963267948966], [275, 119, 100, -0.7853981633974483], [275, 120, 100, -1.5707963267948966], [272, 123, 100, -0.7853981633974483], [272, 124, 100, -1.5707963267948966], [268, 128, 100, -0.7853981633974483], [268, 129, 100, -1.5707963267948966], [264, 133, 100, -0.7853981633974483], [264, 134, 100, -1.5707963267948966], [259, 139, 100, -0.7853981633974483], [259, 140, 100, -1.5707963267948966], [254, 145, 100, -0.7853981633974483], [254, 146, 100, -1.5707963267948966], [250, 150, 100, -0.7853981633974483], [250, 151, 100, -1.5707963267948966], [245, 156, 100, -0.7853981633974483], [245, 157, 100, -1.5707963267948966], [242, 160, 100, -0.7853981633974483], [242, 161, 100, -1.5707963267948966], [238, 165, 100, -0.7853981633974483], [238, 166, 100, -1.5707963267948966], [235, 169, 100, -0.7853981633974483], [235, 170, 100, -1.5707963267948966], [232, 173, 100, -0.7853981633974483], [229, 173, 100, 0.0], [228, 172, 100, 0.7853981633974483], [226, 172, 100, 0.0], [225, 171, 100, 0.7853981633974483], [224, 171, 100, 0.0], [223, 170, 100, 0.7853981633974483], [221, 170, 100, 0.0], [220, 169, 100, 0.7853981633974483], [218, 169, 100, 0.0], [217, 168, 100, 0.7853981633974483], [215, 168, 100, 0.0], [214, 167, 100, 0.7853981633974483], [212, 167, 100, 0.0], [210, 165, 100, 0.7853981633974483], [209, 166, 100, -0.7853981633974483], [207, 164, 100, 0.7853981633974483], [206, 165, 100, -0.7853981633974483], [105, 165, 100, 0.0], [104, 166, 100, -0.7853981633974483], [94, 166, 100, 0.0], [93, 167, 100, -0.7853981633974483], [87, 167, 100, 0.0], [86, 168, 100, -0.7853981633974483], [81, 168, 100, 0.0], [80, 169, 100, -0.7853981633974483], [76, 169, 100, 0.0], [75, 170, 100, -0.7853981633974483], [71, 170, 100, 0.0], [69, 172, 100, -0.7853981633974483], [69, 173, 100, -1.5707963267948966], [67, 175, 100, -0.7853981633974483], [67, 176, 100, -1.5707963267948966], [66, 177, 100, -0.7853981633974483], [66, 178, 100, -1.5707963267948966], [64, 180, 100, -0.7853981633974483], [64, 181, 100, -1.5707963267948966], [63, 182, 100, -0.7853981633974483], [63, 183, 100, -1.5707963267948966], [62, 184, 100, -0.7853981633974483], [62, 185, 100, -1.5707963267948966], [61, 186, 100, -0.7853981633974483], [61, 187, 100, -1.5707963267948966], [60, 188, 100, -0.7853981633974483], [60, 189, 100, -1.5707963267948966], [59, 190, 100, -0.7853981633974483], [59, 191, 100, -1.5707963267948966], [58, 192, 100, -0.7853981633974483], [58, 193, 100, -1.5707963267948966], [57, 194, 100, -0.7853981633974483], [57, 195, 100, -1.5707963267948966], [56, 196, 100, -0.7853981633974483], [56, 197, 100, -1.5707963267948966], [55, 198, 100, -0.7853981633974483], [55, 199, 100, -1.5707963267948966], [54, 200, 100, -0.7853981633974483], [54, 201, 100, -1.5707963267948966], [53, 202, 100, -0.7853981633974483], [53, 203, 100, -1.5707963267948966], [52, 204, 100, -0.7853981633974483], [52, 205, 100, -1.5707963267948966], [51, 206, 100, -0.7853981633974483], [51, 207, 100, -1.5707963267948966], [50, 208, 100, -0.7853981633974483], [50, 209, 100, -1.5707963267948966], [48, 211, 100, -0.7853981633974483], [48, 212, 100, -1.5707963267948966], [47, 213, 100, -0.7853981633974483], [47, 214, 100, -1.5707963267948966], [45, 216, 100, -0.7853981633974483], [45, 217, 100, -1.5707963267948966], [44, 218, 100, -0.7853981633974483], [44, 219, 100, -1.5707963267948966], [42, 221, 100, -0.7853981633974483], [42, 223, 100, -1.5707963267948966], [38, 227, 100, -0.7853981633974483], [38, 228, 100, -1.5707963267948966], [35, 231, 100, -0.7853981633974483], [35, 232, 100, -1.5707963267948966], [33, 234, 100, -0.7853981633974483], [33, 235, 100, -1.5707963267948966], [29, 239, 100, -0.7853981633974483], [29, 240, 100, -1.5707963267948966], [27, 242, 100, -0.7853981633974483], [27, 243, 100, -1.5707963267948966], [25, 245, 100, -0.7853981633974483], [25, 246, 100, -1.5707963267948966], [23, 248, 100, -0.7853981633974483], [23, 249, 100, -1.5707963267948966], [19, 253, 100, -0.7853981633974483], [19, 254, 100, -1.5707963267948966], [16, 257, 100, -0.7853981633974483], [16, 258, 100, -1.5707963267948966], [12, 262, 100, -0.7853981633974483], [12, 263, 100, -1.5707963267948966], [10, 265, 100, -0.7853981633974483], [-6, 265, 100, 0.0], [-7, 266, 100, -0.7853981633974483], [-8, 265, 100, 0.7853981633974483], [-26, 265, 100, 0.0], [-27, 266, 100, -0.7853981633974483], [-28, 265, 100, 0.7853981633974483], [-96, 265, 100, 0.0], [-156, 205, 100, 0.7853981633974483], [-156, 204, 100, 1.5707963267948966], [-157, 203, 100, 0.7853981633974483], [-157, 201, 100, 1.5707963267948966], [-158, 200, 100, 0.7853981633974483], [-158, 198, 100, 1.5707963267948966], [-159, 197, 100, 0.7853981633974483], [-159, 196, 100, 1.5707963267948966], [-160, 195, 100, 0.7853981633974483], [-160, 194, 100, 1.5707963267948966], [-162, 192, 100, 0.7853981633974483], [-162, 191, 100, 1.5707963267948966], [-164, 189, 100, 0.7853981633974483], [-164, 188, 100, 1.5707963267948966], [-167, 185, 100, 0.7853981633974483], [-164, 182, 100, 2.356194490192345], [-164, 181, 100, 1.5707963267948966], [-162, 179, 100, 2.356194490192345], [-162, 178, 100, 1.5707963267948966], [-160, 176, 100, 2.356194490192345], [-160, 175, 100, 1.5707963267948966], [-159, 174, 100, 2.356194490192345], [-159, 173, 100, 1.5707963267948966], [-158, 172, 100, 2.356194490192345], [-158, 170, 100, 1.5707963267948966], [-157, 169, 100, 2.356194490192345], [-157, 166, 100, 1.5707963267948966], [-156, 165, 100, 2.356194490192345], [-156, 164, 100, 1.5707963267948966], [-155, 163, 100, 2.356194490192345], [-155, 162, 100, 1.5707963267948966], [-154, 161, 100, 2.356194490192345], [-154, 160, 100, 1.5707963267948966], [-153, 159, 100, 2.356194490192345], [-153, 158, 100, 1.5707963267948966], [-152, 157, 100, 2.356194490192345], [-152, 156, 100, 1.5707963267948966], [-150, 154, 100, 2.356194490192345], [-150, 153, 100, 1.5707963267948966], [-148, 151, 100, 2.356194490192345], [-147, 151, 100, 3.141592653589793], [-145, 149, 100, 2.356194490192345], [-144, 149, 100, 3.141592653589793], [-142, 147, 100, 2.356194490192345], [-142, 146, 100, 1.5707963267948966], [-140, 144, 100, 2.356194490192345], [-140, 143, 100, 1.5707963267948966], [-138, 141, 100, 2.356194490192345], [-137, 141, 100, 3.141592653589793], [-135, 139, 100, 2.356194490192345], [-134, 139, 100, 3.141592653589793], [-132, 137, 100, 2.356194490192345], [-132, 136, 100, 1.5707963267948966], [-130, 134, 100, 2.356194490192345], [-130, 133, 100, 1.5707963267948966], [-128, 131, 100, 2.356194490192345], [-127, 131, 100, 3.141592653589793], [-125, 129, 100, 2.356194490192345], [-124, 129, 100, 3.141592653589793], [-123, 128, 100, 2.356194490192345], [-122, 128, 100, 3.141592653589793], [-121, 127, 100, 2.356194490192345], [-120, 127, 100, 3.141592653589793], [-119, 126, 100, 2.356194490192345], [-118, 126, 100, 3.141592653589793], [-117, 125, 100, 2.356194490192345], [-116, 125, 100, 3.141592653589793], [-115, 124, 100, 2.356194490192345], [-112, 124, 100, 3.141592653589793], [-111, 123, 100, 2.356194490192345], [-109, 123, 100, 3.141592653589793], [-108, 122, 100, 2.356194490192345], [-107, 122, 100, 3.141592653589793], [-106, 121, 100, 2.356194490192345], [-105, 121, 100, 3.141592653589793], [-103, 119, 100, 2.356194490192345], [-102, 119, 100, 3.141592653589793], [-100, 117, 100, 2.356194490192345], [-99, 117, 100, 3.141592653589793], [-91, 109, 100, 2.356194490192345], [-90, 109, 100, 3.141592653589793], [-83, 102, 100, 2.356194490192345], [-82, 102, 100, 3.141592653589793], [-79, 99, 100, 2.356194490192345], [-78, 99, 100, 3.141592653589793], [-75, 96, 100, 2.356194490192345], [-111, 60, 100, 0.7853981633974483], [-111, 49, 100, 1.5707963267948966], [-112, 48, 100, 0.7853981633974483], [-112, 46, 100, 1.5707963267948966], [-113, 45, 100, 0.7853981633974483], [-113, 43, 100, 1.5707963267948966], [-114, 42, 100, 0.7853981633974483], [-114, 40, 100, 1.5707963267948966], [-115, 39, 100, 0.7853981633974483], [-115, 36, 100, 1.5707963267948966], [-116, 35, 100, 0.7853981633974483]]

In [34]:
len(path)

1289

In [10]:
path = [[0, 0, 8, 0], [1, 0, 8, 3.141592653589793], [2, 0, 8, 3.141592653589793], [3, 0, 8, 3.141592653589793], [4, 0, 8, 3.141592653589793], [5, 0, 8, 3.141592653589793], [6, -1, 8, 2.356194490192345], [6, -2, 8, 1.5707963267948966], [6, -3, 8, 1.5707963267948966], [7, -4, 8, 2.356194490192345], [7, -5, 8, 1.5707963267948966], [7, -6, 8, 1.5707963267948966], [8, -7, 8, 2.356194490192345], [8, -8, 8, 1.5707963267948966], [8, -9, 8, 1.5707963267948966], [9, -10, 8, 2.356194490192345], [10, -11, 8, 2.356194490192345], [9, -12, 8, 0.7853981633974483], [9, -13, 8, 1.5707963267948966], [9, -14, 8, 1.5707963267948966], [9, -15, 8, 1.5707963267948966], [9, -16, 8, 1.5707963267948966], [9, -17, 8, 1.5707963267948966], [9, -18, 8, 1.5707963267948966], [9, -19, 8, 1.5707963267948966], [9, -20, 8, 1.5707963267948966], [9, -21, 8, 1.5707963267948966], [9, -22, 8, 1.5707963267948966], [9, -23, 8, 1.5707963267948966], [9, -24, 8, 1.5707963267948966], [9, -25, 8, 1.5707963267948966], [9, -26, 8, 1.5707963267948966], [9, -27, 8, 1.5707963267948966], [9, -28, 8, 1.5707963267948966], [9, -29, 8, 1.5707963267948966], [9, -30, 8, 1.5707963267948966], [9, -31, 8, 1.5707963267948966], [9, -32, 8, 1.5707963267948966], [9, -33, 8, 1.5707963267948966], [9, -34, 8, 1.5707963267948966], [9, -35, 8, 1.5707963267948966], [9, -36, 8, 1.5707963267948966], [9, -37, 8, 1.5707963267948966], [9, -38, 8, 1.5707963267948966], [9, -39, 8, 1.5707963267948966], [9, -40, 8, 1.5707963267948966], [9, -41, 8, 1.5707963267948966], [9, -42, 8, 1.5707963267948966], [9, -43, 8, 1.5707963267948966], [9, -44, 8, 1.5707963267948966], [9, -45, 8, 1.5707963267948966], [9, -46, 8, 1.5707963267948966], [9, -47, 8, 1.5707963267948966], [9, -48, 8, 1.5707963267948966], [9, -49, 8, 1.5707963267948966], [9, -50, 8, 1.5707963267948966], [9, -51, 8, 1.5707963267948966], [9, -52, 8, 1.5707963267948966], [9, -53, 8, 1.5707963267948966], [9, -54, 8, 1.5707963267948966], [9, -55, 8, 1.5707963267948966], [9, -56, 8, 1.5707963267948966], [9, -57, 8, 1.5707963267948966], [9, -58, 8, 1.5707963267948966], [9, -59, 8, 1.5707963267948966], [9, -60, 8, 1.5707963267948966], [9, -61, 8, 1.5707963267948966], [9, -62, 8, 1.5707963267948966], [9, -63, 8, 1.5707963267948966], [9, -64, 8, 1.5707963267948966], [8, -65, 8, 0.7853981633974483], [8, -66, 8, 1.5707963267948966], [8, -67, 8, 1.5707963267948966], [7, -68, 8, 0.7853981633974483], [6, -69, 8, 0.7853981633974483], [5, -69, 8, 0.0], [4, -70, 8, 0.7853981633974483], [3, -71, 8, 0.7853981633974483], [2, -71, 8, 0.0], [1, -72, 8, 0.7853981633974483], [0, -73, 8, 0.7853981633974483], [0, -74, 8, 1.5707963267948966], [0, -75, 8, 1.5707963267948966], [-1, -76, 8, 0.7853981633974483], [-1, -77, 8, 1.5707963267948966], [-1, -78, 8, 1.5707963267948966], [-1, -79, 8, 1.5707963267948966], [-1, -80, 8, 1.5707963267948966], [-1, -81, 8, 1.5707963267948966], [-1, -82, 8, 1.5707963267948966], [-1, -83, 8, 1.5707963267948966], [-1, -84, 8, 1.5707963267948966], [-1, -85, 8, 1.5707963267948966], [-1, -86, 8, 1.5707963267948966], [-1, -87, 8, 1.5707963267948966], [-1, -88, 8, 1.5707963267948966], [-1, -89, 8, 1.5707963267948966], [-1, -90, 8, 1.5707963267948966], [-2, -91, 8, 0.7853981633974483], [-2, -92, 8, 1.5707963267948966], [-3, -93, 8, 0.7853981633974483], [-4, -94, 8, 0.7853981633974483], [-5, -95, 8, 0.7853981633974483], [-5, -96, 8, 1.5707963267948966], [-5, -97, 8, 1.5707963267948966], [-6, -98, 8, 0.7853981633974483], [-6, -99, 8, 1.5707963267948966], [-6, -100, 8, 1.5707963267948966], [-6, -101, 8, 1.5707963267948966], [-6, -102, 8, 1.5707963267948966], [-6, -103, 8, 1.5707963267948966], [-6, -104, 8, 1.5707963267948966], [-6, -105, 8, 1.5707963267948966], [-6, -106, 8, 1.5707963267948966], [-6, -107, 8, 1.5707963267948966], [-6, -108, 8, 1.5707963267948966], [-6, -109, 8, 1.5707963267948966], [-6, -110, 8, 1.5707963267948966], [-6, -111, 8, 1.5707963267948966], [-6, -112, 8, 1.5707963267948966], [-7, -113, 8, 0.7853981633974483], [-7, -114, 8, 1.5707963267948966], [-7, -115, 8, 1.5707963267948966], [-8, -116, 8, 0.7853981633974483], [-9, -117, 8, 0.7853981633974483], [-10, -118, 8, 0.7853981633974483], [-11, -119, 8, 0.7853981633974483], [-12, -120, 8, 0.7853981633974483], [-13, -121, 8, 0.7853981633974483], [-13, -122, 8, 1.5707963267948966], [-12, -123, 8, 2.356194490192345], [-12, -124, 8, 1.5707963267948966], [-11, -125, 8, 2.356194490192345], [-10, -126, 8, 2.356194490192345], [-10, -127, 8, 1.5707963267948966], [-9, -128, 8, 2.356194490192345], [-8, -129, 8, 2.356194490192345], [-7, -129, 8, 3.141592653589793], [-6, -129, 8, 3.141592653589793], [-5, -130, 8, 2.356194490192345], [-4, -130, 8, 3.141592653589793], [-3, -130, 8, 3.141592653589793], [-2, -130, 8, 3.141592653589793], [-1, -130, 8, 3.141592653589793], [0, -130, 8, 3.141592653589793], [1, -131, 8, 2.356194490192345], [2, -132, 8, 2.356194490192345], [3, -133, 8, 2.356194490192345], [4, -134, 8, 2.356194490192345], [5, -134, 8, 3.141592653589793], [6, -134, 8, 3.141592653589793], [7, -135, 8, 2.356194490192345], [8, -135, 8, 3.141592653589793], [9, -135, 8, 3.141592653589793], [10, -135, 8, 3.141592653589793], [11, -135, 8, 3.141592653589793], [12, -135, 8, 3.141592653589793], [13, -135, 8, 3.141592653589793], [14, -135, 8, 3.141592653589793], [15, -135, 8, 3.141592653589793], [16, -135, 8, 3.141592653589793], [17, -135, 8, 3.141592653589793], [18, -135, 8, 3.141592653589793], [19, -135, 8, 3.141592653589793], [20, -135, 8, 3.141592653589793], [21, -135, 8, 3.141592653589793], [22, -135, 8, 3.141592653589793], [23, -135, 8, 3.141592653589793], [24, -135, 8, 3.141592653589793], [25, -135, 8, 3.141592653589793], [26, -135, 8, 3.141592653589793], [27, -135, 8, 3.141592653589793], [28, -135, 8, 3.141592653589793], [29, -135, 8, 3.141592653589793], [30, -135, 8, 3.141592653589793], [31, -135, 8, 3.141592653589793], [32, -135, 8, 3.141592653589793], [33, -135, 8, 3.141592653589793], [34, -135, 8, 3.141592653589793], [35, -135, 8, 3.141592653589793], [36, -135, 8, 3.141592653589793], [37, -135, 8, 3.141592653589793], [38, -135, 8, 3.141592653589793], [39, -135, 8, 3.141592653589793], [40, -135, 8, 3.141592653589793], [41, -135, 8, 3.141592653589793], [42, -136, 8, 2.356194490192345], [43, -136, 8, 3.141592653589793], [44, -136, 8, 3.141592653589793], [45, -137, 8, 2.356194490192345], [46, -138, 8, 2.356194490192345], [47, -139, 8, 2.356194490192345], [48, -140, 8, 2.356194490192345], [49, -140, 8, 3.141592653589793], [50, -140, 8, 3.141592653589793], [51, -140, 8, 3.141592653589793], [52, -140, 8, 3.141592653589793], [53, -140, 8, 3.141592653589793], [54, -140, 8, 3.141592653589793], [55, -140, 8, 3.141592653589793], [56, -140, 8, 3.141592653589793], [57, -140, 8, 3.141592653589793], [58, -140, 8, 3.141592653589793], [59, -140, 8, 3.141592653589793], [60, -140, 8, 3.141592653589793], [61, -141, 8, 2.356194490192345], [62, -142, 8, 2.356194490192345], [63, -143, 8, 2.356194490192345], [64, -144, 8, 2.356194490192345], [65, -144, 8, 3.141592653589793], [66, -145, 8, 2.356194490192345], [67, -145, 8, 3.141592653589793], [68, -145, 8, 3.141592653589793], [69, -145, 8, 3.141592653589793], [70, -145, 8, 3.141592653589793], [71, -145, 8, 3.141592653589793], [72, -145, 8, 3.141592653589793], [73, -145, 8, 3.141592653589793], [74, -145, 8, 3.141592653589793], [75, -145, 8, 3.141592653589793], [76, -145, 8, 3.141592653589793], [77, -145, 8, 3.141592653589793], [78, -145, 8, 3.141592653589793], [79, -145, 8, 3.141592653589793], [80, -145, 8, 3.141592653589793], [81, -145, 8, 3.141592653589793], [82, -145, 8, 3.141592653589793], [83, -145, 8, 3.141592653589793], [84, -145, 8, 3.141592653589793], [85, -145, 8, 3.141592653589793], [86, -145, 8, 3.141592653589793], [87, -145, 8, 3.141592653589793], [88, -145, 8, 3.141592653589793], [89, -145, 8, 3.141592653589793], [90, -145, 8, 3.141592653589793], [91, -145, 8, 3.141592653589793], [92, -145, 8, 3.141592653589793], [93, -145, 8, 3.141592653589793], [94, -145, 8, 3.141592653589793], [95, -145, 8, 3.141592653589793], [96, -145, 8, 3.141592653589793], [97, -145, 8, 3.141592653589793], [98, -145, 8, 3.141592653589793], [99, -145, 8, 3.141592653589793], [100, -145, 8, 3.141592653589793], [101, -145, 8, 3.141592653589793], [102, -145, 8, 3.141592653589793], [103, -146, 8, 2.356194490192345], [104, -146, 8, 3.141592653589793], [105, -147, 8, 2.356194490192345], [106, -148, 8, 2.356194490192345], [107, -149, 8, 2.356194490192345], [108, -149, 8, 3.141592653589793], [109, -150, 8, 2.356194490192345], [110, -150, 8, 3.141592653589793], [111, -150, 8, 3.141592653589793], [112, -150, 8, 3.141592653589793], [113, -150, 8, 3.141592653589793], [114, -150, 8, 3.141592653589793], [115, -150, 8, 3.141592653589793], [116, -150, 8, 3.141592653589793], [117, -150, 8, 3.141592653589793], [118, -150, 8, 3.141592653589793], [119, -150, 8, 3.141592653589793], [120, -150, 8, 3.141592653589793], [121, -150, 8, 3.141592653589793], [122, -150, 8, 3.141592653589793], [123, -150, 8, 3.141592653589793], [124, -150, 8, 3.141592653589793], [125, -150, 8, 3.141592653589793], [126, -150, 8, 3.141592653589793], [127, -150, 8, 3.141592653589793], [128, -150, 8, 3.141592653589793], [129, -150, 8, 3.141592653589793], [130, -150, 8, 3.141592653589793], [131, -150, 8, 3.141592653589793], [132, -150, 8, 3.141592653589793], [133, -150, 8, 3.141592653589793], [134, -150, 8, 3.141592653589793], [135, -150, 8, 3.141592653589793], [136, -150, 8, 3.141592653589793], [137, -151, 8, 2.356194490192345], [138, -150, 8, -2.356194490192345], [139, -150, 8, 3.141592653589793], [140, -151, 8, 2.356194490192345], [141, -151, 8, 3.141592653589793], [142, -152, 8, 2.356194490192345], [143, -153, 8, 2.356194490192345], [144, -154, 8, 2.356194490192345], [145, -155, 8, 2.356194490192345], [146, -156, 8, 2.356194490192345], [147, -157, 8, 2.356194490192345], [148, -157, 8, 3.141592653589793], [149, -158, 8, 2.356194490192345], [150, -159, 8, 2.356194490192345], [151, -159, 8, 3.141592653589793], [152, -160, 8, 2.356194490192345], [153, -161, 8, 2.356194490192345], [154, -161, 8, 3.141592653589793], [155, -162, 8, 2.356194490192345], [156, -162, 8, 3.141592653589793], [157, -163, 8, 2.356194490192345], [158, -163, 8, 3.141592653589793], [159, -163, 8, 3.141592653589793], [160, -164, 8, 2.356194490192345], [161, -164, 8, 3.141592653589793], [162, -164, 8, 3.141592653589793], [163, -164, 8, 3.141592653589793], [164, -165, 8, 2.356194490192345], [165, -165, 8, 3.141592653589793], [166, -165, 8, 3.141592653589793], [167, -165, 8, 3.141592653589793], [168, -165, 8, 3.141592653589793], [169, -165, 8, 3.141592653589793], [170, -165, 8, 3.141592653589793], [171, -165, 8, 3.141592653589793], [172, -165, 8, 3.141592653589793], [173, -165, 8, 3.141592653589793], [174, -165, 8, 3.141592653589793], [175, -165, 8, 3.141592653589793], [176, -165, 8, 3.141592653589793], [177, -165, 8, 3.141592653589793], [178, -165, 8, 3.141592653589793], [179, -165, 8, 3.141592653589793], [180, -165, 8, 3.141592653589793], [181, -165, 8, 3.141592653589793], [182, -165, 8, 3.141592653589793], [183, -165, 8, 3.141592653589793], [184, -165, 8, 3.141592653589793], [185, -165, 8, 3.141592653589793], [186, -166, 8, 2.356194490192345], [187, -166, 8, 3.141592653589793], [188, -167, 8, 2.356194490192345], [189, -167, 8, 3.141592653589793], [190, -168, 8, 2.356194490192345], [191, -168, 8, 3.141592653589793], [192, -169, 8, 2.356194490192345], [193, -169, 8, 3.141592653589793], [194, -170, 8, 2.356194490192345], [195, -171, 8, 2.356194490192345], [196, -171, 8, 3.141592653589793], [197, -172, 8, 2.356194490192345], [198, -172, 8, 3.141592653589793], [199, -173, 8, 2.356194490192345], [200, -173, 8, 3.141592653589793], [201, -174, 8, 2.356194490192345], [202, -174, 8, 3.141592653589793], [203, -175, 8, 2.356194490192345], [204, -175, 8, 3.141592653589793], [205, -174, 8, -2.356194490192345], [206, -173, 8, -2.356194490192345], [207, -172, 8, -2.356194490192345], [208, -172, 8, 3.141592653589793], [209, -171, 8, -2.356194490192345], [210, -170, 8, -2.356194490192345], [211, -169, 8, -2.356194490192345], [212, -168, 8, -2.356194490192345], [213, -167, 8, -2.356194490192345], [214, -166, 8, -2.356194490192345], [215, -166, 8, 3.141592653589793], [216, -166, 8, 3.141592653589793], [217, -165, 8, -2.356194490192345], [218, -165, 8, 3.141592653589793], [219, -165, 8, 3.141592653589793], [220, -165, 8, 3.141592653589793], [221, -165, 8, 3.141592653589793], [222, -164, 8, -2.356194490192345], [223, -164, 8, 3.141592653589793], [224, -164, 8, 3.141592653589793], [225, -163, 8, -2.356194490192345], [226, -162, 8, -2.356194490192345], [227, -161, 8, -2.356194490192345], [228, -161, 8, 3.141592653589793], [229, -160, 8, -2.356194490192345], [230, -159, 8, -2.356194490192345], [231, -158, 8, -2.356194490192345], [232, -157, 8, -2.356194490192345], [233, -156, 8, -2.356194490192345], [234, -155, 8, -2.356194490192345], [235, -154, 8, -2.356194490192345], [236, -153, 8, -2.356194490192345], [237, -152, 8, -2.356194490192345], [238, -151, 8, -2.356194490192345], [239, -150, 8, -2.356194490192345], [240, -149, 8, -2.356194490192345], [241, -148, 8, -2.356194490192345], [242, -147, 8, -2.356194490192345], [243, -146, 8, -2.356194490192345], [244, -145, 8, -2.356194490192345], [245, -144, 8, -2.356194490192345], [246, -143, 8, -2.356194490192345], [247, -142, 8, -2.356194490192345], [248, -142, 8, 3.141592653589793], [249, -142, 8, 3.141592653589793], [250, -142, 8, 3.141592653589793], [251, -142, 8, 3.141592653589793], [252, -141, 8, -2.356194490192345], [253, -141, 8, 3.141592653589793], [254, -141, 8, 3.141592653589793], [255, -141, 8, 3.141592653589793], [256, -141, 8, 3.141592653589793], [257, -140, 8, -2.356194490192345], [258, -140, 8, 3.141592653589793], [259, -140, 8, 3.141592653589793], [260, -140, 8, 3.141592653589793], [261, -139, 8, -2.356194490192345], [262, -139, 8, 3.141592653589793], [263, -139, 8, 3.141592653589793], [264, -139, 8, 3.141592653589793], [265, -139, 8, 3.141592653589793], [266, -138, 8, -2.356194490192345], [267, -138, 8, 3.141592653589793], [268, -138, 8, 3.141592653589793], [269, -138, 8, 3.141592653589793], [270, -138, 8, 3.141592653589793], [271, -137, 8, -2.356194490192345], [272, -137, 8, 3.141592653589793], [273, -138, 8, 2.356194490192345], [273, -139, 8, 1.5707963267948966], [273, -140, 8, 1.5707963267948966], [274, -141, 8, 2.356194490192345], [274, -142, 8, 1.5707963267948966], [274, -143, 8, 1.5707963267948966], [275, -144, 8, 2.356194490192345], [275, -145, 8, 1.5707963267948966], [276, -146, 8, 2.356194490192345], [276, -147, 8, 1.5707963267948966], [277, -148, 8, 2.356194490192345], [278, -149, 8, 2.356194490192345], [279, -150, 8, 2.356194490192345], [280, -151, 8, 2.356194490192345], [281, -152, 8, 2.356194490192345], [282, -153, 8, 2.356194490192345], [283, -154, 8, 2.356194490192345], [284, -155, 8, 2.356194490192345], [285, -156, 8, 2.356194490192345], [286, -157, 8, 2.356194490192345], [287, -158, 8, 2.356194490192345], [288, -159, 8, 2.356194490192345], [289, -160, 8, 2.356194490192345], [289, -161, 8, 1.5707963267948966], [290, -162, 8, 2.356194490192345], [291, -163, 8, 2.356194490192345], [292, -164, 8, 2.356194490192345], [293, -165, 8, 2.356194490192345], [294, -166, 8, 2.356194490192345], [295, -167, 8, 2.356194490192345], [296, -168, 8, 2.356194490192345], [296, -169, 8, 1.5707963267948966], [297, -170, 8, 2.356194490192345], [298, -171, 8, 2.356194490192345], [298, -172, 8, 1.5707963267948966], [299, -173, 8, 2.356194490192345], [300, -174, 8, 2.356194490192345], [301, -175, 8, 2.356194490192345], [301, -176, 8, 1.5707963267948966], [302, -177, 8, 2.356194490192345], [303, -178, 8, 2.356194490192345], [303, -179, 8, 1.5707963267948966], [304, -180, 8, 2.356194490192345], [305, -180, 8, 3.141592653589793], [306, -180, 8, 3.141592653589793], [307, -180, 8, 3.141592653589793], [308, -180, 8, 3.141592653589793], [309, -180, 8, 3.141592653589793], [310, -180, 8, 3.141592653589793], [311, -180, 8, 3.141592653589793], [312, -180, 8, 3.141592653589793], [313, -180, 8, 3.141592653589793], [314, -180, 8, 3.141592653589793], [315, -180, 8, 3.141592653589793], [316, -180, 8, 3.141592653589793], [317, -180, 8, 3.141592653589793], [318, -180, 8, 3.141592653589793], [319, -180, 8, 3.141592653589793], [320, -180, 8, 3.141592653589793], [321, -180, 8, 3.141592653589793], [322, -180, 8, 3.141592653589793], [323, -180, 8, 3.141592653589793], [324, -180, 8, 3.141592653589793], [325, -180, 8, 3.141592653589793], [326, -180, 8, 3.141592653589793], [327, -180, 8, 3.141592653589793], [328, -180, 8, 3.141592653589793], [329, -180, 8, 3.141592653589793], [330, -180, 8, 3.141592653589793], [331, -180, 8, 3.141592653589793], [332, -180, 8, 3.141592653589793], [333, -180, 8, 3.141592653589793], [334, -180, 8, 3.141592653589793], [335, -180, 8, 3.141592653589793], [336, -180, 8, 3.141592653589793], [337, -180, 8, 3.141592653589793], [338, -180, 8, 3.141592653589793], [339, -180, 8, 3.141592653589793], [340, -180, 8, 3.141592653589793], [341, -180, 8, 3.141592653589793], [342, -180, 8, 3.141592653589793], [343, -180, 8, 3.141592653589793], [344, -181, 8, 2.356194490192345], [345, -181, 8, 3.141592653589793], [346, -181, 8, 3.141592653589793], [347, -182, 8, 2.356194490192345], [348, -182, 8, 3.141592653589793], [349, -183, 8, 2.356194490192345], [350, -183, 8, 3.141592653589793], [351, -184, 8, 2.356194490192345], [352, -184, 8, 3.141592653589793], [353, -185, 8, 2.356194490192345], [354, -185, 8, 3.141592653589793], [355, -185, 8, 3.141592653589793], [356, -185, 8, 3.141592653589793], [357, -185, 8, 3.141592653589793], [358, -185, 8, 3.141592653589793], [359, -185, 8, 3.141592653589793], [360, -185, 8, 3.141592653589793], [361, -185, 8, 3.141592653589793], [362, -185, 8, 3.141592653589793], [363, -185, 8, 3.141592653589793], [364, -185, 8, 3.141592653589793], [365, -185, 8, 3.141592653589793], [366, -185, 8, 3.141592653589793], [367, -185, 8, 3.141592653589793], [368, -185, 8, 3.141592653589793], [369, -185, 8, 3.141592653589793], [370, -185, 8, 3.141592653589793], [371, -185, 8, 3.141592653589793], [372, -185, 8, 3.141592653589793], [373, -185, 8, 3.141592653589793], [374, -186, 8, 2.356194490192345], [375, -187, 8, 2.356194490192345], [375, -188, 8, 1.5707963267948966], [376, -189, 8, 2.356194490192345], [376, -190, 8, 1.5707963267948966], [377, -191, 8, 2.356194490192345], [377, -192, 8, 1.5707963267948966], [378, -193, 8, 2.356194490192345], [378, -194, 8, 1.5707963267948966], [378, -195, 8, 1.5707963267948966], [379, -196, 8, 2.356194490192345], [379, -197, 8, 1.5707963267948966], [379, -198, 8, 1.5707963267948966], [379, -199, 8, 1.5707963267948966], [379, -200, 8, 1.5707963267948966], [379, -201, 8, 1.5707963267948966], [379, -202, 8, 1.5707963267948966], [379, -203, 8, 1.5707963267948966], [379, -204, 8, 1.5707963267948966], [379, -205, 8, 1.5707963267948966], [379, -206, 8, 1.5707963267948966], [379, -207, 8, 1.5707963267948966], [379, -208, 8, 1.5707963267948966], [379, -209, 8, 1.5707963267948966], [379, -210, 8, 1.5707963267948966], [379, -211, 8, 1.5707963267948966], [379, -212, 8, 1.5707963267948966], [379, -213, 8, 1.5707963267948966], [379, -214, 8, 1.5707963267948966], [379, -215, 8, 1.5707963267948966], [379, -216, 8, 1.5707963267948966], [379, -217, 8, 1.5707963267948966], [379, -218, 8, 1.5707963267948966], [379, -219, 8, 1.5707963267948966], [379, -220, 8, 1.5707963267948966], [379, -221, 8, 1.5707963267948966], [379, -222, 8, 1.5707963267948966], [379, -223, 8, 1.5707963267948966], [379, -224, 8, 1.5707963267948966], [379, -225, 8, 1.5707963267948966], [379, -226, 8, 1.5707963267948966], [379, -227, 8, 1.5707963267948966], [379, -228, 8, 1.5707963267948966], [379, -229, 8, 1.5707963267948966], [379, -230, 8, 1.5707963267948966], [379, -231, 8, 1.5707963267948966], [379, -232, 8, 1.5707963267948966], [379, -233, 8, 1.5707963267948966], [379, -234, 8, 1.5707963267948966], [379, -235, 8, 1.5707963267948966], [379, -236, 8, 1.5707963267948966], [378, -237, 8, 0.7853981633974483], [379, -238, 8, 2.356194490192345], [380, -239, 8, 2.356194490192345], [381, -240, 8, 2.356194490192345], [382, -241, 8, 2.356194490192345], [382, -242, 8, 1.5707963267948966], [383, -243, 8, 2.356194490192345], [384, -244, 8, 2.356194490192345], [384, -245, 8, 1.5707963267948966], [385, -246, 8, 2.356194490192345], [386, -247, 8, 2.356194490192345], [386, -248, 8, 1.5707963267948966], [387, -249, 8, 2.356194490192345], [388, -250, 8, 2.356194490192345], [388, -251, 8, 1.5707963267948966], [389, -252, 8, 2.356194490192345], [390, -253, 8, 2.356194490192345], [390, -254, 8, 1.5707963267948966], [391, -255, 8, 2.356194490192345], [392, -256, 8, 2.356194490192345], [393, -257, 8, 2.356194490192345], [393, -258, 8, 1.5707963267948966], [394, -259, 8, 2.356194490192345], [394, -260, 8, 1.5707963267948966], [395, -261, 8, 2.356194490192345], [396, -262, 8, 2.356194490192345], [397, -263, 8, 2.356194490192345], [398, -262, 8, -2.356194490192345], [399, -263, 8, 2.356194490192345], [400, -264, 8, 2.356194490192345], [400, -265, 8, 1.5707963267948966], [400, -266, 8, 1.5707963267948966], [399, -267, 8, 0.7853981633974483], [398, -268, 8, 0.7853981633974483], [399, -269, 8, 2.356194490192345], [399, -270, 8, 1.5707963267948966], [400, -271, 8, 2.356194490192345], [399, -272, 8, 0.7853981633974483], [399, -273, 8, 1.5707963267948966], [400, -274, 8, 2.356194490192345], [401, -274, 8, 3.141592653589793], [402, -275, 8, 2.356194490192345], [402, -276, 8, 1.5707963267948966], [403, -277, 8, 2.356194490192345], [404, -278, 8, 2.356194490192345], [404, -279, 8, 1.5707963267948966], [404, -280, 8, 1.5707963267948966], [405, -281, 8, 2.356194490192345], [406, -281, 8, 3.141592653589793], [407, -282, 8, 2.356194490192345], [408, -282, 8, 3.141592653589793], [409, -283, 8, 2.356194490192345], [410, -283, 8, 3.141592653589793], [411, -284, 8, 2.356194490192345], [412, -284, 8, 3.141592653589793], [413, -284, 8, 3.141592653589793], [414, -285, 8, 2.356194490192345], [415, -284, 8, -2.356194490192345], [416, -284, 8, 3.141592653589793], [417, -284, 8, 3.141592653589793], [418, -284, 8, 3.141592653589793], [419, -285, 8, 2.356194490192345], [420, -285, 8, 3.141592653589793], [421, -285, 8, 3.141592653589793], [422, -285, 8, 3.141592653589793], [423, -285, 8, 3.141592653589793], [424, -285, 8, 3.141592653589793], [425, -285, 8, 3.141592653589793], [426, -285, 8, 3.141592653589793], [427, -285, 8, 3.141592653589793], [428, -285, 8, 3.141592653589793], [429, -285, 8, 3.141592653589793], [430, -285, 8, 3.141592653589793], [431, -285, 8, 3.141592653589793], [432, -285, 8, 3.141592653589793], [433, -285, 8, 3.141592653589793], [434, -285, 8, 3.141592653589793], [435, -284, 8, -2.356194490192345], [436, -283, 8, -2.356194490192345], [437, -282, 8, -2.356194490192345], [438, -281, 8, -2.356194490192345], [439, -280, 8, -2.356194490192345], [440, -279, 8, -2.356194490192345], [441, -279, 8, 3.141592653589793], [442, -278, 8, -2.356194490192345], [443, -277, 8, -2.356194490192345], [444, -276, 8, -2.356194490192345], [445, -275, 8, -2.356194490192345], [446, -274, 8, -2.356194490192345], [447, -273, 8, -2.356194490192345], [448, -272, 8, -2.356194490192345], [449, -271, 8, -2.356194490192345], [450, -271, 8, 3.141592653589793], [451, -270, 8, -2.356194490192345], [452, -269, 8, -2.356194490192345], [453, -268, 8, -2.356194490192345], [454, -268, 8, 3.141592653589793], [455, -267, 8, -2.356194490192345], [456, -266, 8, -2.356194490192345], [457, -265, 8, -2.356194490192345], [458, -265, 8, 3.141592653589793], [459, -264, 8, -2.356194490192345], [460, -264, 8, 3.141592653589793], [461, -263, 8, -2.356194490192345], [462, -262, 8, -2.356194490192345], [463, -262, 8, 3.141592653589793], [464, -261, 8, -2.356194490192345], [465, -261, 8, 3.141592653589793], [466, -260, 8, -2.356194490192345], [467, -260, 8, 3.141592653589793], [468, -259, 8, -2.356194490192345], [469, -259, 8, 3.141592653589793], [470, -259, 8, 3.141592653589793], [471, -258, 8, -2.356194490192345], [472, -257, 8, -2.356194490192345], [473, -256, 8, -2.356194490192345], [474, -255, 8, -2.356194490192345], [475, -254, 8, -2.356194490192345], [476, -253, 8, -2.356194490192345], [477, -252, 8, -2.356194490192345], [478, -251, 8, -2.356194490192345], [479, -250, 8, -2.356194490192345], [480, -250, 8, 3.141592653589793], [481, -249, 8, -2.356194490192345], [482, -248, 8, -2.356194490192345], [483, -247, 8, -2.356194490192345], [484, -246, 8, -2.356194490192345], [485, -245, 8, -2.356194490192345], [486, -244, 8, -2.356194490192345], [487, -244, 8, 3.141592653589793], [488, -243, 8, -2.356194490192345], [489, -243, 8, 3.141592653589793], [490, -242, 8, -2.356194490192345], [491, -242, 8, 3.141592653589793], [492, -241, 8, -2.356194490192345], [493, -241, 8, 3.141592653589793], [494, -240, 8, -2.356194490192345], [495, -239, 8, -2.356194490192345], [496, -239, 8, 3.141592653589793], [497, -238, 8, -2.356194490192345], [498, -237, 8, -2.356194490192345], [498, -236, 8, -1.5707963267948966], [498, -235, 8, -1.5707963267948966], [499, -234, 8, -2.356194490192345], [499, -233, 8, -1.5707963267948966], [499, -232, 8, -1.5707963267948966], [499, -231, 8, -1.5707963267948966], [499, -230, 8, -1.5707963267948966], [499, -229, 8, -1.5707963267948966], [499, -228, 8, -1.5707963267948966], [499, -227, 8, -1.5707963267948966], [499, -226, 8, -1.5707963267948966], [499, -225, 8, -1.5707963267948966], [499, -224, 8, -1.5707963267948966], [499, -223, 8, -1.5707963267948966], [499, -222, 8, -1.5707963267948966], [499, -221, 8, -1.5707963267948966], [499, -220, 8, -1.5707963267948966], [499, -219, 8, -1.5707963267948966], [499, -218, 8, -1.5707963267948966], [499, -217, 8, -1.5707963267948966], [499, -216, 8, -1.5707963267948966], [500, -215, 8, -2.356194490192345], [500, -214, 8, -1.5707963267948966], [500, -213, 8, -1.5707963267948966], [501, -212, 8, -2.356194490192345], [501, -211, 8, -1.5707963267948966], [502, -210, 8, -2.356194490192345], [502, -209, 8, -1.5707963267948966], [503, -208, 8, -2.356194490192345], [503, -207, 8, -1.5707963267948966], [504, -206, 8, -2.356194490192345], [504, -205, 8, -1.5707963267948966], [505, -204, 8, -2.356194490192345], [505, -203, 8, -1.5707963267948966], [505, -202, 8, -1.5707963267948966], [505, -201, 8, -1.5707963267948966], [506, -200, 8, -2.356194490192345], [505, -199, 8, -0.7853981633974483], [505, -198, 8, -1.5707963267948966], [505, -197, 8, -1.5707963267948966], [505, -196, 8, -1.5707963267948966], [504, -195, 8, -0.7853981633974483], [504, -194, 8, -1.5707963267948966], [504, -193, 8, -1.5707963267948966], [504, -192, 8, -1.5707963267948966], [504, -191, 8, -1.5707963267948966], [504, -190, 8, -1.5707963267948966], [504, -189, 8, -1.5707963267948966], [504, -188, 8, -1.5707963267948966], [504, -187, 8, -1.5707963267948966], [504, -186, 8, -1.5707963267948966], [504, -185, 8, -1.5707963267948966], [504, -184, 8, -1.5707963267948966], [504, -183, 8, -1.5707963267948966], [504, -182, 8, -1.5707963267948966], [504, -181, 8, -1.5707963267948966], [504, -180, 8, -1.5707963267948966], [504, -179, 8, -1.5707963267948966], [504, -178, 8, -1.5707963267948966], [504, -177, 8, -1.5707963267948966], [504, -176, 8, -1.5707963267948966], [504, -175, 8, -1.5707963267948966], [503, -174, 8, -0.7853981633974483], [503, -173, 8, -1.5707963267948966], [503, -172, 8, -1.5707963267948966], [503, -171, 8, -1.5707963267948966], [502, -170, 8, -0.7853981633974483], [502, -169, 8, -1.5707963267948966], [502, -168, 8, -1.5707963267948966], [501, -167, 8, -0.7853981633974483], [501, -166, 8, -1.5707963267948966], [500, -165, 8, -0.7853981633974483], [500, -164, 8, -1.5707963267948966], [499, -163, 8, -0.7853981633974483], [498, -162, 8, -0.7853981633974483], [498, -161, 8, -1.5707963267948966], [498, -160, 8, -1.5707963267948966], [497, -159, 8, -0.7853981633974483], [497, -158, 8, -1.5707963267948966], [497, -157, 8, -1.5707963267948966], [496, -156, 8, -0.7853981633974483], [496, -155, 8, -1.5707963267948966], [496, -154, 8, -1.5707963267948966], [495, -153, 8, -0.7853981633974483], [495, -152, 8, -1.5707963267948966], [494, -151, 8, -0.7853981633974483], [494, -150, 8, -1.5707963267948966], [493, -149, 8, -0.7853981633974483], [493, -148, 8, -1.5707963267948966], [492, -147, 8, -0.7853981633974483], [492, -146, 8, -1.5707963267948966], [491, -145, 8, -0.7853981633974483], [491, -144, 8, -1.5707963267948966], [490, -143, 8, -0.7853981633974483], [490, -142, 8, -1.5707963267948966], [489, -141, 8, -0.7853981633974483], [489, -140, 8, -1.5707963267948966], [488, -139, 8, -0.7853981633974483], [487, -138, 8, -0.7853981633974483], [486, -137, 8, -0.7853981633974483], [485, -136, 8, -0.7853981633974483], [484, -135, 8, -0.7853981633974483], [483, -134, 8, -0.7853981633974483], [482, -133, 8, -0.7853981633974483], [481, -132, 8, -0.7853981633974483], [480, -131, 8, -0.7853981633974483], [479, -130, 8, -0.7853981633974483], [478, -129, 8, -0.7853981633974483], [477, -128, 8, -0.7853981633974483], [476, -127, 8, -0.7853981633974483], [475, -126, 8, -0.7853981633974483], [474, -125, 8, -0.7853981633974483], [473, -124, 8, -0.7853981633974483], [472, -123, 8, -0.7853981633974483], [471, -122, 8, -0.7853981633974483], [470, -121, 8, -0.7853981633974483], [469, -120, 8, -0.7853981633974483], [468, -119, 8, -0.7853981633974483], [467, -119, 8, 0.0], [466, -119, 8, 0.0], [465, -119, 8, 0.0], [464, -119, 8, 0.0], [463, -119, 8, 0.0], [462, -119, 8, 0.0], [461, -119, 8, 0.0], [460, -119, 8, 0.0], [459, -119, 8, 0.0], [458, -119, 8, 0.0], [457, -118, 8, -0.7853981633974483], [456, -118, 8, 0.0], [455, -118, 8, 0.0], [454, -118, 8, 0.0], [453, -118, 8, 0.0], [452, -117, 8, -0.7853981633974483], [451, -117, 8, 0.0], [450, -118, 8, 0.7853981633974483], [449, -118, 8, 0.0], [448, -117, 8, -0.7853981633974483], [447, -118, 8, 0.7853981633974483], [446, -118, 8, 0.0], [445, -118, 8, 0.0], [444, -117, 8, -0.7853981633974483], [443, -117, 8, 0.0], [442, -117, 8, 0.0], [441, -118, 8, 0.7853981633974483], [440, -117, 8, -0.7853981633974483], [439, -117, 8, 0.0], [438, -118, 8, 0.7853981633974483], [437, -117, 8, -0.7853981633974483], [436, -117, 8, 0.0], [435, -117, 8, 0.0], [434, -117, 8, 0.0], [433, -116, 8, -0.7853981633974483], [433, -115, 8, -1.5707963267948966], [432, -114, 8, -0.7853981633974483], [432, -113, 8, -1.5707963267948966], [431, -112, 8, -0.7853981633974483], [431, -111, 8, -1.5707963267948966], [430, -110, 8, -0.7853981633974483], [430, -109, 8, -1.5707963267948966], [429, -108, 8, -0.7853981633974483], [429, -107, 8, -1.5707963267948966], [428, -106, 8, -0.7853981633974483], [427, -105, 8, -0.7853981633974483], [427, -104, 8, -1.5707963267948966], [426, -103, 8, -0.7853981633974483], [426, -102, 8, -1.5707963267948966], [425, -101, 8, -0.7853981633974483], [425, -100, 8, -1.5707963267948966], [424, -99, 8, -0.7853981633974483], [424, -98, 8, -1.5707963267948966], [423, -97, 8, -0.7853981633974483], [422, -96, 8, -0.7853981633974483], [421, -95, 8, -0.7853981633974483], [420, -94, 8, -0.7853981633974483], [420, -93, 8, -1.5707963267948966], [419, -92, 8, -0.7853981633974483], [420, -91, 8, -2.356194490192345], [421, -90, 8, -2.356194490192345], [422, -89, 8, -2.356194490192345], [423, -88, 8, -2.356194490192345], [424, -87, 8, -2.356194490192345], [425, -86, 8, -2.356194490192345], [426, -85, 8, -2.356194490192345], [426, -84, 8, -1.5707963267948966], [425, -83, 8, -0.7853981633974483], [424, -84, 8, 0.7853981633974483], [423, -85, 8, 0.7853981633974483], [422, -86, 8, 0.7853981633974483], [421, -87, 8, 0.7853981633974483], [420, -88, 8, 0.7853981633974483], [419, -89, 8, 0.7853981633974483], [418, -90, 8, 0.7853981633974483], [417, -89, 8, -0.7853981633974483], [416, -88, 8, -0.7853981633974483], [415, -87, 8, -0.7853981633974483], [415, -86, 8, -1.5707963267948966], [414, -85, 8, -0.7853981633974483], [413, -84, 8, -0.7853981633974483], [413, -83, 8, -1.5707963267948966], [412, -82, 8, -0.7853981633974483], [412, -81, 8, -1.5707963267948966], [411, -80, 8, -0.7853981633974483], [411, -79, 8, -1.5707963267948966], [410, -78, 8, -0.7853981633974483], [410, -77, 8, -1.5707963267948966], [409, -76, 8, -0.7853981633974483], [409, -75, 8, -1.5707963267948966], [409, -74, 8, -1.5707963267948966], [408, -73, 8, -0.7853981633974483], [408, -72, 8, -1.5707963267948966], [408, -71, 8, -1.5707963267948966], [408, -70, 8, -1.5707963267948966], [408, -69, 8, -1.5707963267948966], [408, -68, 8, -1.5707963267948966], [407, -67, 8, -0.7853981633974483], [407, -66, 8, -1.5707963267948966], [406, -65, 8, -0.7853981633974483], [405, -64, 8, -0.7853981633974483], [405, -63, 8, -1.5707963267948966], [404, -62, 8, -0.7853981633974483], [404, -61, 8, -1.5707963267948966], [404, -60, 8, -1.5707963267948966], [403, -59, 8, -0.7853981633974483], [402, -58, 8, -0.7853981633974483], [401, -57, 8, -0.7853981633974483], [400, -56, 8, -0.7853981633974483], [400, -55, 8, -1.5707963267948966], [399, -54, 8, -0.7853981633974483], [399, -53, 8, -1.5707963267948966], [399, -52, 8, -1.5707963267948966], [399, -51, 8, -1.5707963267948966], [398, -50, 8, -0.7853981633974483], [398, -49, 8, -1.5707963267948966], [398, -48, 8, -1.5707963267948966], [398, -47, 8, -1.5707963267948966], [398, -46, 8, -1.5707963267948966], [398, -45, 8, -1.5707963267948966], [398, -44, 8, -1.5707963267948966], [398, -43, 8, -1.5707963267948966], [398, -42, 8, -1.5707963267948966], [398, -41, 8, -1.5707963267948966], [398, -40, 8, -1.5707963267948966], [398, -39, 8, -1.5707963267948966], [399, -38, 8, -2.356194490192345], [400, -37, 8, -2.356194490192345], [400, -36, 8, -1.5707963267948966], [401, -35, 8, -2.356194490192345], [402, -34, 8, -2.356194490192345], [402, -33, 8, -1.5707963267948966], [403, -32, 8, -2.356194490192345], [403, -31, 8, -1.5707963267948966], [404, -30, 8, -2.356194490192345], [404, -29, 8, -1.5707963267948966], [405, -28, 8, -2.356194490192345], [406, -27, 8, -2.356194490192345], [406, -26, 8, -1.5707963267948966], [405, -25, 8, -0.7853981633974483], [405, -24, 8, -1.5707963267948966], [405, -23, 8, -1.5707963267948966], [404, -22, 8, -0.7853981633974483], [404, -21, 8, -1.5707963267948966], [404, -20, 8, -1.5707963267948966], [404, -19, 8, -1.5707963267948966], [404, -18, 8, -1.5707963267948966], [404, -17, 8, -1.5707963267948966], [404, -16, 8, -1.5707963267948966], [404, -15, 8, -1.5707963267948966], [404, -14, 8, -1.5707963267948966], [404, -13, 8, -1.5707963267948966], [404, -12, 8, -1.5707963267948966], [404, -11, 8, -1.5707963267948966], [404, -10, 8, -1.5707963267948966], [404, -9, 8, -1.5707963267948966], [404, -8, 8, -1.5707963267948966], [404, -7, 8, -1.5707963267948966], [404, -6, 8, -1.5707963267948966], [404, -5, 8, -1.5707963267948966], [404, -4, 8, -1.5707963267948966], [404, -3, 8, -1.5707963267948966], [404, -2, 8, -1.5707963267948966], [404, -1, 8, -1.5707963267948966], [404, 0, 8, -1.5707963267948966], [404, 1, 8, -1.5707963267948966], [404, 2, 8, -1.5707963267948966], [404, 3, 8, -1.5707963267948966], [405, 4, 8, -2.356194490192345], [405, 5, 8, -1.5707963267948966], [406, 6, 8, -2.356194490192345], [407, 7, 8, -2.356194490192345], [408, 8, 8, -2.356194490192345], [407, 9, 8, -0.7853981633974483], [408, 10, 8, -2.356194490192345], [407, 11, 8, -0.7853981633974483], [408, 12, 8, -2.356194490192345], [407, 13, 8, -0.7853981633974483], [408, 14, 8, -2.356194490192345], [408, 15, 8, -1.5707963267948966], [407, 16, 8, -0.7853981633974483], [407, 17, 8, -1.5707963267948966], [408, 18, 8, -2.356194490192345], [408, 19, 8, -1.5707963267948966], [408, 20, 8, -1.5707963267948966], [408, 21, 8, -1.5707963267948966], [408, 22, 8, -1.5707963267948966], [408, 23, 8, -1.5707963267948966], [409, 24, 8, -2.356194490192345], [409, 25, 8, -1.5707963267948966], [410, 26, 8, -2.356194490192345], [409, 27, 8, -0.7853981633974483], [409, 28, 8, -1.5707963267948966], [410, 29, 8, -2.356194490192345], [409, 30, 8, -0.7853981633974483], [410, 31, 8, -2.356194490192345], [411, 32, 8, -2.356194490192345], [412, 33, 8, -2.356194490192345], [413, 34, 8, -2.356194490192345], [413, 35, 8, -1.5707963267948966], [414, 36, 8, -2.356194490192345], [414, 37, 8, -1.5707963267948966], [414, 38, 8, -1.5707963267948966], [414, 39, 8, -1.5707963267948966], [414, 40, 8, -1.5707963267948966], [414, 41, 8, -1.5707963267948966], [414, 42, 8, -1.5707963267948966], [414, 43, 8, -1.5707963267948966], [414, 44, 8, -1.5707963267948966], [414, 45, 8, -1.5707963267948966], [415, 46, 8, -2.356194490192345], [414, 47, 8, -0.7853981633974483], [414, 48, 8, -1.5707963267948966], [415, 49, 8, -2.356194490192345], [415, 50, 8, -1.5707963267948966], [415, 51, 8, -1.5707963267948966], [415, 52, 8, -1.5707963267948966], [416, 53, 8, -2.356194490192345], [416, 54, 8, -1.5707963267948966], [417, 55, 8, -2.356194490192345], [418, 56, 8, -2.356194490192345], [419, 57, 8, -2.356194490192345], [418, 58, 8, -0.7853981633974483], [418, 59, 8, -1.5707963267948966], [418, 60, 8, -1.5707963267948966], [418, 61, 8, -1.5707963267948966], [418, 62, 8, -1.5707963267948966], [418, 63, 8, -1.5707963267948966], [418, 64, 8, -1.5707963267948966], [417, 65, 8, -0.7853981633974483], [417, 66, 8, -1.5707963267948966], [417, 67, 8, -1.5707963267948966], [416, 68, 8, -0.7853981633974483], [416, 69, 8, -1.5707963267948966], [415, 70, 8, -0.7853981633974483], [414, 71, 8, -0.7853981633974483], [414, 72, 8, -1.5707963267948966], [413, 73, 8, -0.7853981633974483], [412, 74, 8, -0.7853981633974483], [411, 75, 8, -0.7853981633974483], [410, 75, 8, 0.0], [409, 75, 8, 0.0], [408, 75, 8, 0.0], [407, 75, 8, 0.0], [406, 75, 8, 0.0], [405, 75, 8, 0.0], [404, 75, 8, 0.0], [403, 75, 8, 0.0], [402, 75, 8, 0.0], [401, 75, 8, 0.0], [400, 75, 8, 0.0], [399, 75, 8, 0.0], [398, 75, 8, 0.0], [397, 75, 8, 0.0], [396, 75, 8, 0.0], [395, 75, 8, 0.0], [394, 75, 8, 0.0], [393, 75, 8, 0.0], [392, 75, 8, 0.0], [391, 75, 8, 0.0], [390, 75, 8, 0.0], [389, 75, 8, 0.0], [388, 75, 8, 0.0], [387, 75, 8, 0.0], [386, 75, 8, 0.0], [385, 75, 8, 0.0], [384, 75, 8, 0.0], [383, 76, 8, -0.7853981633974483], [382, 76, 8, 0.0], [381, 76, 8, 0.0], [380, 76, 8, 0.0], [379, 77, 8, -0.7853981633974483], [378, 77, 8, 0.0], [377, 77, 8, 0.0], [376, 78, 8, -0.7853981633974483], [375, 78, 8, 0.0], [374, 79, 8, -0.7853981633974483], [373, 79, 8, 0.0], [372, 80, 8, -0.7853981633974483], [372, 81, 8, -1.5707963267948966], [371, 82, 8, -0.7853981633974483], [370, 81, 8, 0.7853981633974483], [369, 80, 8, 0.7853981633974483], [368, 80, 8, 0.0], [367, 80, 8, 0.0], [366, 80, 8, 0.0], [365, 80, 8, 0.0], [364, 80, 8, 0.0], [363, 80, 8, 0.0], [362, 80, 8, 0.0], [361, 80, 8, 0.0], [360, 80, 8, 0.0], [359, 80, 8, 0.0], [358, 80, 8, 0.0], [357, 80, 8, 0.0], [356, 80, 8, 0.0], [355, 80, 8, 0.0], [354, 80, 8, 0.0], [353, 80, 8, 0.0], [352, 79, 8, 0.7853981633974483], [351, 79, 8, 0.0], [350, 79, 8, 0.0], [349, 79, 8, 0.0], [348, 78, 8, 0.7853981633974483], [347, 78, 8, 0.0], [346, 78, 8, 0.0], [345, 77, 8, 0.7853981633974483], [344, 77, 8, 0.0], [343, 77, 8, 0.0], [342, 76, 8, 0.7853981633974483], [341, 76, 8, 0.0], [340, 75, 8, 0.7853981633974483], [339, 75, 8, 0.0], [338, 74, 8, 0.7853981633974483], [337, 74, 8, 0.0], [336, 73, 8, 0.7853981633974483], [335, 73, 8, 0.0], [334, 73, 8, 0.0], [333, 72, 8, 0.7853981633974483], [332, 72, 8, 0.0], [331, 72, 8, 0.0], [330, 71, 8, 0.7853981633974483], [329, 71, 8, 0.0], [328, 71, 8, 0.0], [327, 70, 8, 0.7853981633974483], [326, 70, 8, 0.0], [325, 69, 8, 0.7853981633974483], [324, 69, 8, 0.0], [323, 68, 8, 0.7853981633974483], [322, 68, 8, 0.0], [321, 67, 8, 0.7853981633974483], [321, 66, 8, 1.5707963267948966], [321, 65, 8, 1.5707963267948966], [321, 64, 8, 1.5707963267948966], [320, 63, 8, 0.7853981633974483], [320, 62, 8, 1.5707963267948966], [320, 61, 8, 1.5707963267948966], [320, 60, 8, 1.5707963267948966], [320, 59, 8, 1.5707963267948966], [320, 58, 8, 1.5707963267948966], [319, 57, 8, 0.7853981633974483], [319, 56, 8, 1.5707963267948966], [319, 55, 8, 1.5707963267948966], [319, 54, 8, 1.5707963267948966], [319, 53, 8, 1.5707963267948966], [319, 52, 8, 1.5707963267948966], [319, 51, 8, 1.5707963267948966], [319, 50, 8, 1.5707963267948966], [319, 49, 8, 1.5707963267948966], [319, 48, 8, 1.5707963267948966], [319, 47, 8, 1.5707963267948966], [319, 46, 8, 1.5707963267948966], [319, 45, 8, 1.5707963267948966], [319, 44, 8, 1.5707963267948966], [319, 43, 8, 1.5707963267948966], [319, 42, 8, 1.5707963267948966], [319, 41, 8, 1.5707963267948966], [319, 40, 8, 1.5707963267948966], [319, 39, 8, 1.5707963267948966], [319, 38, 8, 1.5707963267948966], [319, 37, 8, 1.5707963267948966], [319, 36, 8, 1.5707963267948966], [319, 35, 8, 1.5707963267948966], [320, 34, 8, 2.356194490192345], [319, 33, 8, 0.7853981633974483], [318, 32, 8, 0.7853981633974483], [318, 31, 8, 1.5707963267948966], [317, 30, 8, 0.7853981633974483], [316, 29, 8, 0.7853981633974483], [316, 28, 8, 1.5707963267948966], [315, 27, 8, 0.7853981633974483], [315, 26, 8, 1.5707963267948966], [314, 25, 8, 0.7853981633974483], [313, 24, 8, 0.7853981633974483], [313, 23, 8, 1.5707963267948966], [312, 22, 8, 0.7853981633974483], [312, 21, 8, 1.5707963267948966], [311, 20, 8, 0.7853981633974483], [310, 19, 8, 0.7853981633974483], [310, 18, 8, 1.5707963267948966], [309, 17, 8, 0.7853981633974483], [308, 16, 8, 0.7853981633974483], [308, 15, 8, 1.5707963267948966], [307, 14, 8, 0.7853981633974483], [306, 13, 8, 0.7853981633974483], [306, 12, 8, 1.5707963267948966], [306, 11, 8, 1.5707963267948966], [306, 10, 8, 1.5707963267948966], [305, 9, 8, 0.7853981633974483], [305, 8, 8, 1.5707963267948966], [305, 7, 8, 1.5707963267948966], [304, 6, 8, 0.7853981633974483], [303, 5, 8, 0.7853981633974483], [304, 4, 8, 2.356194490192345], [304, 3, 8, 1.5707963267948966], [304, 2, 8, 1.5707963267948966], [304, 1, 8, 1.5707963267948966], [304, 0, 8, 1.5707963267948966], [304, -1, 8, 1.5707963267948966], [304, -2, 8, 1.5707963267948966], [304, -3, 8, 1.5707963267948966], [304, -4, 8, 1.5707963267948966], [304, -5, 8, 1.5707963267948966], [304, -6, 8, 1.5707963267948966], [304, -7, 8, 1.5707963267948966], [304, -8, 8, 1.5707963267948966], [304, -9, 8, 1.5707963267948966], [304, -10, 8, 1.5707963267948966], [304, -11, 8, 1.5707963267948966], [304, -12, 8, 1.5707963267948966], [304, -13, 8, 1.5707963267948966], [304, -14, 8, 1.5707963267948966], [304, -15, 8, 1.5707963267948966], [304, -16, 8, 1.5707963267948966], [304, -17, 8, 1.5707963267948966], [304, -18, 8, 1.5707963267948966], [304, -19, 8, 1.5707963267948966], [304, -20, 8, 1.5707963267948966], [304, -21, 8, 1.5707963267948966], [304, -22, 8, 1.5707963267948966], [304, -23, 8, 1.5707963267948966], [304, -24, 8, 1.5707963267948966], [304, -25, 8, 1.5707963267948966], [304, -26, 8, 1.5707963267948966], [304, -27, 8, 1.5707963267948966], [304, -28, 8, 1.5707963267948966], [304, -29, 8, 1.5707963267948966], [304, -30, 8, 1.5707963267948966], [304, -31, 8, 1.5707963267948966], [304, -32, 8, 1.5707963267948966], [304, -33, 8, 1.5707963267948966], [305, -34, 8, 2.356194490192345], [304, -35, 8, 0.7853981633974483], [304, -36, 8, 1.5707963267948966], [303, -37, 8, 0.7853981633974483], [303, -38, 8, 1.5707963267948966], [302, -39, 8, 0.7853981633974483], [302, -40, 8, 1.5707963267948966], [301, -41, 8, 0.7853981633974483], [301, -42, 8, 1.5707963267948966], [300, -43, 8, 0.7853981633974483], [300, -44, 8, 1.5707963267948966], [299, -45, 8, 0.7853981633974483], [298, -46, 8, 0.7853981633974483], [298, -47, 8, 1.5707963267948966], [297, -48, 8, 0.7853981633974483], [297, -49, 8, 1.5707963267948966], [296, -50, 8, 0.7853981633974483], [296, -51, 8, 1.5707963267948966], [295, -52, 8, 0.7853981633974483], [295, -53, 8, 1.5707963267948966], [294, -54, 8, 0.7853981633974483], [293, -55, 8, 0.7853981633974483], [292, -55, 8, 0.0], [291, -54, 8, -0.7853981633974483], [290, -53, 8, -0.7853981633974483], [289, -53, 8, 0.0], [288, -52, 8, -0.7853981633974483], [287, -53, 8, 0.7853981633974483], [286, -52, 8, -0.7853981633974483], [285, -51, 8, -0.7853981633974483], [284, -50, 8, -0.7853981633974483], [283, -50, 8, 0.0], [282, -49, 8, -0.7853981633974483], [281, -49, 8, 0.0], [280, -48, 8, -0.7853981633974483], [279, -48, 8, 0.0], [278, -47, 8, -0.7853981633974483], [277, -47, 8, 0.0], [276, -46, 8, -0.7853981633974483], [275, -46, 8, 0.0], [274, -45, 8, -0.7853981633974483], [273, -45, 8, 0.0], [272, -44, 8, -0.7853981633974483], [271, -44, 8, 0.0], [270, -43, 8, -0.7853981633974483], [269, -43, 8, 0.0], [268, -42, 8, -0.7853981633974483], [267, -42, 8, 0.0], [266, -41, 8, -0.7853981633974483], [265, -41, 8, 0.0], [264, -41, 8, 0.0], [263, -40, 8, -0.7853981633974483], [262, -40, 8, 0.0], [261, -40, 8, 0.0], [260, -40, 8, 0.0], [259, -40, 8, 0.0], [258, -40, 8, 0.0], [257, -39, 8, -0.7853981633974483], [256, -38, 8, -0.7853981633974483], [255, -37, 8, -0.7853981633974483], [254, -36, 8, -0.7853981633974483], [253, -36, 8, 0.0], [252, -36, 8, 0.0], [251, -35, 8, -0.7853981633974483], [250, -35, 8, 0.0], [249, -35, 8, 0.0], [248, -35, 8, 0.0], [247, -35, 8, 0.0], [246, -35, 8, 0.0], [245, -35, 8, 0.0], [244, -35, 8, 0.0], [243, -35, 8, 0.0], [242, -35, 8, 0.0], [241, -35, 8, 0.0], [240, -35, 8, 0.0], [239, -35, 8, 0.0], [238, -35, 8, 0.0], [237, -35, 8, 0.0], [236, -35, 8, 0.0], [235, -35, 8, 0.0], [234, -35, 8, 0.0], [233, -35, 8, 0.0], [232, -35, 8, 0.0], [231, -35, 8, 0.0], [230, -35, 8, 0.0], [229, -35, 8, 0.0], [228, -35, 8, 0.0], [227, -35, 8, 0.0], [226, -35, 8, 0.0], [225, -35, 8, 0.0], [224, -35, 8, 0.0], [223, -35, 8, 0.0], [222, -35, 8, 0.0], [221, -35, 8, 0.0], [220, -35, 8, 0.0], [219, -35, 8, 0.0], [218, -35, 8, 0.0], [217, -35, 8, 0.0], [216, -34, 8, -0.7853981633974483], [215, -34, 8, 0.0], [214, -34, 8, 0.0], [213, -33, 8, -0.7853981633974483], [212, -32, 8, -0.7853981633974483], [211, -31, 8, -0.7853981633974483], [210, -31, 8, 0.0], [209, -30, 8, -0.7853981633974483], [208, -30, 8, 0.0], [207, -30, 8, 0.0], [206, -30, 8, 0.0], [205, -30, 8, 0.0], [204, -30, 8, 0.0], [203, -30, 8, 0.0], [202, -30, 8, 0.0], [201, -30, 8, 0.0], [200, -30, 8, 0.0], [199, -30, 8, 0.0], [198, -30, 8, 0.0], [197, -30, 8, 0.0], [196, -30, 8, 0.0], [195, -30, 8, 0.0], [194, -30, 8, 0.0], [193, -30, 8, 0.0], [192, -30, 8, 0.0], [191, -30, 8, 0.0], [190, -30, 8, 0.0], [189, -30, 8, 0.0], [188, -30, 8, 0.0], [187, -30, 8, 0.0], [186, -30, 8, 0.0], [185, -30, 8, 0.0], [184, -30, 8, 0.0], [183, -30, 8, 0.0], [182, -30, 8, 0.0], [181, -30, 8, 0.0], [180, -30, 8, 0.0], [179, -30, 8, 0.0], [178, -30, 8, 0.0], [177, -30, 8, 0.0], [176, -30, 8, 0.0], [175, -30, 8, 0.0], [174, -29, 8, -0.7853981633974483], [173, -29, 8, 0.0], [172, -29, 8, 0.0], [171, -28, 8, -0.7853981633974483], [170, -28, 8, 0.0], [169, -27, 8, -0.7853981633974483], [168, -27, 8, 0.0], [167, -26, 8, -0.7853981633974483], [166, -26, 8, 0.0], [165, -25, 8, -0.7853981633974483], [164, -24, 8, -0.7853981633974483], [163, -23, 8, -0.7853981633974483], [162, -22, 8, -0.7853981633974483], [161, -21, 8, -0.7853981633974483], [160, -20, 8, -0.7853981633974483], [159, -20, 8, 0.0], [158, -19, 8, -0.7853981633974483], [157, -18, 8, -0.7853981633974483], [156, -17, 8, -0.7853981633974483], [156, -16, 8, -1.5707963267948966], [156, -15, 8, -1.5707963267948966], [156, -14, 8, -1.5707963267948966], [157, -13, 8, -2.356194490192345], [157, -12, 8, -1.5707963267948966], [157, -11, 8, -1.5707963267948966], [158, -10, 8, -2.356194490192345], [158, -9, 8, -1.5707963267948966], [158, -8, 8, -1.5707963267948966], [158, -7, 8, -1.5707963267948966], [159, -6, 8, -2.356194490192345], [159, -5, 8, -1.5707963267948966], [159, -4, 8, -1.5707963267948966], [159, -3, 8, -1.5707963267948966], [159, -2, 8, -1.5707963267948966], [159, -1, 8, -1.5707963267948966], [159, 0, 8, -1.5707963267948966], [159, 1, 8, -1.5707963267948966], [159, 2, 8, -1.5707963267948966], [159, 3, 8, -1.5707963267948966], [159, 4, 8, -1.5707963267948966], [159, 5, 8, -1.5707963267948966], [159, 6, 8, -1.5707963267948966], [159, 7, 8, -1.5707963267948966], [159, 8, 8, -1.5707963267948966], [159, 9, 8, -1.5707963267948966], [159, 10, 8, -1.5707963267948966], [159, 11, 8, -1.5707963267948966], [159, 12, 8, -1.5707963267948966], [159, 13, 8, -1.5707963267948966], [159, 14, 8, -1.5707963267948966], [159, 15, 8, -1.5707963267948966], [159, 16, 8, -1.5707963267948966], [159, 17, 8, -1.5707963267948966], [159, 18, 8, -1.5707963267948966], [159, 19, 8, -1.5707963267948966], [159, 20, 8, -1.5707963267948966], [159, 21, 8, -1.5707963267948966], [159, 22, 8, -1.5707963267948966], [159, 23, 8, -1.5707963267948966], [159, 24, 8, -1.5707963267948966], [159, 25, 8, -1.5707963267948966], [159, 26, 8, -1.5707963267948966], [159, 27, 8, -1.5707963267948966], [159, 28, 8, -1.5707963267948966], [159, 29, 8, -1.5707963267948966], [159, 30, 8, -1.5707963267948966], [159, 31, 8, -1.5707963267948966], [159, 32, 8, -1.5707963267948966], [159, 33, 8, -1.5707963267948966], [159, 34, 8, -1.5707963267948966], [159, 35, 8, -1.5707963267948966], [159, 36, 8, -1.5707963267948966], [160, 37, 8, -2.356194490192345], [160, 38, 8, -1.5707963267948966], [160, 39, 8, -1.5707963267948966], [160, 40, 8, -1.5707963267948966], [161, 41, 8, -2.356194490192345], [162, 41, 8, 3.141592653589793], [163, 41, 8, 3.141592653589793], [164, 42, 8, -2.356194490192345], [165, 42, 8, 3.141592653589793], [166, 42, 8, 3.141592653589793], [167, 43, 8, -2.356194490192345], [168, 43, 8, 3.141592653589793], [169, 43, 8, 3.141592653589793], [170, 44, 8, -2.356194490192345], [171, 44, 8, 3.141592653589793], [172, 44, 8, 3.141592653589793], [173, 44, 8, 3.141592653589793], [174, 45, 8, -2.356194490192345], [175, 45, 8, 3.141592653589793], [176, 45, 8, 3.141592653589793], [177, 45, 8, 3.141592653589793], [178, 45, 8, 3.141592653589793], [179, 45, 8, 3.141592653589793], [180, 45, 8, 3.141592653589793], [181, 45, 8, 3.141592653589793], [182, 45, 8, 3.141592653589793], [183, 45, 8, 3.141592653589793], [184, 45, 8, 3.141592653589793], [185, 45, 8, 3.141592653589793], [186, 46, 8, -2.356194490192345], [187, 46, 8, 3.141592653589793], [188, 47, 8, -2.356194490192345], [189, 47, 8, 3.141592653589793], [190, 48, 8, -2.356194490192345], [191, 48, 8, 3.141592653589793], [192, 49, 8, -2.356194490192345], [193, 49, 8, 3.141592653589793], [194, 49, 8, 3.141592653589793], [195, 50, 8, -2.356194490192345], [196, 50, 8, 3.141592653589793], [197, 50, 8, 3.141592653589793], [198, 50, 8, 3.141592653589793], [199, 50, 8, 3.141592653589793], [200, 50, 8, 3.141592653589793], [201, 50, 8, 3.141592653589793], [202, 50, 8, 3.141592653589793], [203, 50, 8, 3.141592653589793], [204, 50, 8, 3.141592653589793], [205, 50, 8, 3.141592653589793], [206, 50, 8, 3.141592653589793], [207, 50, 8, 3.141592653589793], [208, 50, 8, 3.141592653589793], [209, 50, 8, 3.141592653589793], [210, 50, 8, 3.141592653589793], [211, 50, 8, 3.141592653589793], [212, 50, 8, 3.141592653589793], [213, 50, 8, 3.141592653589793], [214, 50, 8, 3.141592653589793], [215, 50, 8, 3.141592653589793], [216, 50, 8, 3.141592653589793], [217, 50, 8, 3.141592653589793], [218, 50, 8, 3.141592653589793], [219, 50, 8, 3.141592653589793], [220, 50, 8, 3.141592653589793], [221, 50, 8, 3.141592653589793], [222, 50, 8, 3.141592653589793], [223, 50, 8, 3.141592653589793], [224, 51, 8, -2.356194490192345], [225, 51, 8, 3.141592653589793], [226, 51, 8, 3.141592653589793], [227, 52, 8, -2.356194490192345], [228, 53, 8, -2.356194490192345], [228, 54, 8, -1.5707963267948966], [228, 55, 8, -1.5707963267948966], [229, 56, 8, -2.356194490192345], [229, 57, 8, -1.5707963267948966], [229, 58, 8, -1.5707963267948966], [229, 59, 8, -1.5707963267948966], [229, 60, 8, -1.5707963267948966], [229, 61, 8, -1.5707963267948966], [229, 62, 8, -1.5707963267948966], [229, 63, 8, -1.5707963267948966], [229, 64, 8, -1.5707963267948966], [229, 65, 8, -1.5707963267948966], [229, 66, 8, -1.5707963267948966], [229, 67, 8, -1.5707963267948966], [229, 68, 8, -1.5707963267948966], [229, 69, 8, -1.5707963267948966], [229, 70, 8, -1.5707963267948966], [229, 71, 8, -1.5707963267948966], [229, 72, 8, -1.5707963267948966], [229, 73, 8, -1.5707963267948966], [229, 74, 8, -1.5707963267948966], [229, 75, 8, -1.5707963267948966], [229, 76, 8, -1.5707963267948966], [229, 77, 8, -1.5707963267948966], [229, 78, 8, -1.5707963267948966], [229, 79, 8, -1.5707963267948966], [229, 80, 8, -1.5707963267948966], [229, 81, 8, -1.5707963267948966], [229, 82, 8, -1.5707963267948966], [229, 83, 8, -1.5707963267948966], [229, 84, 8, -1.5707963267948966], [230, 85, 8, -2.356194490192345], [230, 86, 8, -1.5707963267948966], [230, 87, 8, -1.5707963267948966], [231, 88, 8, -2.356194490192345], [231, 89, 8, -1.5707963267948966], [232, 90, 8, -2.356194490192345], [232, 91, 8, -1.5707963267948966], [233, 92, 8, -2.356194490192345], [233, 93, 8, -1.5707963267948966], [234, 94, 8, -2.356194490192345], [234, 95, 8, -1.5707963267948966], [234, 96, 8, -1.5707963267948966], [234, 97, 8, -1.5707963267948966], [234, 98, 8, -1.5707963267948966], [234, 99, 8, -1.5707963267948966], [234, 100, 8, -1.5707963267948966], [234, 101, 8, -1.5707963267948966], [233, 102, 8, -0.7853981633974483], [232, 102, 8, 0.0], [231, 103, 8, -0.7853981633974483], [230, 103, 8, 0.0], [229, 103, 8, 0.0], [228, 104, 8, -0.7853981633974483], [227, 104, 8, 0.0], [226, 104, 8, 0.0], [225, 105, 8, -0.7853981633974483], [224, 105, 8, 0.0], [223, 106, 8, -0.7853981633974483], [222, 107, 8, -0.7853981633974483], [221, 108, 8, -0.7853981633974483], [220, 109, 8, -0.7853981633974483], [219, 110, 8, -0.7853981633974483], [218, 111, 8, -0.7853981633974483], [217, 112, 8, -0.7853981633974483], [216, 113, 8, -0.7853981633974483], [215, 114, 8, -0.7853981633974483], [214, 115, 8, -0.7853981633974483], [213, 115, 8, 0.0], [212, 115, 8, 0.0], [211, 115, 8, 0.0], [210, 115, 8, 0.0], [209, 115, 8, 0.0], [208, 115, 8, 0.0], [207, 115, 8, 0.0], [206, 115, 8, 0.0], [205, 115, 8, 0.0], [204, 115, 8, 0.0], [203, 115, 8, 0.0], [202, 115, 8, 0.0], [201, 115, 8, 0.0], [200, 115, 8, 0.0], [199, 115, 8, 0.0], [198, 115, 8, 0.0], [197, 115, 8, 0.0], [196, 115, 8, 0.0], [195, 115, 8, 0.0], [194, 115, 8, 0.0], [193, 115, 8, 0.0], [192, 115, 8, 0.0], [191, 115, 8, 0.0], [190, 115, 8, 0.0], [189, 115, 8, 0.0], [188, 115, 8, 0.0], [187, 115, 8, 0.0], [186, 115, 8, 0.0], [185, 115, 8, 0.0], [184, 115, 8, 0.0], [183, 115, 8, 0.0], [182, 115, 8, 0.0], [181, 115, 8, 0.0], [180, 115, 8, 0.0], [179, 115, 8, 0.0], [178, 115, 8, 0.0], [177, 115, 8, 0.0], [176, 115, 8, 0.0], [175, 115, 8, 0.0], [174, 115, 8, 0.0], [173, 116, 8, -0.7853981633974483], [172, 116, 8, 0.0], [171, 116, 8, 0.0], [170, 116, 8, 0.0], [169, 117, 8, -0.7853981633974483], [168, 117, 8, 0.0], [167, 117, 8, 0.0], [166, 118, 8, -0.7853981633974483], [165, 118, 8, 0.0], [164, 118, 8, 0.0], [163, 119, 8, -0.7853981633974483], [162, 119, 8, 0.0], [161, 119, 8, 0.0], [160, 120, 8, -0.7853981633974483], [159, 120, 8, 0.0], [158, 121, 8, -0.7853981633974483], [157, 122, 8, -0.7853981633974483], [156, 123, 8, -0.7853981633974483], [155, 124, 8, -0.7853981633974483], [154, 125, 8, -0.7853981633974483], [153, 126, 8, -0.7853981633974483], [152, 127, 8, -0.7853981633974483], [151, 128, 8, -0.7853981633974483], [150, 129, 8, -0.7853981633974483], [149, 130, 8, -0.7853981633974483], [148, 131, 8, -0.7853981633974483], [147, 132, 8, -0.7853981633974483], [146, 133, 8, -0.7853981633974483], [147, 134, 8, -2.356194490192345], [148, 135, 8, -2.356194490192345], [148, 136, 8, -1.5707963267948966], [149, 137, 8, -2.356194490192345], [149, 138, 8, -1.5707963267948966], [149, 139, 8, -1.5707963267948966], [150, 140, 8, -2.356194490192345], [150, 141, 8, -1.5707963267948966], [151, 142, 8, -2.356194490192345], [151, 143, 8, -1.5707963267948966], [151, 144, 8, -1.5707963267948966], [152, 145, 8, -2.356194490192345], [152, 146, 8, -1.5707963267948966], [152, 147, 8, -1.5707963267948966], [153, 148, 8, -2.356194490192345], [153, 149, 8, -1.5707963267948966], [154, 150, 8, -2.356194490192345], [154, 151, 8, -1.5707963267948966], [155, 152, 8, -2.356194490192345], [155, 153, 8, -1.5707963267948966], [156, 154, 8, -2.356194490192345], [156, 155, 8, -1.5707963267948966], [156, 156, 8, -1.5707963267948966], [157, 157, 8, -2.356194490192345], [157, 158, 8, -1.5707963267948966], [157, 159, 8, -1.5707963267948966], [158, 160, 8, -2.356194490192345], [158, 161, 8, -1.5707963267948966], [158, 162, 8, -1.5707963267948966], [159, 163, 8, -2.356194490192345], [160, 164, 8, -2.356194490192345], [161, 165, 8, -2.356194490192345], [161, 166, 8, -1.5707963267948966], [162, 167, 8, -2.356194490192345], [163, 168, 8, -2.356194490192345], [163, 169, 8, -1.5707963267948966], [164, 170, 8, -2.356194490192345], [165, 171, 8, -2.356194490192345], [165, 172, 8, -1.5707963267948966], [166, 173, 8, -2.356194490192345], [167, 174, 8, -2.356194490192345], [168, 174, 8, 3.141592653589793], [169, 175, 8, -2.356194490192345], [170, 176, 8, -2.356194490192345], [171, 177, 8, -2.356194490192345], [172, 178, 8, -2.356194490192345], [172, 179, 8, -1.5707963267948966], [172, 180, 8, -1.5707963267948966], [173, 181, 8, -2.356194490192345], [173, 182, 8, -1.5707963267948966], [173, 183, 8, -1.5707963267948966], [174, 184, 8, -2.356194490192345], [174, 185, 8, -1.5707963267948966], [174, 186, 8, -1.5707963267948966], [175, 187, 8, -2.356194490192345], [175, 188, 8, -1.5707963267948966], [175, 189, 8, -1.5707963267948966], [176, 190, 8, -2.356194490192345], [176, 191, 8, -1.5707963267948966], [176, 192, 8, -1.5707963267948966], [177, 193, 8, -2.356194490192345], [177, 194, 8, -1.5707963267948966], [178, 195, 8, -2.356194490192345], [178, 196, 8, -1.5707963267948966], [179, 197, 8, -2.356194490192345], [180, 198, 8, -2.356194490192345], [181, 199, 8, -2.356194490192345], [182, 200, 8, -2.356194490192345], [183, 201, 8, -2.356194490192345], [184, 201, 8, 3.141592653589793], [185, 202, 8, -2.356194490192345], [186, 202, 8, 3.141592653589793], [187, 203, 8, -2.356194490192345], [188, 203, 8, 3.141592653589793], [189, 203, 8, 3.141592653589793], [190, 204, 8, -2.356194490192345], [191, 204, 8, 3.141592653589793], [192, 204, 8, 3.141592653589793], [193, 205, 8, -2.356194490192345], [194, 205, 8, 3.141592653589793], [195, 206, 8, -2.356194490192345], [196, 207, 8, -2.356194490192345], [197, 208, 8, -2.356194490192345], [198, 209, 8, -2.356194490192345], [199, 210, 8, -2.356194490192345], [200, 211, 8, -2.356194490192345], [201, 212, 8, -2.356194490192345], [202, 213, 8, -2.356194490192345], [203, 214, 8, -2.356194490192345], [204, 215, 8, -2.356194490192345], [205, 216, 8, -2.356194490192345], [206, 217, 8, -2.356194490192345], [207, 218, 8, -2.356194490192345], [208, 219, 8, -2.356194490192345], [209, 220, 8, -2.356194490192345], [210, 221, 8, -2.356194490192345], [211, 222, 8, -2.356194490192345], [212, 223, 8, -2.356194490192345], [213, 224, 8, -2.356194490192345], [214, 225, 8, -2.356194490192345], [215, 226, 8, -2.356194490192345], [216, 227, 8, -2.356194490192345], [217, 228, 8, -2.356194490192345], [218, 229, 8, -2.356194490192345], [219, 230, 8, -2.356194490192345], [220, 231, 8, -2.356194490192345], [221, 232, 8, -2.356194490192345], [222, 233, 8, -2.356194490192345], [223, 234, 8, -2.356194490192345], [224, 235, 8, -2.356194490192345], [225, 236, 8, -2.356194490192345], [226, 237, 8, -2.356194490192345], [227, 238, 8, -2.356194490192345], [228, 239, 8, -2.356194490192345], [229, 240, 8, -2.356194490192345], [230, 241, 8, -2.356194490192345], [231, 242, 8, -2.356194490192345], [232, 243, 8, -2.356194490192345], [233, 244, 8, -2.356194490192345], [234, 245, 8, -2.356194490192345], [235, 246, 8, -2.356194490192345], [236, 247, 8, -2.356194490192345], [237, 248, 8, -2.356194490192345], [238, 249, 8, -2.356194490192345], [239, 250, 8, -2.356194490192345], [240, 251, 8, -2.356194490192345], [241, 252, 8, -2.356194490192345], [242, 253, 8, -2.356194490192345], [243, 254, 8, -2.356194490192345], [244, 255, 8, -2.356194490192345], [245, 256, 8, -2.356194490192345], [246, 257, 8, -2.356194490192345], [247, 258, 8, -2.356194490192345], [248, 259, 8, -2.356194490192345], [249, 260, 8, -2.356194490192345], [250, 261, 8, -2.356194490192345], [251, 262, 8, -2.356194490192345], [252, 263, 8, -2.356194490192345], [253, 264, 8, -2.356194490192345], [254, 265, 8, -2.356194490192345], [255, 266, 8, -2.356194490192345], [256, 267, 8, -2.356194490192345], [257, 268, 8, -2.356194490192345], [258, 269, 8, -2.356194490192345], [259, 270, 8, -2.356194490192345], [260, 271, 8, -2.356194490192345], [261, 272, 8, -2.356194490192345], [262, 273, 8, -2.356194490192345], [263, 274, 8, -2.356194490192345], [264, 275, 8, -2.356194490192345], [265, 276, 8, -2.356194490192345], [266, 277, 8, -2.356194490192345], [267, 278, 8, -2.356194490192345], [268, 279, 8, -2.356194490192345], [269, 280, 8, -2.356194490192345], [270, 281, 8, -2.356194490192345], [271, 282, 8, -2.356194490192345], [272, 283, 8, -2.356194490192345], [273, 284, 8, -2.356194490192345], [274, 285, 8, -2.356194490192345], [275, 286, 8, -2.356194490192345], [276, 287, 8, -2.356194490192345], [277, 288, 8, -2.356194490192345], [278, 289, 8, -2.356194490192345], [278, 290, 8, -1.5707963267948966], [278, 291, 8, -1.5707963267948966], [277, 292, 8, -0.7853981633974483], [276, 293, 8, -0.7853981633974483], [276, 294, 8, -1.5707963267948966], [275, 295, 8, -0.7853981633974483], [275, 296, 8, -1.5707963267948966], [274, 297, 8, -0.7853981633974483], [274, 298, 8, -1.5707963267948966], [274, 299, 8, -1.5707963267948966], [273, 300, 8, -0.7853981633974483], [273, 301, 8, -1.5707963267948966], [273, 302, 8, -1.5707963267948966], [273, 303, 8, -1.5707963267948966], [273, 304, 8, -1.5707963267948966], [273, 305, 8, -1.5707963267948966], [273, 306, 8, -1.5707963267948966], [273, 307, 8, -1.5707963267948966], [272, 308, 8, -0.7853981633974483], [271, 309, 8, -0.7853981633974483], [270, 310, 8, -0.7853981633974483], [270, 311, 8, -1.5707963267948966], [269, 312, 8, -0.7853981633974483], [268, 313, 8, -0.7853981633974483], [268, 314, 8, -1.5707963267948966], [267, 315, 8, -0.7853981633974483], [266, 316, 8, -0.7853981633974483], [266, 317, 8, -1.5707963267948966], [265, 318, 8, -0.7853981633974483], [264, 319, 8, -0.7853981633974483], [264, 320, 8, -1.5707963267948966], [263, 321, 8, -0.7853981633974483], [262, 322, 8, -0.7853981633974483], [261, 323, 8, -0.7853981633974483], [260, 324, 8, -0.7853981633974483], [259, 325, 8, -0.7853981633974483], [258, 325, 8, 0.0], [257, 326, 8, -0.7853981633974483], [256, 326, 8, 0.0], [255, 327, 8, -0.7853981633974483], [254, 327, 8, 0.0], [253, 328, 8, -0.7853981633974483], [252, 328, 8, 0.0], [251, 329, 8, -0.7853981633974483], [250, 329, 8, 0.0], [249, 330, 8, -0.7853981633974483], [248, 331, 8, -0.7853981633974483], [248, 332, 8, -1.5707963267948966], [248, 333, 8, -1.5707963267948966], [247, 334, 8, -0.7853981633974483], [247, 335, 8, -1.5707963267948966], [246, 336, 8, -0.7853981633974483], [246, 337, 8, -1.5707963267948966], [245, 338, 8, -0.7853981633974483], [245, 339, 8, -1.5707963267948966], [244, 340, 8, -0.7853981633974483], [244, 341, 8, -1.5707963267948966], [243, 342, 8, -0.7853981633974483], [242, 342, 8, 0.0], [241, 342, 8, 0.0], [240, 343, 8, -0.7853981633974483], [239, 344, 8, -0.7853981633974483], [238, 345, 8, -0.7853981633974483], [237, 346, 8, -0.7853981633974483], [236, 346, 8, 0.0], [235, 347, 8, -0.7853981633974483], [234, 347, 8, 0.0], [233, 348, 8, -0.7853981633974483], [232, 348, 8, 0.0], [231, 348, 8, 0.0], [230, 349, 8, -0.7853981633974483], [229, 349, 8, 0.0], [228, 350, 8, -0.7853981633974483], [228, 351, 8, -1.5707963267948966], [227, 352, 8, -0.7853981633974483], [228, 353, 8, -2.356194490192345], [227, 354, 8, -0.7853981633974483], [226, 355, 8, -0.7853981633974483], [225, 356, 8, -0.7853981633974483], [224, 357, 8, -0.7853981633974483], [224, 358, 8, -1.5707963267948966], [223, 359, 8, -0.7853981633974483], [222, 360, 8, -0.7853981633974483], [221, 360, 8, 0.0], [220, 360, 8, 0.0], [219, 360, 8, 0.0], [218, 361, 8, -0.7853981633974483], [217, 362, 8, -0.7853981633974483], [216, 363, 8, -0.7853981633974483], [215, 364, 8, -0.7853981633974483], [214, 365, 8, -0.7853981633974483], [213, 366, 8, -0.7853981633974483], [212, 367, 8, -0.7853981633974483], [211, 368, 8, -0.7853981633974483], [210, 369, 8, -0.7853981633974483], [209, 370, 8, -0.7853981633974483], [209, 371, 8, -1.5707963267948966], [209, 372, 8, -1.5707963267948966], [209, 373, 8, -1.5707963267948966], [209, 374, 8, -1.5707963267948966], [208, 375, 8, -0.7853981633974483], [208, 376, 8, -1.5707963267948966], [208, 377, 8, -1.5707963267948966], [207, 378, 8, -0.7853981633974483], [207, 379, 8, -1.5707963267948966], [206, 380, 8, -0.7853981633974483], [206, 381, 8, -1.5707963267948966], [205, 382, 8, -0.7853981633974483], [205, 383, 8, -1.5707963267948966], [204, 384, 8, -0.7853981633974483], [203, 385, 8, -0.7853981633974483], [202, 386, 8, -0.7853981633974483], [201, 386, 8, 0.0], [200, 387, 8, -0.7853981633974483], [199, 387, 8, 0.0], [198, 388, 8, -0.7853981633974483], [197, 388, 8, 0.0], [196, 389, 8, -0.7853981633974483], [195, 389, 8, 0.0], [194, 390, 8, -0.7853981633974483], [193, 391, 8, -0.7853981633974483], [192, 391, 8, 0.0], [191, 392, 8, -0.7853981633974483], [190, 393, 8, -0.7853981633974483], [190, 394, 8, -1.5707963267948966], [189, 395, 8, -0.7853981633974483], [188, 396, 8, -0.7853981633974483], [188, 397, 8, -1.5707963267948966], [187, 398, 8, -0.7853981633974483], [186, 399, 8, -0.7853981633974483], [185, 399, 8, 0.0], [184, 399, 8, 0.0], [183, 400, 8, -0.7853981633974483], [182, 400, 8, 0.0], [181, 400, 8, 0.0], [180, 400, 8, 0.0], [179, 400, 8, 0.0], [178, 401, 8, -0.7853981633974483], [177, 402, 8, -0.7853981633974483], [176, 403, 8, -0.7853981633974483], [175, 404, 8, -0.7853981633974483], [174, 405, 8, -0.7853981633974483], [173, 406, 8, -0.7853981633974483], [172, 407, 8, -0.7853981633974483], [171, 408, 8, -0.7853981633974483], [170, 409, 8, -0.7853981633974483], [169, 410, 8, -0.7853981633974483], [168, 411, 8, -0.7853981633974483], [167, 412, 8, -0.7853981633974483], [166, 413, 8, -0.7853981633974483], [165, 414, 8, -0.7853981633974483], [164, 415, 8, -0.7853981633974483], [163, 416, 8, -0.7853981633974483], [162, 417, 8, -0.7853981633974483], [161, 418, 8, -0.7853981633974483], [160, 419, 8, -0.7853981633974483], [159, 420, 8, -0.7853981633974483], [158, 421, 8, -0.7853981633974483], [157, 422, 8, -0.7853981633974483], [156, 423, 8, -0.7853981633974483], [155, 424, 8, -0.7853981633974483], [154, 425, 8, -0.7853981633974483], [153, 426, 8, -0.7853981633974483], [152, 427, 8, -0.7853981633974483], [151, 428, 8, -0.7853981633974483], [150, 429, 8, -0.7853981633974483], [149, 430, 8, -0.7853981633974483], [148, 431, 8, -0.7853981633974483], [147, 432, 8, -0.7853981633974483], [146, 433, 8, -0.7853981633974483], [145, 434, 8, -0.7853981633974483], [144, 435, 8, -0.7853981633974483], [143, 436, 8, -0.7853981633974483], [142, 437, 8, -0.7853981633974483], [141, 438, 8, -0.7853981633974483], [140, 439, 8, -0.7853981633974483], [139, 440, 8, -0.7853981633974483], [138, 441, 8, -0.7853981633974483], [137, 442, 8, -0.7853981633974483], [136, 443, 8, -0.7853981633974483], [135, 444, 8, -0.7853981633974483], [134, 445, 8, -0.7853981633974483], [133, 446, 8, -0.7853981633974483], [132, 447, 8, -0.7853981633974483], [131, 448, 8, -0.7853981633974483], [130, 449, 8, -0.7853981633974483], [129, 450, 8, -0.7853981633974483], [128, 450, 8, 0.0], [127, 450, 8, 0.0], [126, 450, 8, 0.0], [125, 450, 8, 0.0], [124, 451, 8, -0.7853981633974483], [123, 451, 8, 0.0], [122, 451, 8, 0.0], [121, 452, 8, -0.7853981633974483], [120, 452, 8, 0.0], [119, 453, 8, -0.7853981633974483], [118, 453, 8, 0.0], [117, 454, 8, -0.7853981633974483], [116, 454, 8, 0.0], [115, 455, 8, -0.7853981633974483], [114, 456, 8, -0.7853981633974483], [113, 457, 8, -0.7853981633974483], [112, 458, 8, -0.7853981633974483], [111, 459, 8, -0.7853981633974483], [110, 459, 8, 0.0], [109, 460, 8, -0.7853981633974483], [108, 461, 8, -0.7853981633974483], [107, 462, 8, -0.7853981633974483], [106, 463, 8, -0.7853981633974483], [105, 464, 8, -0.7853981633974483], [104, 464, 8, 0.0], [103, 463, 8, 0.7853981633974483], [102, 462, 8, 0.7853981633974483], [102, 461, 8, 1.5707963267948966], [101, 460, 8, 0.7853981633974483], [100, 459, 8, 0.7853981633974483], [100, 458, 8, 1.5707963267948966], [99, 457, 8, 0.7853981633974483], [98, 456, 8, 0.7853981633974483], [97, 455, 8, 0.7853981633974483], [97, 454, 8, 1.5707963267948966], [96, 453, 8, 0.7853981633974483], [95, 452, 8, 0.7853981633974483], [95, 451, 8, 1.5707963267948966], [94, 450, 8, 0.7853981633974483], [93, 449, 8, 0.7853981633974483], [93, 448, 8, 1.5707963267948966], [92, 447, 8, 0.7853981633974483], [91, 446, 8, 0.7853981633974483], [90, 446, 8, 0.0], [89, 445, 8, 0.7853981633974483], [88, 444, 8, 0.7853981633974483], [87, 444, 8, 0.0], [86, 443, 8, 0.7853981633974483], [85, 442, 8, 0.7853981633974483], [85, 441, 8, 1.5707963267948966], [84, 440, 8, 0.7853981633974483], [83, 439, 8, 0.7853981633974483], [83, 438, 8, 1.5707963267948966], [82, 437, 8, 0.7853981633974483], [81, 436, 8, 0.7853981633974483], [80, 436, 8, 0.0], [79, 435, 8, 0.7853981633974483], [78, 434, 8, 0.7853981633974483], [77, 434, 8, 0.0], [76, 433, 8, 0.7853981633974483], [75, 432, 8, 0.7853981633974483], [75, 431, 8, 1.5707963267948966], [74, 430, 8, 0.7853981633974483], [73, 429, 8, 0.7853981633974483], [73, 428, 8, 1.5707963267948966], [72, 427, 8, 0.7853981633974483], [71, 427, 8, 0.0], [70, 427, 8, 0.0], [69, 427, 8, 0.0], [68, 426, 8, 0.7853981633974483], [67, 426, 8, 0.0], [66, 426, 8, 0.0], [65, 426, 8, 0.0], [64, 425, 8, 0.7853981633974483], [63, 425, 8, 0.0], [62, 424, 8, 0.7853981633974483], [61, 424, 8, 0.0], [60, 423, 8, 0.7853981633974483], [59, 423, 8, 0.0], [58, 422, 8, 0.7853981633974483], [57, 422, 8, 0.0], [56, 421, 8, 0.7853981633974483], [55, 421, 8, 0.0], [54, 420, 8, 0.7853981633974483], [53, 419, 8, 0.7853981633974483], [52, 419, 8, 0.0], [51, 418, 8, 0.7853981633974483], [50, 417, 8, 0.7853981633974483], [50, 416, 8, 1.5707963267948966], [49, 415, 8, 0.7853981633974483], [48, 414, 8, 0.7853981633974483], [48, 413, 8, 1.5707963267948966], [47, 412, 8, 0.7853981633974483], [46, 411, 8, 0.7853981633974483], [45, 411, 8, 0.0], [44, 410, 8, 0.7853981633974483], [43, 409, 8, 0.7853981633974483], [42, 409, 8, 0.0], [41, 408, 8, 0.7853981633974483], [40, 407, 8, 0.7853981633974483], [40, 406, 8, 1.5707963267948966], [39, 405, 8, 0.7853981633974483], [38, 404, 8, 0.7853981633974483], [38, 403, 8, 1.5707963267948966], [37, 402, 8, 0.7853981633974483], [36, 401, 8, 0.7853981633974483], [35, 401, 8, 0.0], [34, 400, 8, 0.7853981633974483], [33, 399, 8, 0.7853981633974483], [32, 399, 8, 0.0], [31, 398, 8, 0.7853981633974483], [30, 397, 8, 0.7853981633974483], [30, 396, 8, 1.5707963267948966], [29, 395, 8, 0.7853981633974483], [28, 394, 8, 0.7853981633974483], [28, 393, 8, 1.5707963267948966], [27, 392, 8, 0.7853981633974483], [26, 391, 8, 0.7853981633974483], [25, 391, 8, 0.0], [24, 390, 8, 0.7853981633974483], [23, 389, 8, 0.7853981633974483], [22, 389, 8, 0.0], [21, 388, 8, 0.7853981633974483], [20, 388, 8, 0.0], [19, 387, 8, 0.7853981633974483], [18, 387, 8, 0.0], [17, 386, 8, 0.7853981633974483], [16, 386, 8, 0.0], [15, 385, 8, 0.7853981633974483], [14, 384, 8, 0.7853981633974483], [13, 383, 8, 0.7853981633974483], [12, 382, 8, 0.7853981633974483], [11, 381, 8, 0.7853981633974483], [10, 381, 8, 0.0], [9, 380, 8, 0.7853981633974483], [10, 379, 8, 2.356194490192345], [11, 378, 8, 2.356194490192345], [12, 377, 8, 2.356194490192345], [13, 376, 8, 2.356194490192345], [14, 375, 8, 2.356194490192345], [15, 374, 8, 2.356194490192345], [16, 373, 8, 2.356194490192345], [17, 372, 8, 2.356194490192345], [18, 371, 8, 2.356194490192345], [19, 370, 8, 2.356194490192345], [19, 369, 8, 1.5707963267948966], [20, 368, 8, 2.356194490192345], [21, 367, 8, 2.356194490192345], [22, 366, 8, 2.356194490192345], [23, 365, 8, 2.356194490192345], [23, 364, 8, 1.5707963267948966], [23, 363, 8, 1.5707963267948966], [24, 362, 8, 2.356194490192345], [24, 361, 8, 1.5707963267948966], [24, 360, 8, 1.5707963267948966], [24, 359, 8, 1.5707963267948966], [24, 358, 8, 1.5707963267948966], [24, 357, 8, 1.5707963267948966], [25, 356, 8, 2.356194490192345], [26, 355, 8, 2.356194490192345], [27, 355, 8, 3.141592653589793], [28, 355, 8, 3.141592653589793], [29, 355, 8, 3.141592653589793], [30, 355, 8, 3.141592653589793], [31, 355, 8, 3.141592653589793], [32, 354, 8, 2.356194490192345], [33, 353, 8, 2.356194490192345], [34, 352, 8, 2.356194490192345], [34, 351, 8, 1.5707963267948966], [34, 350, 8, 1.5707963267948966], [34, 349, 8, 1.5707963267948966], [34, 348, 8, 1.5707963267948966], [34, 347, 8, 1.5707963267948966], [35, 346, 8, 2.356194490192345], [36, 346, 8, 3.141592653589793], [37, 345, 8, 2.356194490192345], [38, 345, 8, 3.141592653589793], [39, 345, 8, 3.141592653589793], [40, 345, 8, 3.141592653589793], [41, 345, 8, 3.141592653589793], [42, 344, 8, 2.356194490192345], [43, 343, 8, 2.356194490192345], [44, 342, 8, 2.356194490192345], [44, 341, 8, 1.5707963267948966], [44, 340, 8, 1.5707963267948966], [44, 339, 8, 1.5707963267948966], [44, 338, 8, 1.5707963267948966], [44, 337, 8, 1.5707963267948966], [45, 336, 8, 2.356194490192345], [46, 336, 8, 3.141592653589793], [47, 335, 8, 2.356194490192345], [48, 335, 8, 3.141592653589793], [49, 335, 8, 3.141592653589793], [50, 335, 8, 3.141592653589793], [51, 335, 8, 3.141592653589793], [52, 334, 8, 2.356194490192345], [53, 333, 8, 2.356194490192345], [54, 332, 8, 2.356194490192345], [54, 331, 8, 1.5707963267948966], [54, 330, 8, 1.5707963267948966], [54, 329, 8, 1.5707963267948966], [54, 328, 8, 1.5707963267948966], [54, 327, 8, 1.5707963267948966], [55, 326, 8, 2.356194490192345], [55, 325, 8, 1.5707963267948966], [56, 324, 8, 2.356194490192345], [57, 323, 8, 2.356194490192345], [58, 322, 8, 2.356194490192345], [59, 321, 8, 2.356194490192345], [59, 320, 8, 1.5707963267948966], [59, 319, 8, 1.5707963267948966], [59, 318, 8, 1.5707963267948966], [59, 317, 8, 1.5707963267948966], [59, 316, 8, 1.5707963267948966], [60, 315, 8, 2.356194490192345], [60, 314, 8, 1.5707963267948966], [60, 313, 8, 1.5707963267948966], [61, 312, 8, 2.356194490192345], [61, 311, 8, 1.5707963267948966], [62, 310, 8, 2.356194490192345], [62, 309, 8, 1.5707963267948966], [63, 308, 8, 2.356194490192345], [63, 307, 8, 1.5707963267948966], [64, 306, 8, 2.356194490192345], [64, 305, 8, 1.5707963267948966], [64, 304, 8, 1.5707963267948966], [64, 303, 8, 1.5707963267948966], [64, 302, 8, 1.5707963267948966], [64, 301, 8, 1.5707963267948966], [64, 300, 8, 1.5707963267948966], [64, 299, 8, 1.5707963267948966], [64, 298, 8, 1.5707963267948966], [64, 297, 8, 1.5707963267948966], [64, 296, 8, 1.5707963267948966], [64, 295, 8, 1.5707963267948966], [64, 294, 8, 1.5707963267948966], [64, 293, 8, 1.5707963267948966], [64, 292, 8, 1.5707963267948966], [64, 291, 8, 1.5707963267948966], [64, 290, 8, 1.5707963267948966], [64, 289, 8, 1.5707963267948966], [64, 288, 8, 1.5707963267948966], [64, 287, 8, 1.5707963267948966], [65, 286, 8, 2.356194490192345], [64, 285, 8, 0.7853981633974483], [64, 284, 8, 1.5707963267948966], [64, 283, 8, 1.5707963267948966], [64, 282, 8, 1.5707963267948966], [64, 281, 8, 1.5707963267948966], [64, 280, 8, 1.5707963267948966], [64, 279, 8, 1.5707963267948966], [64, 278, 8, 1.5707963267948966], [64, 277, 8, 1.5707963267948966], [64, 276, 8, 1.5707963267948966], [64, 275, 8, 1.5707963267948966], [64, 274, 8, 1.5707963267948966], [64, 273, 8, 1.5707963267948966], [64, 272, 8, 1.5707963267948966], [64, 271, 8, 1.5707963267948966], [64, 270, 8, 1.5707963267948966], [64, 269, 8, 1.5707963267948966], [64, 268, 8, 1.5707963267948966], [64, 267, 8, 1.5707963267948966], [65, 266, 8, 2.356194490192345], [64, 265, 8, 0.7853981633974483], [64, 264, 8, 1.5707963267948966], [64, 263, 8, 1.5707963267948966], [64, 262, 8, 1.5707963267948966], [64, 261, 8, 1.5707963267948966], [64, 260, 8, 1.5707963267948966], [64, 259, 8, 1.5707963267948966], [64, 258, 8, 1.5707963267948966], [64, 257, 8, 1.5707963267948966], [64, 256, 8, 1.5707963267948966], [64, 255, 8, 1.5707963267948966], [64, 254, 8, 1.5707963267948966], [64, 253, 8, 1.5707963267948966], [64, 252, 8, 1.5707963267948966], [64, 251, 8, 1.5707963267948966], [64, 250, 8, 1.5707963267948966], [64, 249, 8, 1.5707963267948966], [64, 248, 8, 1.5707963267948966], [64, 247, 8, 1.5707963267948966], [65, 246, 8, 2.356194490192345], [64, 245, 8, 0.7853981633974483], [64, 244, 8, 1.5707963267948966], [64, 243, 8, 1.5707963267948966], [64, 242, 8, 1.5707963267948966], [63, 241, 8, 0.7853981633974483], [63, 240, 8, 1.5707963267948966], [63, 239, 8, 1.5707963267948966], [63, 238, 8, 1.5707963267948966], [63, 237, 8, 1.5707963267948966], [63, 236, 8, 1.5707963267948966], [63, 235, 8, 1.5707963267948966], [62, 234, 8, 0.7853981633974483], [61, 234, 8, 0.0], [60, 233, 8, 0.7853981633974483], [59, 232, 8, 0.7853981633974483], [58, 231, 8, 0.7853981633974483], [57, 231, 8, 0.0], [56, 230, 8, 0.7853981633974483], [55, 229, 8, 0.7853981633974483], [54, 229, 8, 0.0], [53, 228, 8, 0.7853981633974483], [52, 227, 8, 0.7853981633974483], [51, 227, 8, 0.0], [50, 226, 8, 0.7853981633974483], [49, 225, 8, 0.7853981633974483], [48, 226, 8, -0.7853981633974483], [47, 226, 8, 0.0], [46, 226, 8, 0.0], [45, 226, 8, 0.0], [44, 227, 8, -0.7853981633974483], [43, 227, 8, 0.0], [42, 227, 8, 0.0], [41, 228, 8, -0.7853981633974483], [40, 228, 8, 0.0], [39, 228, 8, 0.0], [38, 228, 8, 0.0], [37, 228, 8, 0.0], [36, 229, 8, -0.7853981633974483], [35, 229, 8, 0.0], [34, 230, 8, -0.7853981633974483], [33, 230, 8, 0.0], [32, 231, 8, -0.7853981633974483], [31, 231, 8, 0.0], [30, 232, 8, -0.7853981633974483], [29, 232, 8, 0.0], [28, 232, 8, 0.0], [27, 233, 8, -0.7853981633974483], [26, 233, 8, 0.0], [25, 233, 8, 0.0], [24, 234, 8, -0.7853981633974483], [23, 234, 8, 0.0], [22, 234, 8, 0.0], [21, 235, 8, -0.7853981633974483], [20, 235, 8, 0.0], [19, 235, 8, 0.0], [18, 236, 8, -0.7853981633974483], [17, 236, 8, 0.0], [16, 236, 8, 0.0], [15, 237, 8, -0.7853981633974483], [14, 237, 8, 0.0], [13, 237, 8, 0.0], [12, 237, 8, 0.0], [11, 238, 8, -0.7853981633974483], [10, 238, 8, 0.0], [9, 238, 8, 0.0], [8, 238, 8, 0.0], [7, 238, 8, 0.0], [6, 239, 8, -0.7853981633974483], [5, 239, 8, 0.0], [4, 239, 8, 0.0], [3, 239, 8, 0.0], [2, 239, 8, 0.0], [1, 239, 8, 0.0], [0, 239, 8, 0.0], [-1, 239, 8, 0.0], [-2, 240, 8, -0.7853981633974483], [-3, 240, 8, 0.0], [-4, 240, 8, 0.0], [-5, 240, 8, 0.0], [-6, 240, 8, 0.0], [-7, 240, 8, 0.0], [-8, 240, 8, 0.0], [-9, 240, 8, 0.0], [-10, 240, 8, 0.0], [-11, 241, 8, -0.7853981633974483], [-12, 241, 8, 0.0], [-13, 242, 8, -0.7853981633974483], [-14, 242, 8, 0.0], [-15, 243, 8, -0.7853981633974483], [-16, 244, 8, -0.7853981633974483], [-17, 244, 8, 0.0], [-18, 245, 8, -0.7853981633974483], [-19, 246, 8, -0.7853981633974483], [-20, 246, 8, 0.0], [-21, 247, 8, -0.7853981633974483], [-22, 247, 8, 0.0], [-23, 248, 8, -0.7853981633974483], [-24, 249, 8, -0.7853981633974483], [-25, 250, 8, -0.7853981633974483], [-26, 251, 8, -0.7853981633974483], [-27, 252, 8, -0.7853981633974483], [-28, 252, 8, 0.0], [-29, 253, 8, -0.7853981633974483], [-30, 254, 8, -0.7853981633974483], [-31, 255, 8, -0.7853981633974483], [-32, 256, 8, -0.7853981633974483], [-33, 257, 8, -0.7853981633974483], [-34, 258, 8, -0.7853981633974483], [-35, 259, 8, -0.7853981633974483], [-36, 260, 8, -0.7853981633974483], [-37, 261, 8, -0.7853981633974483], [-38, 262, 8, -0.7853981633974483], [-39, 263, 8, -0.7853981633974483], [-40, 264, 8, -0.7853981633974483], [-41, 265, 8, -0.7853981633974483], [-42, 265, 8, 0.0], [-43, 265, 8, 0.0], [-44, 265, 8, 0.0], [-45, 265, 8, 0.0], [-46, 265, 8, 0.0], [-47, 265, 8, 0.0], [-48, 265, 8, 0.0], [-49, 265, 8, 0.0], [-50, 265, 8, 0.0], [-51, 265, 8, 0.0], [-52, 265, 8, 0.0], [-53, 265, 8, 0.0], [-54, 265, 8, 0.0], [-55, 265, 8, 0.0], [-56, 265, 8, 0.0], [-57, 265, 8, 0.0], [-58, 265, 8, 0.0], [-59, 265, 8, 0.0], [-60, 265, 8, 0.0], [-61, 265, 8, 0.0], [-62, 265, 8, 0.0], [-63, 265, 8, 0.0], [-64, 265, 8, 0.0], [-65, 265, 8, 0.0], [-66, 265, 8, 0.0], [-67, 265, 8, 0.0], [-68, 265, 8, 0.0], [-69, 265, 8, 0.0], [-70, 265, 8, 0.0], [-71, 265, 8, 0.0], [-72, 265, 8, 0.0], [-73, 265, 8, 0.0], [-74, 265, 8, 0.0], [-75, 265, 8, 0.0], [-76, 265, 8, 0.0], [-77, 265, 8, 0.0], [-78, 265, 8, 0.0], [-79, 265, 8, 0.0], [-80, 265, 8, 0.0], [-81, 265, 8, 0.0], [-82, 265, 8, 0.0], [-83, 265, 8, 0.0], [-84, 265, 8, 0.0], [-85, 265, 8, 0.0], [-86, 265, 8, 0.0], [-87, 265, 8, 0.0], [-88, 265, 8, 0.0], [-89, 265, 8, 0.0], [-90, 265, 8, 0.0], [-91, 265, 8, 0.0], [-92, 265, 8, 0.0], [-93, 265, 8, 0.0], [-94, 265, 8, 0.0], [-95, 265, 8, 0.0], [-96, 265, 8, 0.0], [-97, 266, 8, -0.7853981633974483], [-98, 267, 8, -0.7853981633974483], [-98, 268, 8, -1.5707963267948966], [-99, 269, 8, -0.7853981633974483], [-100, 270, 8, -0.7853981633974483], [-101, 271, 8, -0.7853981633974483], [-102, 272, 8, -0.7853981633974483], [-103, 273, 8, -0.7853981633974483], [-104, 274, 8, -0.7853981633974483], [-105, 275, 8, -0.7853981633974483], [-106, 276, 8, -0.7853981633974483], [-107, 277, 8, -0.7853981633974483], [-108, 278, 8, -0.7853981633974483], [-108, 279, 8, -1.5707963267948966], [-109, 280, 8, -0.7853981633974483], [-110, 281, 8, -0.7853981633974483], [-110, 282, 8, -1.5707963267948966], [-111, 283, 8, -0.7853981633974483], [-112, 284, 8, -0.7853981633974483], [-113, 285, 8, -0.7853981633974483], [-113, 286, 8, -1.5707963267948966], [-114, 287, 8, -0.7853981633974483], [-115, 288, 8, -0.7853981633974483], [-115, 289, 8, -1.5707963267948966], [-116, 290, 8, -0.7853981633974483], [-117, 291, 8, -0.7853981633974483], [-117, 292, 8, -1.5707963267948966], [-118, 293, 8, -0.7853981633974483], [-119, 294, 8, -0.7853981633974483], [-120, 294, 8, 0.0], [-121, 295, 8, -0.7853981633974483], [-122, 296, 8, -0.7853981633974483], [-123, 296, 8, 0.0], [-124, 297, 8, -0.7853981633974483], [-125, 298, 8, -0.7853981633974483], [-125, 299, 8, -1.5707963267948966], [-126, 300, 8, -0.7853981633974483], [-127, 301, 8, -0.7853981633974483], [-127, 302, 8, -1.5707963267948966], [-128, 303, 8, -0.7853981633974483], [-129, 304, 8, -0.7853981633974483], [-130, 304, 8, 0.0], [-131, 305, 8, -0.7853981633974483], [-132, 306, 8, -0.7853981633974483], [-133, 306, 8, 0.0], [-134, 307, 8, -0.7853981633974483], [-135, 308, 8, -0.7853981633974483], [-135, 309, 8, -1.5707963267948966], [-136, 310, 8, -0.7853981633974483], [-137, 311, 8, -0.7853981633974483], [-138, 312, 8, -0.7853981633974483], [-139, 313, 8, -0.7853981633974483], [-140, 313, 8, 0.0], [-141, 313, 8, 0.0], [-142, 314, 8, -0.7853981633974483], [-143, 314, 8, 0.0], [-144, 314, 8, 0.0], [-145, 315, 8, -0.7853981633974483], [-146, 315, 8, 0.0], [-147, 315, 8, 0.0], [-148, 316, 8, -0.7853981633974483], [-149, 316, 8, 0.0], [-150, 316, 8, 0.0], [-151, 317, 8, -0.7853981633974483], [-152, 317, 8, 0.0], [-153, 317, 8, 0.0], [-154, 317, 8, 0.0], [-155, 318, 8, -0.7853981633974483], [-155, 319, 8, -1.5707963267948966], [-156, 320, 8, -0.7853981633974483], [-157, 321, 8, -0.7853981633974483], [-157, 322, 8, -1.5707963267948966], [-158, 323, 8, -0.7853981633974483], [-159, 324, 8, -0.7853981633974483], [-160, 324, 8, 0.0], [-161, 325, 8, -0.7853981633974483], [-162, 326, 8, -0.7853981633974483], [-163, 326, 8, 0.0], [-164, 327, 8, -0.7853981633974483], [-165, 328, 8, -0.7853981633974483], [-165, 329, 8, -1.5707963267948966], [-166, 330, 8, -0.7853981633974483], [-167, 331, 8, -0.7853981633974483], [-167, 332, 8, -1.5707963267948966], [-168, 333, 8, -0.7853981633974483], [-169, 334, 8, -0.7853981633974483], [-170, 334, 8, 0.0], [-171, 335, 8, -0.7853981633974483], [-172, 336, 8, -0.7853981633974483], [-173, 336, 8, 0.0], [-174, 337, 8, -0.7853981633974483], [-175, 338, 8, -0.7853981633974483], [-175, 339, 8, -1.5707963267948966], [-176, 340, 8, -0.7853981633974483], [-177, 341, 8, -0.7853981633974483], [-177, 342, 8, -1.5707963267948966], [-178, 343, 8, -0.7853981633974483], [-179, 344, 8, -0.7853981633974483], [-180, 344, 8, 0.0], [-181, 345, 8, -0.7853981633974483], [-182, 346, 8, -0.7853981633974483], [-183, 346, 8, 0.0], [-184, 347, 8, -0.7853981633974483], [-185, 348, 8, -0.7853981633974483], [-185, 349, 8, -1.5707963267948966], [-186, 350, 8, -0.7853981633974483], [-187, 351, 8, -0.7853981633974483], [-187, 352, 8, -1.5707963267948966], [-188, 353, 8, -0.7853981633974483], [-189, 354, 8, -0.7853981633974483], [-189, 355, 8, -1.5707963267948966], [-190, 356, 8, -0.7853981633974483], [-191, 357, 8, -0.7853981633974483], [-192, 358, 8, -0.7853981633974483], [-192, 359, 8, -1.5707963267948966], [-192, 360, 8, -1.5707963267948966], [-193, 361, 8, -0.7853981633974483], [-193, 362, 8, -1.5707963267948966], [-194, 363, 8, -0.7853981633974483], [-195, 364, 8, -0.7853981633974483], [-196, 365, 8, -0.7853981633974483], [-197, 366, 8, -0.7853981633974483], [-198, 367, 8, -0.7853981633974483], [-199, 368, 8, -0.7853981633974483], [-200, 369, 8, -0.7853981633974483], [-201, 370, 8, -0.7853981633974483], [-202, 371, 8, -0.7853981633974483], [-203, 371, 8, 0.0], [-204, 372, 8, -0.7853981633974483], [-205, 372, 8, 0.0], [-206, 373, 8, -0.7853981633974483], [-207, 373, 8, 0.0], [-208, 374, 8, -0.7853981633974483], [-209, 374, 8, 0.0], [-210, 375, 8, -0.7853981633974483], [-211, 375, 8, 0.0], [-212, 376, 8, -0.7853981633974483], [-213, 376, 8, 0.0], [-214, 377, 8, -0.7853981633974483], [-215, 377, 8, 0.0], [-216, 377, 8, 0.0], [-217, 378, 8, -0.7853981633974483], [-218, 378, 8, 0.0], [-219, 378, 8, 0.0], [-220, 379, 8, -0.7853981633974483], [-221, 379, 8, 0.0], [-222, 380, 8, -0.7853981633974483], [-223, 380, 8, 0.0], [-224, 380, 8, 0.0], [-225, 381, 8, -0.7853981633974483], [-226, 381, 8, 0.0], [-227, 382, 8, -0.7853981633974483], [-228, 383, 8, -0.7853981633974483], [-229, 383, 8, 0.0], [-230, 383, 8, 0.0], [-231, 383, 8, 0.0], [-232, 384, 8, -0.7853981633974483], [-233, 384, 8, 0.0], [-234, 384, 8, 0.0], [-235, 385, 8, -0.7853981633974483], [-236, 385, 8, 0.0], [-237, 386, 8, -0.7853981633974483], [-238, 386, 8, 0.0], [-239, 387, 8, -0.7853981633974483], [-240, 387, 8, 0.0], [-241, 388, 8, -0.7853981633974483], [-242, 389, 8, -0.7853981633974483], [-243, 388, 8, 0.7853981633974483], [-244, 389, 8, -0.7853981633974483], [-245, 389, 8, 0.0], [-246, 389, 8, 0.0], [-247, 390, 8, -0.7853981633974483], [-248, 390, 8, 0.0], [-249, 390, 8, 0.0], [-250, 391, 8, -0.7853981633974483], [-251, 391, 8, 0.0], [-252, 391, 8, 0.0], [-253, 391, 8, 0.0], [-254, 392, 8, -0.7853981633974483], [-255, 392, 8, 0.0], [-256, 392, 8, 0.0], [-257, 393, 8, -0.7853981633974483], [-258, 393, 8, 0.0], [-259, 393, 8, 0.0], [-260, 393, 8, 0.0], [-261, 393, 8, 0.0], [-262, 393, 8, 0.0], [-263, 393, 8, 0.0], [-264, 394, 8, -0.7853981633974483], [-265, 394, 8, 0.0], [-266, 394, 8, 0.0], [-267, 394, 8, 0.0], [-268, 394, 8, 0.0], [-269, 394, 8, 0.0], [-270, 394, 8, 0.0], [-271, 394, 8, 0.0], [-272, 395, 8, -0.7853981633974483], [-273, 395, 8, 0.0], [-274, 395, 8, 0.0], [-275, 396, 8, -0.7853981633974483], [-276, 395, 8, 0.7853981633974483], [-277, 395, 8, 0.0], [-278, 395, 8, 0.0], [-279, 395, 8, 0.0], [-280, 395, 8, 0.0], [-281, 395, 8, 0.0], [-282, 395, 8, 0.0], [-283, 395, 8, 0.0], [-284, 395, 8, 0.0], [-285, 395, 8, 0.0], [-286, 395, 8, 0.0], [-287, 395, 8, 0.0], [-288, 395, 8, 0.0], [-289, 395, 8, 0.0], [-290, 395, 8, 0.0], [-291, 395, 8, 0.0], [-292, 395, 8, 0.0], [-293, 395, 8, 0.0], [-294, 395, 8, 0.0], [-295, 395, 8, 0.0], [-296, 395, 8, 0.0], [-297, 395, 8, 0.0], [-298, 395, 8, 0.0], [-299, 395, 8, 0.0], [-300, 395, 8, 0.0], [-301, 395, 8, 0.0], [-302, 395, 8, 0.0], [-303, 395, 8, 0.0], [-304, 395, 8, 0.0], [-305, 395, 8, 0.0], [-306, 395, 8, 0.0], [-307, 395, 8, 0.0], [-308, 395, 8, 0.0], [-309, 395, 8, 0.0], [-310, 395, 8, 0.0], [-311, 395, 8, 0.0], [-312, 395, 8, 0.0], [-313, 395, 8, 0.0], [-314, 395, 8, 0.0], [-315, 395, 8, 0.0], [-316, 394, 8, 0.7853981633974483], [-316, 393, 8, 1.5707963267948966], [-316, 392, 8, 1.5707963267948966], [-316, 391, 8, 1.5707963267948966], [-316, 390, 8, 1.5707963267948966], [-316, 389, 8, 1.5707963267948966], [-316, 388, 8, 1.5707963267948966], [-316, 387, 8, 1.5707963267948966], [-316, 386, 8, 1.5707963267948966], [-316, 385, 8, 1.5707963267948966], [-316, 384, 8, 1.5707963267948966], [-316, 383, 8, 1.5707963267948966], [-316, 382, 8, 1.5707963267948966], [-316, 381, 8, 1.5707963267948966], [-316, 380, 8, 1.5707963267948966], [-316, 379, 8, 1.5707963267948966], [-316, 378, 8, 1.5707963267948966], [-316, 377, 8, 1.5707963267948966], [-316, 376, 8, 1.5707963267948966], [-316, 375, 8, 1.5707963267948966], [-316, 374, 8, 1.5707963267948966], [-316, 373, 8, 1.5707963267948966], [-316, 372, 8, 1.5707963267948966], [-316, 371, 8, 1.5707963267948966], [-316, 370, 8, 1.5707963267948966], [-316, 369, 8, 1.5707963267948966], [-316, 368, 8, 1.5707963267948966], [-316, 367, 8, 1.5707963267948966], [-316, 366, 8, 1.5707963267948966], [-316, 365, 8, 1.5707963267948966], [-316, 364, 8, 1.5707963267948966], [-316, 363, 8, 1.5707963267948966], [-316, 362, 8, 1.5707963267948966], [-316, 361, 8, 1.5707963267948966], [-316, 360, 8, 1.5707963267948966], [-316, 359, 8, 1.5707963267948966], [-316, 358, 8, 1.5707963267948966], [-316, 357, 8, 1.5707963267948966], [-316, 356, 8, 1.5707963267948966], [-316, 355, 8, 1.5707963267948966], [-316, 354, 8, 1.5707963267948966], [-316, 353, 8, 1.5707963267948966], [-316, 352, 8, 1.5707963267948966], [-316, 351, 8, 1.5707963267948966], [-316, 350, 8, 1.5707963267948966], [-316, 349, 8, 1.5707963267948966], [-316, 348, 8, 1.5707963267948966], [-316, 347, 8, 1.5707963267948966], [-316, 346, 8, 1.5707963267948966], [-316, 345, 8, 1.5707963267948966], [-316, 344, 8, 1.5707963267948966], [-316, 343, 8, 1.5707963267948966], [-316, 342, 8, 1.5707963267948966], [-316, 341, 8, 1.5707963267948966], [-316, 340, 8, 1.5707963267948966], [-316, 339, 8, 1.5707963267948966], [-316, 338, 8, 1.5707963267948966], [-316, 337, 8, 1.5707963267948966], [-316, 336, 8, 1.5707963267948966], [-316, 335, 8, 1.5707963267948966], [-316, 334, 8, 1.5707963267948966], [-316, 333, 8, 1.5707963267948966], [-316, 332, 8, 1.5707963267948966], [-316, 331, 8, 1.5707963267948966], [-316, 330, 8, 1.5707963267948966], [-316, 329, 8, 1.5707963267948966], [-316, 328, 8, 1.5707963267948966], [-316, 327, 8, 1.5707963267948966], [-316, 326, 8, 1.5707963267948966], [-316, 325, 8, 1.5707963267948966], [-316, 324, 8, 1.5707963267948966], [-316, 323, 8, 1.5707963267948966], [-316, 322, 8, 1.5707963267948966], [-316, 321, 8, 1.5707963267948966], [-316, 320, 8, 1.5707963267948966], [-316, 319, 8, 1.5707963267948966], [-316, 318, 8, 1.5707963267948966], [-316, 317, 8, 1.5707963267948966], [-316, 316, 8, 1.5707963267948966], [-316, 315, 8, 1.5707963267948966], [-316, 314, 8, 1.5707963267948966], [-316, 313, 8, 1.5707963267948966], [-316, 312, 8, 1.5707963267948966], [-316, 311, 8, 1.5707963267948966], [-316, 310, 8, 1.5707963267948966], [-316, 309, 8, 1.5707963267948966], [-316, 308, 8, 1.5707963267948966], [-316, 307, 8, 1.5707963267948966], [-316, 306, 8, 1.5707963267948966], [-316, 305, 8, 1.5707963267948966], [-316, 304, 8, 1.5707963267948966], [-316, 303, 8, 1.5707963267948966], [-316, 302, 8, 1.5707963267948966], [-316, 301, 8, 1.5707963267948966], [-316, 300, 8, 1.5707963267948966], [-316, 299, 8, 1.5707963267948966], [-316, 298, 8, 1.5707963267948966], [-316, 297, 8, 1.5707963267948966], [-316, 296, 8, 1.5707963267948966], [-316, 295, 8, 1.5707963267948966], [-316, 294, 8, 1.5707963267948966], [-316, 293, 8, 1.5707963267948966], [-315, 292, 8, 2.356194490192345], [-314, 292, 8, 3.141592653589793], [-313, 292, 8, 3.141592653589793], [-312, 291, 8, 2.356194490192345], [-311, 291, 8, 3.141592653589793], [-310, 291, 8, 3.141592653589793], [-309, 290, 8, 2.356194490192345], [-308, 290, 8, 3.141592653589793], [-307, 289, 8, 2.356194490192345], [-306, 289, 8, 3.141592653589793], [-305, 289, 8, 3.141592653589793], [-304, 288, 8, 2.356194490192345], [-303, 288, 8, 3.141592653589793], [-302, 287, 8, 2.356194490192345], [-301, 287, 8, 3.141592653589793], [-300, 287, 8, 3.141592653589793], [-299, 286, 8, 2.356194490192345], [-298, 286, 8, 3.141592653589793], [-297, 286, 8, 3.141592653589793], [-296, 285, 8, 2.356194490192345], [-295, 285, 8, 3.141592653589793], [-294, 284, 8, 2.356194490192345], [-293, 284, 8, 3.141592653589793], [-292, 284, 8, 3.141592653589793], [-291, 283, 8, 2.356194490192345], [-290, 283, 8, 3.141592653589793], [-289, 283, 8, 3.141592653589793], [-288, 282, 8, 2.356194490192345], [-287, 282, 8, 3.141592653589793], [-286, 281, 8, 2.356194490192345], [-285, 281, 8, 3.141592653589793], [-284, 281, 8, 3.141592653589793], [-283, 280, 8, 2.356194490192345], [-282, 280, 8, 3.141592653589793], [-281, 279, 8, 2.356194490192345], [-280, 279, 8, 3.141592653589793], [-279, 279, 8, 3.141592653589793], [-278, 278, 8, 2.356194490192345], [-277, 278, 8, 3.141592653589793], [-276, 277, 8, 2.356194490192345], [-275, 276, 8, 2.356194490192345], [-274, 276, 8, 3.141592653589793], [-273, 275, 8, 2.356194490192345], [-272, 274, 8, 2.356194490192345], [-271, 274, 8, 3.141592653589793], [-270, 274, 8, 3.141592653589793], [-269, 273, 8, 2.356194490192345], [-268, 272, 8, 2.356194490192345], [-267, 271, 8, 2.356194490192345], [-266, 270, 8, 2.356194490192345], [-265, 270, 8, 3.141592653589793], [-264, 269, 8, 2.356194490192345], [-263, 269, 8, 3.141592653589793], [-262, 268, 8, 2.356194490192345], [-261, 268, 8, 3.141592653589793], [-260, 267, 8, 2.356194490192345], [-259, 267, 8, 3.141592653589793], [-258, 266, 8, 2.356194490192345], [-257, 266, 8, 3.141592653589793], [-256, 265, 8, 2.356194490192345], [-255, 265, 8, 3.141592653589793], [-254, 264, 8, 2.356194490192345], [-253, 264, 8, 3.141592653589793], [-252, 264, 8, 3.141592653589793], [-251, 263, 8, 2.356194490192345], [-250, 263, 8, 3.141592653589793], [-249, 263, 8, 3.141592653589793], [-248, 263, 8, 3.141592653589793], [-247, 262, 8, 2.356194490192345], [-246, 261, 8, 2.356194490192345], [-245, 261, 8, 3.141592653589793], [-244, 260, 8, 2.356194490192345], [-243, 259, 8, 2.356194490192345], [-242, 259, 8, 3.141592653589793], [-241, 258, 8, 2.356194490192345], [-240, 257, 8, 2.356194490192345], [-240, 256, 8, 1.5707963267948966], [-239, 255, 8, 2.356194490192345], [-238, 254, 8, 2.356194490192345], [-238, 253, 8, 1.5707963267948966], [-237, 252, 8, 2.356194490192345], [-237, 251, 8, 1.5707963267948966], [-236, 250, 8, 2.356194490192345], [-236, 249, 8, 1.5707963267948966], [-235, 248, 8, 2.356194490192345], [-235, 247, 8, 1.5707963267948966], [-234, 246, 8, 2.356194490192345], [-234, 245, 8, 1.5707963267948966], [-233, 244, 8, 2.356194490192345], [-233, 243, 8, 1.5707963267948966], [-232, 242, 8, 2.356194490192345], [-231, 242, 8, 3.141592653589793], [-230, 241, 8, 2.356194490192345], [-229, 241, 8, 3.141592653589793], [-228, 240, 8, 2.356194490192345], [-227, 239, 8, 2.356194490192345], [-226, 238, 8, 2.356194490192345], [-225, 238, 8, 3.141592653589793], [-224, 237, 8, 2.356194490192345], [-223, 236, 8, 2.356194490192345], [-222, 236, 8, 3.141592653589793], [-221, 235, 8, 2.356194490192345], [-220, 234, 8, 2.356194490192345], [-219, 234, 8, 3.141592653589793], [-218, 233, 8, 2.356194490192345], [-218, 232, 8, 1.5707963267948966], [-218, 231, 8, 1.5707963267948966], [-218, 230, 8, 1.5707963267948966], [-217, 229, 8, 2.356194490192345], [-217, 228, 8, 1.5707963267948966], [-217, 227, 8, 1.5707963267948966], [-217, 226, 8, 1.5707963267948966], [-216, 225, 8, 2.356194490192345], [-216, 224, 8, 1.5707963267948966], [-215, 223, 8, 2.356194490192345], [-215, 222, 8, 1.5707963267948966], [-214, 221, 8, 2.356194490192345], [-214, 220, 8, 1.5707963267948966], [-213, 219, 8, 2.356194490192345], [-213, 218, 8, 1.5707963267948966], [-212, 217, 8, 2.356194490192345], [-212, 216, 8, 1.5707963267948966], [-211, 215, 8, 2.356194490192345], [-210, 214, 8, 2.356194490192345], [-210, 213, 8, 1.5707963267948966], [-209, 212, 8, 2.356194490192345], [-208, 211, 8, 2.356194490192345], [-207, 211, 8, 3.141592653589793], [-206, 210, 8, 2.356194490192345], [-205, 209, 8, 2.356194490192345], [-204, 209, 8, 3.141592653589793], [-203, 208, 8, 2.356194490192345], [-202, 207, 8, 2.356194490192345], [-202, 206, 8, 1.5707963267948966], [-201, 205, 8, 2.356194490192345], [-200, 204, 8, 2.356194490192345], [-200, 203, 8, 1.5707963267948966], [-199, 202, 8, 2.356194490192345], [-198, 201, 8, 2.356194490192345], [-197, 201, 8, 3.141592653589793], [-196, 200, 8, 2.356194490192345], [-195, 199, 8, 2.356194490192345], [-194, 199, 8, 3.141592653589793], [-193, 198, 8, 2.356194490192345], [-192, 198, 8, 3.141592653589793], [-191, 197, 8, 2.356194490192345], [-190, 197, 8, 3.141592653589793], [-189, 196, 8, 2.356194490192345], [-188, 196, 8, 3.141592653589793], [-187, 195, 8, 2.356194490192345], [-186, 194, 8, 2.356194490192345], [-185, 193, 8, 2.356194490192345], [-184, 192, 8, 2.356194490192345], [-183, 191, 8, 2.356194490192345], [-182, 191, 8, 3.141592653589793], [-181, 190, 8, 2.356194490192345], [-180, 189, 8, 2.356194490192345], [-179, 188, 8, 2.356194490192345], [-178, 187, 8, 2.356194490192345], [-177, 186, 8, 2.356194490192345], [-176, 185, 8, 2.356194490192345], [-175, 185, 8, 3.141592653589793], [-174, 185, 8, 3.141592653589793], [-173, 185, 8, 3.141592653589793], [-172, 185, 8, 3.141592653589793], [-171, 185, 8, 3.141592653589793], [-170, 185, 8, 3.141592653589793], [-169, 185, 8, 3.141592653589793], [-168, 185, 8, 3.141592653589793], [-167, 185, 8, 3.141592653589793], [-166, 184, 8, 2.356194490192345], [-165, 183, 8, 2.356194490192345], [-164, 182, 8, 2.356194490192345], [-164, 181, 8, 1.5707963267948966], [-163, 180, 8, 2.356194490192345], [-162, 179, 8, 2.356194490192345], [-162, 178, 8, 1.5707963267948966], [-161, 177, 8, 2.356194490192345], [-160, 176, 8, 2.356194490192345], [-160, 175, 8, 1.5707963267948966], [-159, 174, 8, 2.356194490192345], [-159, 173, 8, 1.5707963267948966], [-158, 172, 8, 2.356194490192345], [-158, 171, 8, 1.5707963267948966], [-158, 170, 8, 1.5707963267948966], [-157, 169, 8, 2.356194490192345], [-157, 168, 8, 1.5707963267948966], [-157, 167, 8, 1.5707963267948966], [-157, 166, 8, 1.5707963267948966], [-156, 165, 8, 2.356194490192345], [-156, 164, 8, 1.5707963267948966], [-155, 163, 8, 2.356194490192345], [-155, 162, 8, 1.5707963267948966], [-154, 161, 8, 2.356194490192345], [-154, 160, 8, 1.5707963267948966], [-153, 159, 8, 2.356194490192345], [-153, 158, 8, 1.5707963267948966], [-152, 157, 8, 2.356194490192345], [-152, 156, 8, 1.5707963267948966], [-151, 155, 8, 2.356194490192345], [-150, 154, 8, 2.356194490192345], [-150, 153, 8, 1.5707963267948966], [-149, 152, 8, 2.356194490192345], [-148, 151, 8, 2.356194490192345], [-147, 151, 8, 3.141592653589793], [-146, 150, 8, 2.356194490192345], [-145, 149, 8, 2.356194490192345], [-144, 149, 8, 3.141592653589793], [-143, 148, 8, 2.356194490192345], [-142, 147, 8, 2.356194490192345], [-142, 146, 8, 1.5707963267948966], [-141, 145, 8, 2.356194490192345], [-140, 144, 8, 2.356194490192345], [-140, 143, 8, 1.5707963267948966], [-139, 142, 8, 2.356194490192345], [-138, 141, 8, 2.356194490192345], [-137, 141, 8, 3.141592653589793], [-136, 140, 8, 2.356194490192345], [-135, 139, 8, 2.356194490192345], [-134, 139, 8, 3.141592653589793], [-133, 138, 8, 2.356194490192345], [-132, 137, 8, 2.356194490192345], [-132, 136, 8, 1.5707963267948966], [-131, 135, 8, 2.356194490192345], [-130, 134, 8, 2.356194490192345], [-130, 133, 8, 1.5707963267948966], [-129, 132, 8, 2.356194490192345], [-128, 131, 8, 2.356194490192345], [-127, 131, 8, 3.141592653589793], [-126, 130, 8, 2.356194490192345], [-125, 129, 8, 2.356194490192345], [-124, 129, 8, 3.141592653589793], [-123, 128, 8, 2.356194490192345], [-122, 128, 8, 3.141592653589793], [-121, 127, 8, 2.356194490192345], [-120, 127, 8, 3.141592653589793], [-119, 126, 8, 2.356194490192345], [-118, 126, 8, 3.141592653589793], [-117, 125, 8, 2.356194490192345], [-116, 125, 8, 3.141592653589793], [-115, 124, 8, 2.356194490192345], [-114, 123, 8, 2.356194490192345], [-113, 122, 8, 2.356194490192345], [-112, 121, 8, 2.356194490192345], [-111, 120, 8, 2.356194490192345], [-110, 119, 8, 2.356194490192345], [-109, 118, 8, 2.356194490192345], [-108, 117, 8, 2.356194490192345], [-107, 116, 8, 2.356194490192345], [-106, 115, 8, 2.356194490192345], [-106, 114, 8, 1.5707963267948966], [-106, 113, 8, 1.5707963267948966], [-106, 112, 8, 1.5707963267948966], [-106, 111, 8, 1.5707963267948966], [-106, 110, 8, 1.5707963267948966], [-106, 109, 8, 1.5707963267948966], [-106, 108, 8, 1.5707963267948966], [-106, 107, 8, 1.5707963267948966], [-106, 106, 8, 1.5707963267948966], [-106, 105, 8, 1.5707963267948966], [-106, 104, 8, 1.5707963267948966], [-106, 103, 8, 1.5707963267948966], [-106, 102, 8, 1.5707963267948966], [-106, 101, 8, 1.5707963267948966], [-106, 100, 8, 1.5707963267948966], [-106, 99, 8, 1.5707963267948966], [-106, 98, 8, 1.5707963267948966], [-106, 97, 8, 1.5707963267948966], [-106, 96, 8, 1.5707963267948966], [-106, 95, 8, 1.5707963267948966], [-106, 94, 8, 1.5707963267948966], [-106, 93, 8, 1.5707963267948966], [-106, 92, 8, 1.5707963267948966], [-106, 91, 8, 1.5707963267948966], [-106, 90, 8, 1.5707963267948966], [-106, 89, 8, 1.5707963267948966], [-106, 88, 8, 1.5707963267948966], [-106, 87, 8, 1.5707963267948966], [-106, 86, 8, 1.5707963267948966], [-106, 85, 8, 1.5707963267948966], [-106, 84, 8, 1.5707963267948966], [-106, 83, 8, 1.5707963267948966], [-106, 82, 8, 1.5707963267948966], [-106, 81, 8, 1.5707963267948966], [-106, 80, 8, 1.5707963267948966], [-106, 79, 8, 1.5707963267948966], [-106, 78, 8, 1.5707963267948966], [-106, 77, 8, 1.5707963267948966], [-106, 76, 8, 1.5707963267948966], [-106, 75, 8, 1.5707963267948966], [-106, 74, 8, 1.5707963267948966], [-106, 73, 8, 1.5707963267948966], [-106, 72, 8, 1.5707963267948966], [-106, 71, 8, 1.5707963267948966], [-106, 70, 8, 1.5707963267948966], [-106, 69, 8, 1.5707963267948966], [-106, 68, 8, 1.5707963267948966], [-106, 67, 8, 1.5707963267948966], [-105, 66, 8, 2.356194490192345], [-106, 65, 8, 0.7853981633974483], [-107, 64, 8, 0.7853981633974483], [-108, 63, 8, 0.7853981633974483], [-109, 62, 8, 0.7853981633974483], [-110, 61, 8, 0.7853981633974483], [-111, 60, 8, 0.7853981633974483], [-111, 59, 8, 1.5707963267948966], [-111, 58, 8, 1.5707963267948966], [-111, 57, 8, 1.5707963267948966], [-111, 56, 8, 1.5707963267948966], [-111, 55, 8, 1.5707963267948966], [-111, 54, 8, 1.5707963267948966], [-111, 53, 8, 1.5707963267948966], [-111, 52, 8, 1.5707963267948966], [-111, 51, 8, 1.5707963267948966], [-111, 50, 8, 1.5707963267948966], [-111, 49, 8, 1.5707963267948966], [-112, 48, 8, 0.7853981633974483], [-112, 47, 8, 1.5707963267948966], [-112, 46, 8, 1.5707963267948966], [-113, 45, 8, 0.7853981633974483], [-113, 44, 8, 1.5707963267948966], [-113, 43, 8, 1.5707963267948966], [-114, 42, 8, 0.7853981633974483], [-114, 41, 8, 1.5707963267948966], [-114, 40, 8, 1.5707963267948966], [-115, 39, 8, 0.7853981633974483], [-115, 38, 8, 1.5707963267948966], [-115, 37, 8, 1.5707963267948966], [-115, 36, 8, 1.5707963267948966], [-116, 35, 8, 0.7853981633974483], [-117, 34, 8, 0.7853981633974483], [-118, 33, 8, 0.7853981633974483]]

In [1]:
path=[[-1, 0, 100, 0], [3, 4, 100, -2.356194490192345], [5, 2, 100, 2.356194490192345], [5, 0, 100, 1.5707963267948966], [6, -1, 100, 2.356194490192345], [6, -3, 100, 1.5707963267948966], [7, -4, 100, 2.356194490192345], [7, -6, 100, 1.5707963267948966], [8, -7, 100, 2.356194490192345], [8, -9, 100, 1.5707963267948966], [10, -11, 100, 2.356194490192345], [9, -12, 100, 0.7853981633974483], [9, -64, 100, 1.5707963267948966], [8, -65, 100, 0.7853981633974483], [8, -67, 100, 1.5707963267948966], [7, -68, 100, 0.7853981633974483], [7, -69, 100, 1.5707963267948966], [6, -70, 100, 0.7853981633974483], [6, -71, 100, 1.5707963267948966], [5, -72, 100, 0.7853981633974483], [5, -73, 100, 1.5707963267948966], [4, -74, 100, 0.7853981633974483], [4, -95, 100, 1.5707963267948966], [5, -96, 100, 2.356194490192345], [5, -99, 100, 1.5707963267948966], [6, -100, 100, 2.356194490192345], [6, -102, 100, 1.5707963267948966], [7, -103, 100, 2.356194490192345], [7, -104, 100, 1.5707963267948966], [8, -105, 100, 2.356194490192345], [8, -106, 100, 1.5707963267948966], [10, -108, 100, 2.356194490192345], [10, -110, 100, 1.5707963267948966], [11, -111, 100, 2.356194490192345], [11, -114, 100, 1.5707963267948966], [12, -115, 100, 2.356194490192345], [12, -116, 100, 1.5707963267948966], [13, -117, 100, 2.356194490192345], [15, -117, 100, 3.141592653589793], [16, -118, 100, 2.356194490192345], [18, -118, 100, 3.141592653589793], [19, -119, 100, 2.356194490192345], [22, -119, 100, 3.141592653589793], [23, -120, 100, 2.356194490192345], [45, -120, 100, 3.141592653589793], [46, -121, 100, 2.356194490192345], [49, -121, 100, 3.141592653589793], [50, -122, 100, 2.356194490192345], [52, -122, 100, 3.141592653589793], [53, -123, 100, 2.356194490192345], [55, -123, 100, 3.141592653589793], [56, -124, 100, 2.356194490192345], [57, -124, 100, 3.141592653589793], [58, -125, 100, 2.356194490192345], [59, -125, 100, 3.141592653589793], [60, -126, 100, 2.356194490192345], [61, -126, 100, 3.141592653589793], [62, -127, 100, 2.356194490192345], [64, -127, 100, 3.141592653589793], [65, -128, 100, 2.356194490192345], [67, -128, 100, 3.141592653589793], [68, -129, 100, 2.356194490192345], [70, -129, 100, 3.141592653589793], [71, -130, 100, 2.356194490192345], [72, -130, 100, 3.141592653589793], [73, -131, 100, 2.356194490192345], [74, -131, 100, 3.141592653589793], [75, -132, 100, 2.356194490192345], [77, -132, 100, 3.141592653589793], [78, -133, 100, 2.356194490192345], [79, -133, 100, 3.141592653589793], [80, -134, 100, 2.356194490192345], [82, -134, 100, 3.141592653589793], [83, -135, 100, 2.356194490192345], [84, -135, 100, 3.141592653589793], [85, -136, 100, 2.356194490192345], [87, -136, 100, 3.141592653589793], [88, -137, 100, 2.356194490192345], [89, -137, 100, 3.141592653589793], [90, -138, 100, 2.356194490192345], [92, -138, 100, 3.141592653589793], [93, -139, 100, 2.356194490192345], [94, -139, 100, 3.141592653589793], [95, -140, 100, 2.356194490192345], [96, -140, 100, 3.141592653589793], [97, -141, 100, 2.356194490192345], [99, -141, 100, 3.141592653589793], [100, -142, 100, 2.356194490192345], [101, -142, 100, 3.141592653589793], [102, -143, 100, 2.356194490192345], [104, -143, 100, 3.141592653589793], [105, -144, 100, 2.356194490192345], [106, -144, 100, 3.141592653589793], [107, -145, 100, 2.356194490192345], [109, -145, 100, 3.141592653589793], [110, -146, 100, 2.356194490192345], [111, -146, 100, 3.141592653589793], [112, -147, 100, 2.356194490192345], [114, -147, 100, 3.141592653589793], [115, -148, 100, 2.356194490192345], [116, -148, 100, 3.141592653589793], [117, -149, 100, 2.356194490192345], [119, -149, 100, 3.141592653589793], [123, -153, 100, 2.356194490192345], [124, -153, 100, 3.141592653589793], [125, -154, 100, 2.356194490192345], [126, -153, 100, -2.356194490192345], [128, -153, 100, 3.141592653589793], [132, -157, 100, 2.356194490192345], [133, -156, 100, -2.356194490192345], [134, -157, 100, 2.356194490192345], [135, -156, 100, -2.356194490192345], [136, -157, 100, 2.356194490192345], [138, -157, 100, 3.141592653589793], [143, -162, 100, 2.356194490192345], [145, -162, 100, 3.141592653589793], [146, -161, 100, -2.356194490192345], [149, -164, 100, 2.356194490192345], [150, -164, 100, 3.141592653589793], [151, -165, 100, 2.356194490192345], [152, -164, 100, -2.356194490192345], [153, -165, 100, 2.356194490192345], [154, -165, 100, 3.141592653589793], [155, -166, 100, 2.356194490192345], [156, -165, 100, -2.356194490192345], [158, -167, 100, 2.356194490192345], [159, -166, 100, -2.356194490192345], [159, -165, 100, -1.5707963267948966], [160, -164, 100, -2.356194490192345], [160, -163, 100, -1.5707963267948966], [162, -161, 100, -2.356194490192345], [162, -160, 100, -1.5707963267948966], [166, -156, 100, -2.356194490192345], [166, -155, 100, -1.5707963267948966], [169, -152, 100, -2.356194490192345], [169, -151, 100, -1.5707963267948966], [171, -149, 100, -2.356194490192345], [171, -148, 100, -1.5707963267948966], [173, -146, 100, -2.356194490192345], [173, -145, 100, -1.5707963267948966], [175, -143, 100, -2.356194490192345], [175, -142, 100, -1.5707963267948966], [178, -139, 100, -2.356194490192345], [178, -138, 100, -1.5707963267948966], [180, -136, 100, -2.356194490192345], [180, -135, 100, -1.5707963267948966], [183, -132, 100, -2.356194490192345], [183, -131, 100, -1.5707963267948966], [186, -128, 100, -2.356194490192345], [188, -128, 100, 3.141592653589793], [189, -127, 100, -2.356194490192345], [191, -127, 100, 3.141592653589793], [192, -126, 100, -2.356194490192345], [194, -126, 100, 3.141592653589793], [195, -125, 100, -2.356194490192345], [197, -125, 100, 3.141592653589793], [198, -124, 100, -2.356194490192345], [201, -124, 100, 3.141592653589793], [202, -123, 100, -2.356194490192345], [204, -123, 100, 3.141592653589793], [205, -122, 100, -2.356194490192345], [207, -122, 100, 3.141592653589793], [208, -121, 100, -2.356194490192345], [210, -121, 100, 3.141592653589793], [211, -120, 100, -2.356194490192345], [213, -120, 100, 3.141592653589793], [214, -119, 100, -2.356194490192345], [216, -119, 100, 3.141592653589793], [217, -118, 100, -2.356194490192345], [220, -118, 100, 3.141592653589793], [221, -117, 100, -2.356194490192345], [223, -117, 100, 3.141592653589793], [224, -116, 100, -2.356194490192345], [227, -116, 100, 3.141592653589793], [228, -115, 100, -2.356194490192345], [231, -115, 100, 3.141592653589793], [232, -114, 100, -2.356194490192345], [235, -114, 100, 3.141592653589793], [236, -113, 100, -2.356194490192345], [237, -113, 100, 3.141592653589793], [243, -107, 100, -2.356194490192345], [244, -107, 100, 3.141592653589793], [248, -103, 100, -2.356194490192345], [249, -103, 100, 3.141592653589793], [253, -99, 100, -2.356194490192345], [254, -99, 100, 3.141592653589793], [256, -97, 100, -2.356194490192345], [257, -97, 100, 3.141592653589793], [259, -95, 100, -2.356194490192345], [260, -95, 100, 3.141592653589793], [262, -93, 100, -2.356194490192345], [263, -93, 100, 3.141592653589793], [265, -91, 100, -2.356194490192345], [266, -91, 100, 3.141592653589793], [267, -90, 100, -2.356194490192345], [268, -90, 100, 3.141592653589793], [270, -88, 100, -2.356194490192345], [271, -88, 100, 3.141592653589793], [272, -87, 100, -2.356194490192345], [273, -88, 100, 2.356194490192345], [275, -88, 100, 3.141592653589793], [276, -87, 100, -2.356194490192345], [277, -88, 100, 2.356194490192345], [278, -88, 100, 3.141592653589793], [279, -89, 100, 2.356194490192345], [280, -88, 100, -2.356194490192345], [283, -91, 100, 2.356194490192345], [284, -91, 100, 3.141592653589793], [285, -92, 100, 2.356194490192345], [287, -90, 100, -2.356194490192345], [285, -88, 100, -0.7853981633974483], [284, -88, 100, 0.0], [281, -85, 100, -0.7853981633974483], [280, -86, 100, 0.7853981633974483], [279, -85, 100, -0.7853981633974483], [278, -86, 100, 0.7853981633974483], [275, -83, 100, -0.7853981633974483], [279, -79, 100, -2.356194490192345], [279, -78, 100, -1.5707963267948966], [283, -74, 100, -2.356194490192345], [283, -73, 100, -1.5707963267948966], [285, -71, 100, -2.356194490192345], [285, -70, 100, -1.5707963267948966], [287, -68, 100, -2.356194490192345], [287, -67, 100, -1.5707963267948966], [289, -65, 100, -2.356194490192345], [289, -64, 100, -1.5707963267948966], [290, -63, 100, -2.356194490192345], [290, -62, 100, -1.5707963267948966], [291, -61, 100, -2.356194490192345], [291, -60, 100, -1.5707963267948966], [292, -59, 100, -2.356194490192345], [292, -58, 100, -1.5707963267948966], [293, -57, 100, -2.356194490192345], [293, -56, 100, -1.5707963267948966], [294, -55, 100, -2.356194490192345], [294, -54, 100, -1.5707963267948966], [295, -53, 100, -2.356194490192345], [295, -52, 100, -1.5707963267948966], [296, -51, 100, -2.356194490192345], [296, -50, 100, -1.5707963267948966], [297, -49, 100, -2.356194490192345], [297, -48, 100, -1.5707963267948966], [298, -47, 100, -2.356194490192345], [298, -46, 100, -1.5707963267948966], [300, -44, 100, -2.356194490192345], [300, -43, 100, -1.5707963267948966], [301, -42, 100, -2.356194490192345], [301, -41, 100, -1.5707963267948966], [302, -40, 100, -2.356194490192345], [302, -39, 100, -1.5707963267948966], [303, -38, 100, -2.356194490192345], [303, -37, 100, -1.5707963267948966], [305, -35, 100, -2.356194490192345], [306, -36, 100, 2.356194490192345], [307, -36, 100, 3.141592653589793], [308, -37, 100, 2.356194490192345], [310, -37, 100, 3.141592653589793], [311, -38, 100, 2.356194490192345], [312, -38, 100, 3.141592653589793], [314, -40, 100, 2.356194490192345], [315, -40, 100, 3.141592653589793], [316, -41, 100, 2.356194490192345], [317, -41, 100, 3.141592653589793], [318, -42, 100, 2.356194490192345], [319, -42, 100, 3.141592653589793], [320, -43, 100, 2.356194490192345], [321, -43, 100, 3.141592653589793], [322, -44, 100, 2.356194490192345], [323, -44, 100, 3.141592653589793], [324, -45, 100, 2.356194490192345], [325, -45, 100, 3.141592653589793], [326, -46, 100, 2.356194490192345], [327, -46, 100, 3.141592653589793], [328, -47, 100, 2.356194490192345], [329, -47, 100, 3.141592653589793], [330, -48, 100, 2.356194490192345], [331, -48, 100, 3.141592653589793], [332, -49, 100, 2.356194490192345], [334, -49, 100, 3.141592653589793], [335, -50, 100, 2.356194490192345], [359, -50, 100, 3.141592653589793], [360, -51, 100, 2.356194490192345], [361, -51, 100, 3.141592653589793], [364, -54, 100, 2.356194490192345], [366, -54, 100, 3.141592653589793], [367, -55, 100, 2.356194490192345], [416, -55, 100, 3.141592653589793], [417, -54, 100, -2.356194490192345], [418, -55, 100, 2.356194490192345], [424, -55, 100, 3.141592653589793], [425, -56, 100, 2.356194490192345], [427, -56, 100, 3.141592653589793], [428, -57, 100, 2.356194490192345], [430, -57, 100, 3.141592653589793], [431, -58, 100, 2.356194490192345], [433, -58, 100, 3.141592653589793], [434, -59, 100, 2.356194490192345], [436, -59, 100, 3.141592653589793], [437, -60, 100, 2.356194490192345], [439, -60, 100, 3.141592653589793], [442, -63, 100, 2.356194490192345], [443, -62, 100, -2.356194490192345], [444, -62, 100, 3.141592653589793], [449, -67, 100, 2.356194490192345], [450, -66, 100, -2.356194490192345], [452, -68, 100, 2.356194490192345], [453, -68, 100, 3.141592653589793], [454, -67, 100, -2.356194490192345], [455, -68, 100, 2.356194490192345], [456, -67, 100, -2.356194490192345], [457, -67, 100, 3.141592653589793], [459, -69, 100, 2.356194490192345], [460, -69, 100, 3.141592653589793], [461, -70, 100, 2.356194490192345], [462, -69, 100, -2.356194490192345], [463, -70, 100, 2.356194490192345], [464, -70, 100, 3.141592653589793], [465, -71, 100, 2.356194490192345], [466, -70, 100, -2.356194490192345], [468, -72, 100, 2.356194490192345], [469, -71, 100, -2.356194490192345], [471, -73, 100, 2.356194490192345], [472, -73, 100, 3.141592653589793], [475, -76, 100, 2.356194490192345], [476, -76, 100, 3.141592653589793], [478, -78, 100, 2.356194490192345], [479, -78, 100, 3.141592653589793], [480, -79, 100, 2.356194490192345], [487, -72, 100, -2.356194490192345], [488, -72, 100, 3.141592653589793], [489, -71, 100, -2.356194490192345], [490, -71, 100, 3.141592653589793], [492, -69, 100, -2.356194490192345], [493, -69, 100, 3.141592653589793], [494, -68, 100, -2.356194490192345], [495, -68, 100, 3.141592653589793], [496, -67, 100, -2.356194490192345], [497, -67, 100, 3.141592653589793], [499, -65, 100, -2.356194490192345], [500, -65, 100, 3.141592653589793], [501, -64, 100, -2.356194490192345], [502, -64, 100, 3.141592653589793], [503, -63, 100, -2.356194490192345], [504, -63, 100, 3.141592653589793], [506, -61, 100, -2.356194490192345], [507, -61, 100, 3.141592653589793], [508, -60, 100, -2.356194490192345], [509, -60, 100, 3.141592653589793], [510, -59, 100, -2.356194490192345], [511, -59, 100, 3.141592653589793], [513, -57, 100, -2.356194490192345], [514, -57, 100, 3.141592653589793], [515, -56, 100, -2.356194490192345], [516, -56, 100, 3.141592653589793], [517, -55, 100, -2.356194490192345], [518, -55, 100, 3.141592653589793], [520, -53, 100, -2.356194490192345], [521, -53, 100, 3.141592653589793], [522, -52, 100, -2.356194490192345], [523, -52, 100, 3.141592653589793], [524, -51, 100, -2.356194490192345], [525, -51, 100, 3.141592653589793], [527, -49, 100, -2.356194490192345], [528, -49, 100, 3.141592653589793], [529, -48, 100, -2.356194490192345], [530, -48, 100, 3.141592653589793], [532, -46, 100, -2.356194490192345], [533, -46, 100, 3.141592653589793], [534, -45, 100, -2.356194490192345], [535, -45, 100, 3.141592653589793], [536, -44, 100, -2.356194490192345], [537, -44, 100, 3.141592653589793], [539, -42, 100, -2.356194490192345], [540, -42, 100, 3.141592653589793], [541, -41, 100, -2.356194490192345], [542, -41, 100, 3.141592653589793], [543, -40, 100, -2.356194490192345], [544, -40, 100, 3.141592653589793], [546, -38, 100, -2.356194490192345], [547, -38, 100, 3.141592653589793], [548, -37, 100, -2.356194490192345], [549, -37, 100, 3.141592653589793], [550, -36, 100, -2.356194490192345], [551, -36, 100, 3.141592653589793], [553, -34, 100, -2.356194490192345], [554, -34, 100, 3.141592653589793], [555, -33, 100, -2.356194490192345], [556, -33, 100, 3.141592653589793], [557, -32, 100, -2.356194490192345], [558, -32, 100, 3.141592653589793], [559, -31, 100, -2.356194490192345], [559, -30, 100, -1.5707963267948966], [560, -29, 100, -2.356194490192345], [561, -29, 100, 3.141592653589793], [563, -27, 100, -2.356194490192345], [564, -28, 100, 2.356194490192345], [565, -28, 100, 3.141592653589793], [568, -25, 100, -2.356194490192345], [570, -25, 100, 3.141592653589793], [573, -22, 100, -2.356194490192345], [574, -23, 100, 2.356194490192345], [578, -19, 100, -2.356194490192345], [579, -20, 100, 2.356194490192345], [580, -19, 100, -2.356194490192345], [582, -19, 100, 3.141592653589793], [583, -18, 100, -2.356194490192345], [585, -18, 100, 3.141592653589793], [586, -17, 100, -2.356194490192345], [588, -17, 100, 3.141592653589793], [589, -16, 100, -2.356194490192345], [591, -16, 100, 3.141592653589793], [592, -15, 100, -2.356194490192345], [594, -15, 100, 3.141592653589793], [595, -14, 100, -2.356194490192345], [597, -14, 100, 3.141592653589793], [598, -13, 100, -2.356194490192345], [600, -13, 100, 3.141592653589793], [601, -12, 100, -2.356194490192345], [603, -12, 100, 3.141592653589793], [604, -13, 100, 2.356194490192345], [604, -55, 100, 1.5707963267948966], [603, -56, 100, 0.7853981633974483], [604, -57, 100, 2.356194490192345], [604, -444, 100, 1.5707963267948966], [603, -445, 100, 0.7853981633974483], [449, -445, 100, 0.0], [448, -444, 100, -0.7853981633974483], [447, -445, 100, 0.7853981633974483], [374, -445, 100, 0.0], [373, -444, 100, -0.7853981633974483], [372, -445, 100, 0.7853981633974483], [359, -445, 100, 0.0], [358, -444, 100, -0.7853981633974483], [357, -445, 100, 0.7853981633974483], [217, -445, 100, 0.0], [216, -444, 100, -0.7853981633974483], [215, -445, 100, 0.7853981633974483], [207, -445, 100, 0.0], [206, -444, 100, -0.7853981633974483], [205, -445, 100, 0.7853981633974483], [104, -445, 100, 0.0], [98, -439, 100, -0.7853981633974483], [98, -438, 100, -1.5707963267948966], [92, -432, 100, -0.7853981633974483], [92, -431, 100, -1.5707963267948966], [90, -429, 100, -0.7853981633974483], [90, -428, 100, -1.5707963267948966], [88, -426, 100, -0.7853981633974483], [88, -425, 100, -1.5707963267948966], [87, -424, 100, -0.7853981633974483], [87, -423, 100, -1.5707963267948966], [86, -422, 100, -0.7853981633974483], [86, -420, 100, -1.5707963267948966], [85, -419, 100, -0.7853981633974483], [85, -417, 100, -1.5707963267948966], [84, -416, 100, -0.7853981633974483], [84, -414, 100, -1.5707963267948966], [83, -413, 100, -0.7853981633974483], [83, -411, 100, -1.5707963267948966], [82, -410, 100, -0.7853981633974483], [82, -408, 100, -1.5707963267948966], [81, -407, 100, -0.7853981633974483], [81, -406, 100, -1.5707963267948966], [80, -405, 100, -0.7853981633974483], [80, -404, 100, -1.5707963267948966], [78, -402, 100, -0.7853981633974483], [78, -401, 100, -1.5707963267948966], [76, -399, 100, -0.7853981633974483], [76, -398, 100, -1.5707963267948966], [70, -392, 100, -0.7853981633974483], [70, -391, 100, -1.5707963267948966], [67, -388, 100, -0.7853981633974483], [65, -388, 100, 0.0], [64, -389, 100, 0.7853981633974483], [63, -389, 100, 0.0], [62, -390, 100, 0.7853981633974483], [61, -390, 100, 0.0], [60, -391, 100, 0.7853981633974483], [58, -391, 100, 0.0], [57, -392, 100, 0.7853981633974483], [55, -392, 100, 0.0], [54, -393, 100, 0.7853981633974483], [52, -393, 100, 0.0], [51, -394, 100, 0.7853981633974483], [50, -394, 100, 0.0], [49, -395, 100, 0.7853981633974483], [48, -395, 100, 0.0], [47, -396, 100, 0.7853981633974483], [46, -396, 100, 0.0], [45, -397, 100, 0.7853981633974483], [43, -397, 100, 0.0], [42, -398, 100, 0.7853981633974483], [40, -398, 100, 0.0], [39, -399, 100, 0.7853981633974483], [36, -399, 100, 0.0], [35, -400, 100, 0.7853981633974483], [23, -400, 100, 0.0], [22, -401, 100, 0.7853981633974483], [19, -401, 100, 0.0], [18, -402, 100, 0.7853981633974483], [16, -402, 100, 0.0], [15, -403, 100, 0.7853981633974483], [13, -403, 100, 0.0], [12, -404, 100, 0.7853981633974483], [11, -404, 100, 0.0], [10, -405, 100, 0.7853981633974483], [9, -405, 100, 0.0], [8, -406, 100, 0.7853981633974483], [7, -406, 100, 0.0], [6, -407, 100, 0.7853981633974483], [5, -407, 100, 0.0], [3, -409, 100, 0.7853981633974483], [2, -409, 100, 0.0], [-1, -412, 100, 0.7853981633974483], [-2, -412, 100, 0.0], [-5, -415, 100, 0.7853981633974483], [-6, -415, 100, 0.0], [-9, -418, 100, 0.7853981633974483], [-10, -418, 100, 0.0], [-14, -422, 100, 0.7853981633974483], [-15, -422, 100, 0.0], [-19, -426, 100, 0.7853981633974483], [-21, -426, 100, 0.0], [-25, -430, 100, 0.7853981633974483], [-26, -429, 100, -0.7853981633974483], [-29, -432, 100, 0.7853981633974483], [-31, -432, 100, 0.0], [-36, -437, 100, 0.7853981633974483], [-37, -436, 100, -0.7853981633974483], [-38, -437, 100, 0.7853981633974483], [-40, -437, 100, 0.0], [-45, -442, 100, 0.7853981633974483], [-46, -442, 100, 0.0], [-49, -445, 100, 0.7853981633974483], [-50, -444, 100, -0.7853981633974483], [-51, -445, 100, 0.7853981633974483], [-52, -444, 100, -0.7853981633974483], [-53, -445, 100, 0.7853981633974483], [-74, -445, 100, 0.0], [-75, -444, 100, -0.7853981633974483], [-76, -445, 100, 0.7853981633974483], [-88, -445, 100, 0.0], [-89, -444, 100, -0.7853981633974483], [-89, -442, 100, -1.5707963267948966], [-90, -441, 100, -0.7853981633974483], [-90, -437, 100, -1.5707963267948966], [-91, -436, 100, -0.7853981633974483], [-91, -433, 100, -1.5707963267948966], [-92, -432, 100, -0.7853981633974483], [-92, -429, 100, -1.5707963267948966], [-93, -428, 100, -0.7853981633974483], [-93, -424, 100, -1.5707963267948966], [-94, -423, 100, -0.7853981633974483], [-94, -420, 100, -1.5707963267948966], [-95, -419, 100, -0.7853981633974483], [-95, -415, 100, -1.5707963267948966], [-96, -414, 100, -0.7853981633974483], [-96, -411, 100, -1.5707963267948966], [-97, -410, 100, -0.7853981633974483], [-97, -406, 100, -1.5707963267948966], [-98, -405, 100, -0.7853981633974483], [-98, -400, 100, -1.5707963267948966], [-99, -399, 100, -0.7853981633974483], [-99, -394, 100, -1.5707963267948966], [-100, -393, 100, -0.7853981633974483], [-100, -384, 100, -1.5707963267948966], [-101, -383, 100, -0.7853981633974483], [-101, -357, 100, -1.5707963267948966], [-103, -355, 100, -0.7853981633974483], [-226, -355, 100, 0.0], [-227, -354, 100, -0.7853981633974483], [-230, -354, 100, 0.0], [-231, -353, 100, -0.7853981633974483], [-233, -353, 100, 0.0], [-234, -352, 100, -0.7853981633974483], [-235, -352, 100, 0.0], [-236, -351, 100, -0.7853981633974483], [-237, -351, 100, 0.0], [-239, -349, 100, -0.7853981633974483], [-241, -349, 100, 0.0], [-242, -348, 100, -0.7853981633974483], [-244, -348, 100, 0.0], [-245, -347, 100, -0.7853981633974483], [-247, -347, 100, 0.0], [-248, -346, 100, -0.7853981633974483], [-249, -346, 100, 0.0], [-250, -345, 100, -0.7853981633974483], [-251, -345, 100, 0.0], [-252, -344, 100, -0.7853981633974483], [-253, -344, 100, 0.0], [-254, -343, 100, -0.7853981633974483], [-255, -343, 100, 0.0], [-257, -341, 100, -0.7853981633974483], [-258, -341, 100, 0.0], [-260, -339, 100, -0.7853981633974483], [-264, -339, 100, 0.0], [-265, -338, 100, -0.7853981633974483], [-270, -338, 100, 0.0], [-271, -337, 100, -0.7853981633974483], [-276, -337, 100, 0.0], [-277, -336, 100, -0.7853981633974483], [-282, -336, 100, 0.0], [-283, -335, 100, -0.7853981633974483], [-288, -335, 100, 0.0], [-289, -334, 100, -0.7853981633974483], [-294, -334, 100, 0.0], [-295, -333, 100, -0.7853981633974483], [-300, -333, 100, 0.0], [-301, -332, 100, -0.7853981633974483], [-304, -332, 100, 0.0], [-307, -335, 100, 0.7853981633974483], [-310, -332, 100, -0.7853981633974483], [-310, -331, 100, -1.5707963267948966], [-316, -325, 100, -0.7853981633974483], [-315, -324, 100, -2.356194490192345], [-316, -323, 100, -0.7853981633974483], [-316, -304, 100, -1.5707963267948966], [-315, -303, 100, -2.356194490192345], [-314, -303, 100, 3.141592653589793], [-280, -269, 100, -2.356194490192345], [-279, -269, 100, 3.141592653589793], [-273, -263, 100, -2.356194490192345], [-272, -263, 100, 3.141592653589793], [-270, -261, 100, -2.356194490192345], [-269, -261, 100, 3.141592653589793], [-266, -258, 100, -2.356194490192345], [-265, -258, 100, 3.141592653589793], [-263, -256, 100, -2.356194490192345], [-262, -256, 100, 3.141592653589793], [-260, -254, 100, -2.356194490192345], [-259, -254, 100, 3.141592653589793], [-257, -252, 100, -2.356194490192345], [-256, -252, 100, 3.141592653589793], [-253, -249, 100, -2.356194490192345], [-251, -249, 100, 3.141592653589793], [-250, -248, 100, -2.356194490192345], [-248, -248, 100, 3.141592653589793], [-247, -247, 100, -2.356194490192345], [-245, -247, 100, 3.141592653589793], [-244, -246, 100, -2.356194490192345], [-244, -245, 100, -1.5707963267948966], [-243, -244, 100, -2.356194490192345], [-243, -243, 100, -1.5707963267948966], [-242, -242, 100, -2.356194490192345], [-242, -241, 100, -1.5707963267948966], [-230, -229, 100, -2.356194490192345], [-229, -229, 100, 3.141592653589793], [-228, -228, 100, -2.356194490192345], [-227, -228, 100, 3.141592653589793], [-226, -227, 100, -2.356194490192345], [-225, -227, 100, 3.141592653589793], [-224, -226, 100, -2.356194490192345], [-223, -226, 100, 3.141592653589793], [-222, -225, 100, -2.356194490192345], [-221, -225, 100, 3.141592653589793], [-220, -224, 100, -2.356194490192345], [-219, -224, 100, 3.141592653589793], [-218, -223, 100, -2.356194490192345], [-216, -223, 100, 3.141592653589793], [-215, -222, 100, -2.356194490192345], [-213, -222, 100, 3.141592653589793], [-212, -221, 100, -2.356194490192345], [-210, -221, 100, 3.141592653589793], [-209, -220, 100, -2.356194490192345], [-208, -220, 100, 3.141592653589793], [-207, -219, 100, -2.356194490192345], [-206, -219, 100, 3.141592653589793], [-205, -218, 100, -2.356194490192345], [-204, -218, 100, 3.141592653589793], [-202, -216, 100, -2.356194490192345], [-201, -216, 100, 3.141592653589793], [-200, -215, 100, -2.356194490192345], [-199, -215, 100, 3.141592653589793], [-197, -213, 100, -2.356194490192345], [-196, -213, 100, 3.141592653589793], [-192, -209, 100, -2.356194490192345], [-220, -181, 100, -0.7853981633974483], [-220, -180, 100, -1.5707963267948966], [-225, -175, 100, -0.7853981633974483], [-225, -174, 100, -1.5707963267948966], [-226, -173, 100, -0.7853981633974483], [-226, -168, 100, -1.5707963267948966], [-227, -167, 100, -0.7853981633974483], [-227, -166, 100, -1.5707963267948966], [-228, -165, 100, -0.7853981633974483], [-233, -165, 100, 0.0], [-236, -162, 100, -0.7853981633974483], [-236, -158, 100, -1.5707963267948966], [-239, -155, 100, -0.7853981633974483], [-243, -155, 100, 0.0], [-244, -154, 100, -0.7853981633974483], [-245, -154, 100, 0.0], [-246, -153, 100, -0.7853981633974483], [-246, -148, 100, -1.5707963267948966], [-249, -145, 100, -0.7853981633974483], [-254, -145, 100, 0.0], [-255, -144, 100, -0.7853981633974483], [-255, -143, 100, -1.5707963267948966], [-256, -142, 100, -0.7853981633974483], [-256, -137, 100, -1.5707963267948966], [-258, -135, 100, -0.7853981633974483], [-263, -135, 100, 0.0], [-264, -134, 100, -0.7853981633974483], [-266, -134, 100, 0.0], [-270, -130, 100, -0.7853981633974483], [-275, -130, 100, 0.0], [-276, -129, 100, -0.7853981633974483], [-278, -129, 100, 0.0], [-279, -128, 100, -0.7853981633974483], [-280, -128, 100, 0.0], [-281, -127, 100, -0.7853981633974483], [-282, -127, 100, 0.0], [-283, -126, 100, -0.7853981633974483], [-284, -126, 100, 0.0], [-285, -125, 100, -0.7853981633974483], [-286, -125, 100, 0.0], [-287, -124, 100, -0.7853981633974483], [-290, -124, 100, 0.0], [-291, -123, 100, -0.7853981633974483], [-293, -123, 100, 0.0], [-294, -122, 100, -0.7853981633974483], [-296, -122, 100, 0.0], [-297, -121, 100, -0.7853981633974483], [-299, -121, 100, 0.0], [-300, -120, 100, -0.7853981633974483], [-315, -120, 100, 0.0], [-316, -119, 100, -0.7853981633974483], [-316, -47, 100, -1.5707963267948966], [-314, -45, 100, -2.356194490192345], [-296, -45, 100, 3.141592653589793], [-295, -46, 100, 2.356194490192345], [-293, -44, 100, -2.356194490192345], [-290, -44, 100, 3.141592653589793], [-289, -43, 100, -2.356194490192345], [-286, -43, 100, 3.141592653589793], [-285, -42, 100, -2.356194490192345], [-282, -42, 100, 3.141592653589793], [-281, -41, 100, -2.356194490192345], [-279, -41, 100, 3.141592653589793], [-277, -39, 100, -2.356194490192345], [-276, -39, 100, 3.141592653589793], [-275, -38, 100, -2.356194490192345], [-274, -38, 100, 3.141592653589793], [-273, -37, 100, -2.356194490192345], [-271, -37, 100, 3.141592653589793], [-270, -36, 100, -2.356194490192345], [-267, -36, 100, 3.141592653589793], [-266, -35, 100, -2.356194490192345], [-256, -35, 100, 3.141592653589793], [-255, -34, 100, -2.356194490192345], [-252, -34, 100, 3.141592653589793], [-251, -33, 100, -2.356194490192345], [-249, -33, 100, 3.141592653589793], [-248, -32, 100, -2.356194490192345], [-247, -32, 100, 3.141592653589793], [-246, -31, 100, -2.356194490192345], [-245, -31, 100, 3.141592653589793], [-243, -29, 100, -2.356194490192345], [-241, -29, 100, 3.141592653589793], [-240, -28, 100, -2.356194490192345], [-237, -28, 100, 3.141592653589793], [-236, -27, 100, -2.356194490192345], [-233, -27, 100, 3.141592653589793], [-219, -13, 100, -2.356194490192345], [-219, -12, 100, -1.5707963267948966], [-217, -10, 100, -2.356194490192345], [-217, -9, 100, -1.5707963267948966], [-218, -8, 100, -0.7853981633974483], [-218, -5, 100, -1.5707963267948966], [-219, -4, 100, -0.7853981633974483], [-219, -1, 100, -1.5707963267948966], [-220, 0, 100, -0.7853981633974483], [-220, 2, 100, -1.5707963267948966], [-222, 4, 100, -0.7853981633974483], [-222, 5, 100, -1.5707963267948966], [-223, 6, 100, -0.7853981633974483], [-223, 7, 100, -1.5707963267948966], [-224, 8, 100, -0.7853981633974483], [-224, 10, 100, -1.5707963267948966], [-225, 11, 100, -0.7853981633974483], [-225, 14, 100, -1.5707963267948966], [-226, 15, 100, -0.7853981633974483], [-226, 16, 100, -1.5707963267948966], [-227, 17, 100, -0.7853981633974483], [-227, 18, 100, -1.5707963267948966], [-228, 19, 100, -0.7853981633974483], [-228, 20, 100, -1.5707963267948966], [-229, 21, 100, -0.7853981633974483], [-229, 22, 100, -1.5707963267948966], [-230, 23, 100, -0.7853981633974483], [-230, 25, 100, -1.5707963267948966], [-231, 26, 100, -0.7853981633974483], [-231, 30, 100, -1.5707963267948966], [-281, 80, 100, -0.7853981633974483], [-272, 89, 100, -2.356194490192345], [-272, 90, 100, -1.5707963267948966], [-267, 95, 100, -2.356194490192345], [-267, 97, 100, -1.5707963267948966], [-266, 98, 100, -2.356194490192345], [-266, 102, 100, -1.5707963267948966], [-263, 105, 100, -2.356194490192345], [-258, 105, 100, 3.141592653589793], [-256, 107, 100, -2.356194490192345], [-256, 113, 100, -1.5707963267948966], [-254, 115, 100, -2.356194490192345], [-249, 115, 100, 3.141592653589793], [-246, 118, 100, -2.356194490192345], [-246, 123, 100, -1.5707963267948966], [-245, 124, 100, -2.356194490192345], [-245, 125, 100, -1.5707963267948966], [-241, 129, 100, -2.356194490192345], [-241, 130, 100, -1.5707963267948966], [-236, 135, 100, -2.356194490192345], [-236, 163, 100, -1.5707963267948966], [-237, 164, 100, -0.7853981633974483], [-236, 165, 100, -2.356194490192345], [-236, 183, 100, -1.5707963267948966], [-237, 184, 100, -0.7853981633974483], [-236, 185, 100, -2.356194490192345], [-236, 190, 100, -1.5707963267948966], [-239, 193, 100, -0.7853981633974483], [-239, 194, 100, -1.5707963267948966], [-244, 199, 100, -0.7853981633974483], [-244, 200, 100, -1.5707963267948966], [-245, 201, 100, -0.7853981633974483], [-245, 202, 100, -1.5707963267948966], [-247, 204, 100, -0.7853981633974483], [-247, 205, 100, -1.5707963267948966], [-249, 207, 100, -0.7853981633974483], [-249, 208, 100, -1.5707963267948966], [-251, 210, 100, -0.7853981633974483], [-251, 212, 100, -1.5707963267948966], [-252, 213, 100, -0.7853981633974483], [-252, 215, 100, -1.5707963267948966], [-254, 217, 100, -0.7853981633974483], [-254, 218, 100, -1.5707963267948966], [-255, 219, 100, -0.7853981633974483], [-255, 220, 100, -1.5707963267948966], [-263, 228, 100, -0.7853981633974483], [-263, 229, 100, -1.5707963267948966], [-270, 236, 100, -0.7853981633974483], [-270, 237, 100, -1.5707963267948966], [-277, 244, 100, -0.7853981633974483], [-278, 244, 100, 0.0], [-279, 245, 100, -0.7853981633974483], [-280, 245, 100, 0.0], [-282, 247, 100, -0.7853981633974483], [-283, 247, 100, 0.0], [-284, 248, 100, -0.7853981633974483], [-285, 248, 100, 0.0], [-286, 249, 100, -0.7853981633974483], [-287, 249, 100, 0.0], [-288, 250, 100, -0.7853981633974483], [-289, 250, 100, 0.0], [-292, 253, 100, -0.7853981633974483], [-294, 253, 100, 0.0], [-295, 254, 100, -0.7853981633974483], [-296, 254, 100, 0.0], [-298, 256, 100, -0.7853981633974483], [-299, 256, 100, 0.0], [-300, 257, 100, -0.7853981633974483], [-301, 257, 100, 0.0], [-303, 259, 100, -0.7853981633974483], [-304, 259, 100, 0.0], [-306, 261, 100, -0.7853981633974483], [-307, 261, 100, 0.0], [-309, 263, 100, -0.7853981633974483], [-310, 263, 100, 0.0], [-312, 265, 100, -0.7853981633974483], [-313, 265, 100, 0.0], [-314, 266, 100, -0.7853981633974483], [-315, 266, 100, 0.0], [-316, 267, 100, -0.7853981633974483], [-316, 474, 100, -1.5707963267948966], [-315, 475, 100, -2.356194490192345], [-271, 475, 100, 3.141592653589793], [-270, 474, 100, 2.356194490192345], [-269, 475, 100, -2.356194490192345], [-256, 475, 100, 3.141592653589793], [-255, 474, 100, 2.356194490192345], [-254, 475, 100, -2.356194490192345], [-236, 475, 100, 3.141592653589793], [-235, 474, 100, 2.356194490192345], [-234, 475, 100, -2.356194490192345], [-216, 475, 100, 3.141592653589793], [-215, 474, 100, 2.356194490192345], [-214, 475, 100, -2.356194490192345], [-48, 475, 100, 3.141592653589793], [-47, 474, 100, 2.356194490192345], [-46, 475, 100, -2.356194490192345], [-28, 475, 100, 3.141592653589793], [-27, 474, 100, 2.356194490192345], [-26, 475, 100, -2.356194490192345], [-16, 475, 100, 3.141592653589793], [-15, 474, 100, 2.356194490192345], [-14, 475, 100, -2.356194490192345], [14, 475, 100, 3.141592653589793], [15, 474, 100, 2.356194490192345], [16, 475, 100, -2.356194490192345], [34, 475, 100, 3.141592653589793], [35, 474, 100, 2.356194490192345], [36, 475, 100, -2.356194490192345], [54, 475, 100, 3.141592653589793], [55, 474, 100, 2.356194490192345], [56, 475, 100, -2.356194490192345], [182, 475, 100, 3.141592653589793], [183, 474, 100, 2.356194490192345], [184, 475, 100, -2.356194490192345], [202, 475, 100, 3.141592653589793], [203, 474, 100, 2.356194490192345], [204, 475, 100, -2.356194490192345], [222, 475, 100, 3.141592653589793], [223, 474, 100, 2.356194490192345], [224, 475, 100, -2.356194490192345], [242, 475, 100, 3.141592653589793], [243, 474, 100, 2.356194490192345], [244, 475, 100, -2.356194490192345], [450, 475, 100, 3.141592653589793], [451, 474, 100, 2.356194490192345], [452, 475, 100, -2.356194490192345], [603, 475, 100, 3.141592653589793], [604, 474, 100, 2.356194490192345], [604, 401, 100, 1.5707963267948966], [603, 400, 100, 0.7853981633974483], [604, 399, 100, 2.356194490192345], [604, 22, 100, 1.5707963267948966], [603, 21, 100, 0.7853981633974483], [604, 20, 100, 2.356194490192345], [604, 15, 100, 1.5707963267948966], [602, 13, 100, 0.7853981633974483], [600, 15, 100, -0.7853981633974483], [601, 16, 100, -2.356194490192345], [599, 18, 100, -0.7853981633974483], [598, 17, 100, 0.7853981633974483], [596, 19, 100, -0.7853981633974483], [597, 20, 100, -2.356194490192345], [595, 22, 100, -0.7853981633974483], [594, 21, 100, 0.7853981633974483], [592, 23, 100, -0.7853981633974483], [593, 24, 100, -2.356194490192345], [591, 26, 100, -0.7853981633974483], [590, 25, 100, 0.7853981633974483], [588, 27, 100, -0.7853981633974483], [589, 28, 100, -2.356194490192345], [587, 30, 100, -0.7853981633974483], [586, 29, 100, 0.7853981633974483], [584, 31, 100, -0.7853981633974483], [585, 32, 100, -2.356194490192345], [583, 34, 100, -0.7853981633974483], [582, 33, 100, 0.7853981633974483], [580, 35, 100, -0.7853981633974483], [581, 36, 100, -2.356194490192345], [577, 40, 100, -0.7853981633974483], [578, 41, 100, -2.356194490192345], [576, 43, 100, -0.7853981633974483], [574, 43, 100, 0.0], [573, 42, 100, 0.7853981633974483], [572, 42, 100, 0.0], [571, 43, 100, -0.7853981633974483], [570, 43, 100, 0.0], [569, 44, 100, -0.7853981633974483], [568, 44, 100, 0.0], [567, 43, 100, 0.7853981633974483], [565, 43, 100, 0.0], [564, 44, 100, -0.7853981633974483], [563, 44, 100, 0.0], [562, 45, 100, -0.7853981633974483], [561, 44, 100, 0.7853981633974483], [560, 45, 100, -0.7853981633974483], [559, 45, 100, 0.0], [558, 46, 100, -0.7853981633974483], [557, 45, 100, 0.7853981633974483], [556, 45, 100, 0.0], [554, 47, 100, -0.7853981633974483], [553, 47, 100, 0.0], [552, 46, 100, 0.7853981633974483], [554, 44, 100, 2.356194490192345], [552, 42, 100, 0.7853981633974483], [551, 42, 100, 0.0], [550, 43, 100, -0.7853981633974483], [549, 43, 100, 0.0], [548, 44, 100, -0.7853981633974483], [550, 46, 100, -2.356194490192345], [548, 48, 100, -0.7853981633974483], [545, 48, 100, 0.0], [544, 49, 100, -0.7853981633974483], [542, 49, 100, 0.0], [541, 48, 100, 0.7853981633974483], [539, 50, 100, -0.7853981633974483], [538, 50, 100, 0.0], [537, 49, 100, 0.7853981633974483], [536, 50, 100, -0.7853981633974483], [535, 50, 100, 0.0], [534, 51, 100, -0.7853981633974483], [533, 50, 100, 0.7853981633974483], [532, 50, 100, 0.0], [531, 51, 100, -0.7853981633974483], [530, 50, 100, 0.7853981633974483], [529, 51, 100, -0.7853981633974483], [528, 51, 100, 0.0], [527, 52, 100, -0.7853981633974483], [525, 50, 100, 0.7853981633974483], [522, 53, 100, -0.7853981633974483], [520, 53, 100, 0.0], [519, 54, 100, -0.7853981633974483], [516, 54, 100, 0.0], [515, 55, 100, -0.7853981633974483], [512, 52, 100, 0.7853981633974483], [511, 52, 100, 0.0], [510, 53, 100, -0.7853981633974483], [509, 53, 100, 0.0], [505, 57, 100, -0.7853981633974483], [504, 56, 100, 0.7853981633974483], [503, 57, 100, -0.7853981633974483], [502, 56, 100, 0.7853981633974483], [501, 56, 100, 0.0], [498, 59, 100, -0.7853981633974483], [495, 59, 100, 0.0], [494, 58, 100, 0.7853981633974483], [493, 58, 100, 0.0], [490, 61, 100, -0.7853981633974483], [487, 61, 100, 0.0], [486, 62, 100, -0.7853981633974483], [483, 62, 100, 0.0], [482, 63, 100, -0.7853981633974483], [479, 63, 100, 0.0], [478, 64, 100, -0.7853981633974483], [475, 64, 100, 0.0], [474, 65, 100, -0.7853981633974483], [471, 65, 100, 0.0], [470, 66, 100, -0.7853981633974483], [467, 66, 100, 0.0], [466, 67, 100, -0.7853981633974483], [463, 67, 100, 0.0], [462, 68, 100, -0.7853981633974483], [459, 68, 100, 0.0], [458, 69, 100, -0.7853981633974483], [455, 69, 100, 0.0], [454, 70, 100, -0.7853981633974483], [452, 70, 100, 0.0], [451, 71, 100, -0.7853981633974483], [448, 71, 100, 0.0], [447, 72, 100, -0.7853981633974483], [444, 72, 100, 0.0], [443, 73, 100, -0.7853981633974483], [440, 73, 100, 0.0], [439, 74, 100, -0.7853981633974483], [436, 74, 100, 0.0], [435, 75, 100, -0.7853981633974483], [434, 75, 100, 0.0], [433, 76, 100, -0.7853981633974483], [432, 75, 100, 0.7853981633974483], [384, 75, 100, 0.0], [383, 76, 100, -0.7853981633974483], [380, 76, 100, 0.0], [379, 77, 100, -0.7853981633974483], [377, 77, 100, 0.0], [376, 78, 100, -0.7853981633974483], [375, 78, 100, 0.0], [374, 79, 100, -0.7853981633974483], [373, 79, 100, 0.0], [372, 80, 100, -0.7853981633974483], [331, 80, 100, 0.0], [330, 79, 100, 0.7853981633974483], [329, 80, 100, -0.7853981633974483], [328, 80, 100, 0.0], [327, 81, 100, -0.7853981633974483], [323, 81, 100, 0.0], [322, 82, 100, -0.7853981633974483], [318, 82, 100, 0.0], [317, 83, 100, -0.7853981633974483], [313, 83, 100, 0.0], [312, 84, 100, -0.7853981633974483], [308, 84, 100, 0.0], [307, 85, 100, -0.7853981633974483], [303, 85, 100, 0.0], [302, 86, 100, -0.7853981633974483], [298, 86, 100, 0.0], [297, 87, 100, -0.7853981633974483], [295, 87, 100, 0.0], [294, 88, 100, -0.7853981633974483], [294, 89, 100, -1.5707963267948966], [292, 91, 100, -0.7853981633974483], [292, 92, 100, -1.5707963267948966], [291, 93, 100, -0.7853981633974483], [291, 94, 100, -1.5707963267948966], [290, 95, 100, -0.7853981633974483], [290, 96, 100, -1.5707963267948966], [289, 97, 100, -0.7853981633974483], [289, 98, 100, -1.5707963267948966], [287, 100, 100, -0.7853981633974483], [287, 101, 100, -1.5707963267948966], [286, 102, 100, -0.7853981633974483], [286, 103, 100, -1.5707963267948966], [285, 104, 100, -0.7853981633974483], [285, 105, 100, -1.5707963267948966], [283, 107, 100, -0.7853981633974483], [283, 108, 100, -1.5707963267948966], [282, 109, 100, -0.7853981633974483], [282, 110, 100, -1.5707963267948966], [280, 112, 100, -0.7853981633974483], [280, 113, 100, -1.5707963267948966], [278, 115, 100, -0.7853981633974483], [278, 116, 100, -1.5707963267948966], [275, 119, 100, -0.7853981633974483], [275, 120, 100, -1.5707963267948966], [272, 123, 100, -0.7853981633974483], [272, 124, 100, -1.5707963267948966], [268, 128, 100, -0.7853981633974483], [268, 129, 100, -1.5707963267948966], [264, 133, 100, -0.7853981633974483], [264, 134, 100, -1.5707963267948966], [259, 139, 100, -0.7853981633974483], [259, 140, 100, -1.5707963267948966], [254, 145, 100, -0.7853981633974483], [254, 146, 100, -1.5707963267948966], [250, 150, 100, -0.7853981633974483], [250, 151, 100, -1.5707963267948966], [245, 156, 100, -0.7853981633974483], [245, 157, 100, -1.5707963267948966], [242, 160, 100, -0.7853981633974483], [242, 161, 100, -1.5707963267948966], [238, 165, 100, -0.7853981633974483], [238, 166, 100, -1.5707963267948966], [235, 169, 100, -0.7853981633974483], [235, 170, 100, -1.5707963267948966], [232, 173, 100, -0.7853981633974483], [229, 173, 100, 0.0], [228, 172, 100, 0.7853981633974483], [226, 172, 100, 0.0], [225, 171, 100, 0.7853981633974483], [224, 171, 100, 0.0], [223, 170, 100, 0.7853981633974483], [221, 170, 100, 0.0], [220, 169, 100, 0.7853981633974483], [218, 169, 100, 0.0], [217, 168, 100, 0.7853981633974483], [215, 168, 100, 0.0], [214, 167, 100, 0.7853981633974483], [212, 167, 100, 0.0], [210, 165, 100, 0.7853981633974483], [209, 166, 100, -0.7853981633974483], [207, 164, 100, 0.7853981633974483], [206, 165, 100, -0.7853981633974483], [105, 165, 100, 0.0], [104, 166, 100, -0.7853981633974483], [94, 166, 100, 0.0], [93, 167, 100, -0.7853981633974483], [87, 167, 100, 0.0], [86, 168, 100, -0.7853981633974483], [81, 168, 100, 0.0], [80, 169, 100, -0.7853981633974483], [76, 169, 100, 0.0], [75, 170, 100, -0.7853981633974483], [71, 170, 100, 0.0], [69, 172, 100, -0.7853981633974483], [69, 173, 100, -1.5707963267948966], [67, 175, 100, -0.7853981633974483], [67, 176, 100, -1.5707963267948966], [66, 177, 100, -0.7853981633974483], [66, 178, 100, -1.5707963267948966], [64, 180, 100, -0.7853981633974483], [64, 181, 100, -1.5707963267948966], [63, 182, 100, -0.7853981633974483], [63, 183, 100, -1.5707963267948966], [62, 184, 100, -0.7853981633974483], [62, 185, 100, -1.5707963267948966], [61, 186, 100, -0.7853981633974483], [61, 187, 100, -1.5707963267948966], [60, 188, 100, -0.7853981633974483], [60, 189, 100, -1.5707963267948966], [59, 190, 100, -0.7853981633974483], [59, 191, 100, -1.5707963267948966], [58, 192, 100, -0.7853981633974483], [58, 193, 100, -1.5707963267948966], [57, 194, 100, -0.7853981633974483], [57, 195, 100, -1.5707963267948966], [56, 196, 100, -0.7853981633974483], [56, 197, 100, -1.5707963267948966], [55, 198, 100, -0.7853981633974483], [55, 199, 100, -1.5707963267948966], [54, 200, 100, -0.7853981633974483], [54, 201, 100, -1.5707963267948966], [53, 202, 100, -0.7853981633974483], [53, 203, 100, -1.5707963267948966], [52, 204, 100, -0.7853981633974483], [52, 205, 100, -1.5707963267948966], [51, 206, 100, -0.7853981633974483], [51, 207, 100, -1.5707963267948966], [50, 208, 100, -0.7853981633974483], [50, 209, 100, -1.5707963267948966], [48, 211, 100, -0.7853981633974483], [48, 212, 100, -1.5707963267948966], [47, 213, 100, -0.7853981633974483], [47, 214, 100, -1.5707963267948966], [45, 216, 100, -0.7853981633974483], [45, 217, 100, -1.5707963267948966], [44, 218, 100, -0.7853981633974483], [44, 219, 100, -1.5707963267948966], [42, 221, 100, -0.7853981633974483], [42, 223, 100, -1.5707963267948966], [38, 227, 100, -0.7853981633974483], [38, 228, 100, -1.5707963267948966], [35, 231, 100, -0.7853981633974483], [35, 232, 100, -1.5707963267948966], [33, 234, 100, -0.7853981633974483], [33, 235, 100, -1.5707963267948966], [29, 239, 100, -0.7853981633974483], [29, 240, 100, -1.5707963267948966], [27, 242, 100, -0.7853981633974483], [27, 243, 100, -1.5707963267948966], [25, 245, 100, -0.7853981633974483], [25, 246, 100, -1.5707963267948966], [23, 248, 100, -0.7853981633974483], [23, 249, 100, -1.5707963267948966], [19, 253, 100, -0.7853981633974483], [19, 254, 100, -1.5707963267948966], [16, 257, 100, -0.7853981633974483], [16, 258, 100, -1.5707963267948966], [12, 262, 100, -0.7853981633974483], [12, 263, 100, -1.5707963267948966], [10, 265, 100, -0.7853981633974483], [-6, 265, 100, 0.0], [-7, 266, 100, -0.7853981633974483], [-8, 265, 100, 0.7853981633974483], [-26, 265, 100, 0.0], [-27, 266, 100, -0.7853981633974483], [-28, 265, 100, 0.7853981633974483], [-96, 265, 100, 0.0], [-156, 205, 100, 0.7853981633974483], [-156, 204, 100, 1.5707963267948966], [-157, 203, 100, 0.7853981633974483], [-157, 201, 100, 1.5707963267948966], [-158, 200, 100, 0.7853981633974483], [-158, 198, 100, 1.5707963267948966], [-159, 197, 100, 0.7853981633974483], [-159, 196, 100, 1.5707963267948966], [-160, 195, 100, 0.7853981633974483], [-160, 194, 100, 1.5707963267948966], [-162, 192, 100, 0.7853981633974483], [-162, 191, 100, 1.5707963267948966], [-164, 189, 100, 0.7853981633974483], [-164, 188, 100, 1.5707963267948966], [-167, 185, 100, 0.7853981633974483], [-164, 182, 100, 2.356194490192345], [-164, 181, 100, 1.5707963267948966], [-162, 179, 100, 2.356194490192345], [-162, 178, 100, 1.5707963267948966], [-160, 176, 100, 2.356194490192345], [-160, 175, 100, 1.5707963267948966], [-159, 174, 100, 2.356194490192345], [-159, 173, 100, 1.5707963267948966], [-158, 172, 100, 2.356194490192345], [-158, 170, 100, 1.5707963267948966], [-157, 169, 100, 2.356194490192345], [-157, 166, 100, 1.5707963267948966], [-156, 165, 100, 2.356194490192345], [-156, 164, 100, 1.5707963267948966], [-155, 163, 100, 2.356194490192345], [-155, 162, 100, 1.5707963267948966], [-154, 161, 100, 2.356194490192345], [-154, 160, 100, 1.5707963267948966], [-153, 159, 100, 2.356194490192345], [-153, 158, 100, 1.5707963267948966], [-152, 157, 100, 2.356194490192345], [-152, 156, 100, 1.5707963267948966], [-150, 154, 100, 2.356194490192345], [-150, 153, 100, 1.5707963267948966], [-148, 151, 100, 2.356194490192345], [-147, 151, 100, 3.141592653589793], [-145, 149, 100, 2.356194490192345], [-144, 149, 100, 3.141592653589793], [-142, 147, 100, 2.356194490192345], [-142, 146, 100, 1.5707963267948966], [-140, 144, 100, 2.356194490192345], [-140, 143, 100, 1.5707963267948966], [-138, 141, 100, 2.356194490192345], [-137, 141, 100, 3.141592653589793], [-135, 139, 100, 2.356194490192345], [-134, 139, 100, 3.141592653589793], [-132, 137, 100, 2.356194490192345], [-132, 136, 100, 1.5707963267948966], [-130, 134, 100, 2.356194490192345], [-130, 133, 100, 1.5707963267948966], [-128, 131, 100, 2.356194490192345], [-127, 131, 100, 3.141592653589793], [-125, 129, 100, 2.356194490192345], [-124, 129, 100, 3.141592653589793], [-123, 128, 100, 2.356194490192345], [-122, 128, 100, 3.141592653589793], [-121, 127, 100, 2.356194490192345], [-120, 127, 100, 3.141592653589793], [-119, 126, 100, 2.356194490192345], [-118, 126, 100, 3.141592653589793], [-117, 125, 100, 2.356194490192345], [-116, 125, 100, 3.141592653589793], [-115, 124, 100, 2.356194490192345], [-112, 124, 100, 3.141592653589793], [-111, 123, 100, 2.356194490192345], [-109, 123, 100, 3.141592653589793], [-108, 122, 100, 2.356194490192345], [-107, 122, 100, 3.141592653589793], [-106, 121, 100, 2.356194490192345], [-105, 121, 100, 3.141592653589793], [-103, 119, 100, 2.356194490192345], [-102, 119, 100, 3.141592653589793], [-100, 117, 100, 2.356194490192345], [-99, 117, 100, 3.141592653589793], [-91, 109, 100, 2.356194490192345], [-90, 109, 100, 3.141592653589793], [-83, 102, 100, 2.356194490192345], [-82, 102, 100, 3.141592653589793], [-79, 99, 100, 2.356194490192345], [-78, 99, 100, 3.141592653589793], [-75, 96, 100, 2.356194490192345], [-111, 60, 100, 0.7853981633974483], [-111, 49, 100, 1.5707963267948966], [-112, 48, 100, 0.7853981633974483], [-112, 46, 100, 1.5707963267948966], [-113, 45, 100, 0.7853981633974483], [-113, 43, 100, 1.5707963267948966], [-114, 42, 100, 0.7853981633974483], [-114, 40, 100, 1.5707963267948966], [-115, 39, 100, 0.7853981633974483], [-115, 36, 100, 1.5707963267948966], [-116, 35, 100, 0.7853981633974483]]